## Análise Exploratória dos Dados Brutos

## Hemoprod Alagoas

In [1]:
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)


In [2]:
import pandas as pd
import os
import numpy as np

# --- 1. Defina os caminhos para seus arquivos ---
# Ajuste os caminhos conforme a estrutura do seu projeto no notebook
dados_brutos_path = 'dados_brutos'
dicionario_path = 'dicionario_colunas_269.xlsx'
arquivo_dados_path = os.path.join(dados_brutos_path, 'Hemoprod_AL.xlsx')
nome_planilha = 'HEMOPROD - ALAGOAS'

# --- 2. Carregue os dados e o dicionário ---
try:
    # Carrega o arquivo de dados
    hemoprod_al = pd.read_excel(arquivo_dados_path, sheet_name=nome_planilha)
    print("Arquivo de dados carregado com sucesso.")
    print(f"Número de colunas original: {len(hemoprod_al.columns)}")

    # Carrega o arquivo de dicionário
    dicionario = pd.read_excel(dicionario_path)
    print("Arquivo de dicionário carregado com sucesso.")

    # --- 3. Limpeza Inicial dos Nomes das Colunas (ADICIONADO) ---
    # Mapeia as colunas, limpando espaços em branco no início e fim
    # e substituindo o caractere \xa0 (Non-breaking space) por um espaço normal.
    mapa_limpeza = {
        col: col.strip().replace('\xa0', ' ') 
        for col in hemoprod_al.columns
    }

    # Aplica a renomeação para limpar os nomes
    hemoprod_al = hemoprod_al.rename(columns=mapa_limpeza)
    print("Nomes das colunas do DataFrame limpos e padronizados (strip/\\xa0).")

    # --- 4. Crie o dicionário de mapeamento ---
    # Cria um dicionário no formato {'nome_original': 'nome_sql'} para uso no .rename()
    # NOTA: O 'nome_original' no dicionário TAMBÉM deve estar limpo para combinar.
    # Se o dicionário não estiver limpo, adicione a mesma limpeza aqui:
    dicionario['nome_original'] = dicionario['nome_original'].astype(str).str.strip().str.replace('\xa0', ' ')
    
    mapa_renomeacao = pd.Series(dicionario['nome_sql'].values, index=dicionario['nome_original']).to_dict()
    
    # Lista dos nomes de coluna no DataFrame atual APÓS a limpeza inicial
    colunas_atuais = set(hemoprod_al.columns)
    
    # Lista dos nomes originais de coluna no dicionário APÓS a limpeza (se aplicada)
    colunas_originais_dicionario = set(dicionario['nome_original'].tolist())
    
    # Lista dos nomes SQL (os desejados) no dicionário
    colunas_sql_desejadas = set(dicionario['nome_sql'].tolist())
    
    # --- 5. Renomeie as colunas com base no mapeamento (nome_original -> nome_sql) ---
    print("\n--- Processo de Renomeação ---")
    hemoprod_al.rename(columns=mapa_renomeacao, inplace=True)
    print("Colunas renomeadas com sucesso (apenas as que existiam no dicionário foram modificadas).")


   # --- 4. Inferir Tipos e Criar Mapeamento de Tipos ---
    
    # --- Lógica de Inferência customizada para 'Int64' ---
    tipos_inferidos = {}
    for col in hemoprod_al.columns:
        
        # 4.1. Tenta converter a coluna para o tipo que melhor representa seus dados (incluindo Int64/string/datetime)
        # O errors='ignore' é crucial para não falhar se a coluna não puder ser convertida
        coluna_convertida = pd.to_numeric(hemoprod_al[col], errors='coerce')
        
        # Se a conversão for bem-sucedida (não é totalmente NaN, nem totalmente string)
        if not coluna_convertida.isna().all() and coluna_convertida.dtype.kind in 'fi': # 'f' para float, 'i' para int
            
            # Se a coluna parecer um número, tentamos forçar para Int64
            # O .astype('Int64') usa o tipo inteiro que suporta NaN
            try:
                # Se for possível converter para Int64, use 'Int64'
                hemoprod_al[col] = hemoprod_al[col].astype('Int64')
                tipos_inferidos[col] = 'Int64'
            except Exception:
                # Se for numérico mas não puder ser Int64 (ex: float com muitas casas decimais), use 'float64'
                tipos_inferidos[col] = 'float64'
        
        # Verifica se é data/hora
        elif pd.api.types.is_datetime64_any_dtype(hemoprod_al[col]):
             tipos_inferidos[col] = 'datetime64[ns]'
             
        # Caso contrário, assume-se que é um texto/string
        else:
            tipos_inferidos[col] = 'object' # O padrão para string no pandas

    
    print("\nTipos de dados inferidos (amostra):")
    for i, (col, dtype) in enumerate(tipos_inferidos.items()):
        if i < 5:
            print(f"  {col}: {dtype}")
        if i == 5:
            print("  ...")
    
    # --- 5. Atualizar o DataFrame Dicionário ---
    
    # 5.1. Cria a coluna 'tipo_dados' no dicionário e preenche com os tipos inferidos
    dicionario['tipo_dados'] = dicionario['nome_sql'].map(tipos_inferidos)
    
    # 5.2. Trata colunas não encontradas no DataFrame de dados
    dicionario['tipo_dados'] = dicionario['tipo_dados'].fillna('object')
    
    print("\n--- Dicionário Atualizado ---")
    print("Coluna 'tipo_dados' criada com sucesso, com numéricos definidos como 'Int64' ou 'float64'.")
    
    # --- 6. Salvar o Dicionário Atualizado ---

    # Sugestão de novo caminho para salvar
    novo_dicionario_path = 'dicionario_colunas_269_COM_TIPOS_V2.xlsx'
    
    dicionario.to_excel(novo_dicionario_path, index=False)
    
    print(f"\n✅ Dicionário salvo com a nova coluna 'tipo_dados' em: {novo_dicionario_path}")
    print("\nPrimeiras linhas do dicionário atualizado:")
    display(dicionario.head())

    # --- 6. Análise de Colunas (Qualidade dos Dados) ---

    # 6.1. Colunas que não puderam ser renomeadas (existem no DF, mas não no 'nome_original' do dicionário)
    # Aqui usamos as colunas atuais ANTES da renomeação para ver o que sobrou.
    colunas_nao_mapeadas = [
        col for col in colunas_atuais 
        if col not in colunas_originais_dicionario
    ]

    print("-" * 30)
    print("Análise de Colunas do DataFrame (hemoprod_al):")
    print(f"Número de colunas não mapeadas: {len(colunas_nao_mapeadas)}")
    print(f"Colunas não mapeadas (manterão nome original): {colunas_nao_mapeadas}")
    
    # 6.2. Análise de Colunas Faltantes/A Mais (Comparação com 'nome_sql' desejado)
    colunas_apos_renomeacao = set(hemoprod_al.columns)
    
    colunas_faltantes = list(colunas_sql_desejadas - colunas_apos_renomeacao)
    colunas_a_mais = list(colunas_apos_renomeacao - colunas_sql_desejadas)

    print("-" * 30)
    print("Análise de Colunas (Comparação com a lista SQL DESEJADA):")
    print(f"Número de colunas FALTANTES: {len(colunas_faltantes)}")
    print(f"Colunas FALTANTES (deveriam estar, mas não estão): {colunas_faltantes}")
    print("-" * 30)
    print(f"Número de colunas A MAIS: {len(colunas_a_mais)}")
    print(f"Colunas A MAIS (estão no DF, mas não na lista SQL desejada): {colunas_a_mais}")
    print("-" * 30)

    # --- 7. Verifique o resultado ---
    print("\nInformações do DataFrame com as novas colunas:")
    hemoprod_al.info()
    
    print("\nAs 5 primeiras linhas com as novas colunas:")
    display(hemoprod_al.head())

except FileNotFoundError as e:
    print(f"\nErro de arquivo não encontrado: {e}")
except KeyError as e:
    print(f"\nErro de coluna não encontrada: {e}. Verifique se as colunas 'nome_original' e 'nome_sql' existem no seu arquivo de dicionário.")
except Exception as e:
    print(f"\nOcorreu um erro inesperado: {e}")

Arquivo de dados carregado com sucesso.
Número de colunas original: 269
Arquivo de dicionário carregado com sucesso.
Nomes das colunas do DataFrame limpos e padronizados (strip/\xa0).

--- Processo de Renomeação ---
Colunas renomeadas com sucesso (apenas as que existiam no dicionário foram modificadas).

Tipos de dados inferidos (amostra):
  id: Int64
  data_envio: object
  ultima_pagina: Int64
  idioma_inicial: object
  semente: Int64
  ...

--- Dicionário Atualizado ---
Coluna 'tipo_dados' criada com sucesso, com numéricos definidos como 'Int64' ou 'float64'.

✅ Dicionário salvo com a nova coluna 'tipo_dados' em: dicionario_colunas_269_COM_TIPOS_V2.xlsx

Primeiras linhas do dicionário atualizado:


nome_original        nome_sql  \
0  ID da resposta              id   
1   Data de envio      data_envio   
2   Última página   ultima_pagina   
3  Idioma inicial  idioma_inicial   
4         Semente         semente   

                                          comentario tipo_dados  
0  Identificador único e chave primária da submis...      Int64  
1   Data e hora exatas do envio final do formulário.     object  
2  Título da última página do formulário acessada...      Int64  
3  Idioma selecionado no início do preenchimento ...     object  
4  Valor interno de semente/aleatorização (uso té...      Int64

------------------------------
Análise de Colunas do DataFrame (hemoprod_al):
Número de colunas não mapeadas: 0
Colunas não mapeadas (manterão nome original): []
------------------------------
Análise de Colunas (Comparação com a lista SQL DESEJADA):
Número de colunas FALTANTES: 0
Colunas FALTANTES (deveriam estar, mas não estão): []
------------------------------
Número de colunas A MAIS: 0
Colunas A MAIS (estão no DF, mas não na lista SQL desejada): []
------------------------------

Informações do DataFrame com as novas colunas:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 315 entries, 0 to 314
Columns: 269 entries, id to hemoprod_3_observacoes
dtypes: Int64(235), float64(16), object(18)
memory usage: 734.4+ KB

As 5 primeiras linhas com as novas colunas:


id           data_envio  ultima_pagina idioma_inicial     semente  \
0  21  2024-07-03 09:12:00              4          pt-BR        <NA>   
1  22  2024-07-03 18:36:00              4          pt-BR        <NA>   
2  26  2024-07-05 18:21:55              4          pt-BR     5371664   
3  28  2024-07-07 18:21:00              4          pt-BR        <NA>   
4  29  2024-07-07 18:39:39              4          pt-BR  1067738071   

     codigo_acesso          data_inicio     data_ultima_acao              ip  \
0  mC2pcyfb6aHYhhG  2024-07-03 09:00:00  2024-07-03 09:12:00  186.249.59.158   
1  FPAwxbAGdnaP0uv  2024-07-03 18:21:00  2024-07-03 18:36:00   186.249.60.28   
2  VwcXLtA5rfFIUi9  2024-07-05 17:19:26  2024-07-05 18:21:55    206.42.47.96   
3  7qTz7fGLGpNNxUf  2024-07-07 17:40:00  2024-07-07 18:21:00  190.102.52.160   
4  XpuFs3JEYKeGWPJ  2024-07-07 18:27:15  2024-07-07 18:39:39  190.102.52.160   

   identificacao_dado tipo_envio  ano_referencia periodo_referencia  \
0                 NaN   ORIGINAL            2024              Junho   
1                 NaN   ORIGINAL            2024              Junho   
2                 NaN   ORIGINAL            2024              Junho   
3                 NaN   ORIGINAL            2024              Junho   
4                 NaN   ORIGINAL            2024              Junho   

   identificacao_estabelecimento                 municipio  \
0                            NaN  Delmiro Gouveia, Alagoas   
1                            NaN           Maceió, Alagoas   
2                            NaN           Maceió, Alagoas   
3                            NaN        Arapiraca, Alagoas   
4                            NaN        Arapiraca, Alagoas   

                          razao_social_nome_fantasia  \
0  Secretaria de Estado da Saúde - Hospital Regio...   
1  Secretaria de Estado da Saúde - Hospital Metro...   
2           Banco de Sangue Oswaldo Calado - Hemopac   
3  Secretaria de Estado da Saúde - Unidade Emergê...   
4             Centro Hospitalar Manoel André - Chama   

         razao_social_nome_fantasia_outros            cnpj  \
0  Hospital Regional do Alto Sertão - HRAS  12200259000165   
1        HOSPITAL METROPOLITANO DE ALAGOAS  12200259000165   
2                                      NaN  12181996000168   
3                                      NaN  12200259000408   
4                                      NaN    471021000124   

             tipo_estabelecimento natureza_estabelecimento  \
0          Agência Transfusional                   Público   
1          Agência Transfusional                   Público   
2  Unidade de Coleta e Transfusão              Privado-SUS   
3          Agência Transfusional                   Público   
4          Agência Transfusional               Privado-SUS   

  dados_informados_referem_se  \
0               Único serviço   
1               Único serviço   
2            Rede de serviços   
3               Único serviço   
4               Único serviço   

                                rede_estabelecimento  cnes  endereco  \
0                                                NaN   NaN       NaN   
1                                                NaN   NaN       NaN   
2  Agência Transfusional Unimed do Banco de Sangu...   NaN       NaN   
3                                                NaN   NaN       NaN   
4                                                NaN   NaN       NaN   

   triagem_clinica_total_doacao_espontanea_aptos  \
0                                           <NA>   
1                                           <NA>   
2                                             88   
3                                           <NA>   
4                                           <NA>   

   triagem_clinica_total_doacao_espontanea_inaptos  \
0                                             <NA>   
1                                             <NA>   
2                                               19   
3                                            

In [3]:
# ASSUME QUE AS VARIÁVEIS 'hemoprod_al', 'dicionario', 'colunas_a_mais', 
# 'colunas_faltantes' E 'colunas_sql_desejadas' EXISTEM DA CÉLULA ANTERIOR.

print("--- 6. PADRONIZAÇÃO DO ESQUEMA (Remoção, Adição e Reordenação) ---")

# 6.1. REMOVE as Colunas a Mais
if colunas_a_mais:
    # Verificação de segurança: Só tenta dropar colunas que estão realmente no DF
    colunas_para_dropar = [col for col in colunas_a_mais if col in hemoprod_al.columns]
    hemoprod_al.drop(columns=colunas_para_dropar, inplace=True)
    print(f"✅ {len(colunas_para_dropar)} colunas a mais removidas.")
else:
    print("Nenhuma coluna a mais para remover.")

# 6.2. ADICIONA as Colunas Faltantes
if colunas_faltantes:
    
    # Prepara o sub-dicionário apenas com as colunas faltantes (para tipos)
    dicionario_faltante = dicionario[dicionario['nome_sql'].isin(colunas_faltantes)]
    
    for col_sql in colunas_faltantes:
        
        # Adiciona a coluna com valor nulo (NaN)
        hemoprod_al[col_sql] = np.nan 

        # --- Lógica Opcional de Conversão de Tipo (Baseada na coluna 'tipo_dados' no dicionário) ---
        # Tenta encontrar o tipo no dicionário (apenas se a coluna 'tipo_dados' existir e não estiver vazia)
        if 'tipo_dados' in dicionario.columns:
            tipo_desejado_row = dicionario_faltante[dicionario_faltante['nome_sql'] == col_sql]
            
            if not tipo_desejado_row.empty:
                tipo_desejado = tipo_desejado_row['tipo_dados'].iloc[0].lower()

                # Converte para o tipo, se for reconhecido
                if 'int' in tipo_desejado or 'float' in tipo_desejado:
                    # Usa 'float64' para números que podem ter NaNs, para evitar erros de Pandas
                    hemoprod_al[col_sql] = hemoprod_al[col_sql].astype('float64') 
                elif 'string' in tipo_desejado or 'object' in tipo_desejado:
                    # Converte para 'object' (string)
                    hemoprod_al[col_sql] = hemoprod_al[col_sql].astype('object')
                 
    print(f"✅ {len(colunas_faltantes)} colunas faltantes adicionadas e preenchidas com NaN.")
else:
    print("Nenhuma coluna faltante para adicionar.")


# 6.3. Reordena as colunas (Para garantir a ordem padronizada do dicionário)
colunas_finais = dicionario['nome_sql'].tolist()
# Garante que só as colunas que realmente existem no DF (após drop/adição) sejam usadas na reordenação
colunas_finais_presentes = [col for col in colunas_finais if col in hemoprod_al.columns]

# Esta é a linha que reordena o DataFrame
hemoprod_al = hemoprod_al[colunas_finais_presentes]
print("✅ Colunas reordenadas para seguir a ordem do dicionário.")


# --- 7. Verifique o resultado Final ---
print("\n--- Resultado Final ---")
print(f"Número de colunas final: {len(hemoprod_al.columns)}")
print("Informações do DataFrame padronizado:")
hemoprod_al.info()

print("\nAs 5 primeiras linhas com as colunas padronizadas:")
display(hemoprod_al.head())

--- 6. PADRONIZAÇÃO DO ESQUEMA (Remoção, Adição e Reordenação) ---
Nenhuma coluna a mais para remover.
Nenhuma coluna faltante para adicionar.
✅ Colunas reordenadas para seguir a ordem do dicionário.

--- Resultado Final ---
Número de colunas final: 269
Informações do DataFrame padronizado:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 315 entries, 0 to 314
Columns: 269 entries, id to hemoprod_3_observacoes
dtypes: Int64(235), float64(16), object(18)
memory usage: 734.4+ KB

As 5 primeiras linhas com as colunas padronizadas:


id           data_envio  ultima_pagina idioma_inicial     semente  \
0  21  2024-07-03 09:12:00              4          pt-BR        <NA>   
1  22  2024-07-03 18:36:00              4          pt-BR        <NA>   
2  26  2024-07-05 18:21:55              4          pt-BR     5371664   
3  28  2024-07-07 18:21:00              4          pt-BR        <NA>   
4  29  2024-07-07 18:39:39              4          pt-BR  1067738071   

     codigo_acesso          data_inicio     data_ultima_acao              ip  \
0  mC2pcyfb6aHYhhG  2024-07-03 09:00:00  2024-07-03 09:12:00  186.249.59.158   
1  FPAwxbAGdnaP0uv  2024-07-03 18:21:00  2024-07-03 18:36:00   186.249.60.28   
2  VwcXLtA5rfFIUi9  2024-07-05 17:19:26  2024-07-05 18:21:55    206.42.47.96   
3  7qTz7fGLGpNNxUf  2024-07-07 17:40:00  2024-07-07 18:21:00  190.102.52.160   
4  XpuFs3JEYKeGWPJ  2024-07-07 18:27:15  2024-07-07 18:39:39  190.102.52.160   

   identificacao_dado tipo_envio  ano_referencia periodo_referencia  \
0                 NaN   ORIGINAL            2024              Junho   
1                 NaN   ORIGINAL            2024              Junho   
2                 NaN   ORIGINAL            2024              Junho   
3                 NaN   ORIGINAL            2024              Junho   
4                 NaN   ORIGINAL            2024              Junho   

   identificacao_estabelecimento                 municipio  \
0                            NaN  Delmiro Gouveia, Alagoas   
1                            NaN           Maceió, Alagoas   
2                            NaN           Maceió, Alagoas   
3                            NaN        Arapiraca, Alagoas   
4                            NaN        Arapiraca, Alagoas   

                          razao_social_nome_fantasia  \
0  Secretaria de Estado da Saúde - Hospital Regio...   
1  Secretaria de Estado da Saúde - Hospital Metro...   
2           Banco de Sangue Oswaldo Calado - Hemopac   
3  Secretaria de Estado da Saúde - Unidade Emergê...   
4             Centro Hospitalar Manoel André - Chama   

         razao_social_nome_fantasia_outros            cnpj  \
0  Hospital Regional do Alto Sertão - HRAS  12200259000165   
1        HOSPITAL METROPOLITANO DE ALAGOAS  12200259000165   
2                                      NaN  12181996000168   
3                                      NaN  12200259000408   
4                                      NaN    471021000124   

             tipo_estabelecimento natureza_estabelecimento  \
0          Agência Transfusional                   Público   
1          Agência Transfusional                   Público   
2  Unidade de Coleta e Transfusão              Privado-SUS   
3          Agência Transfusional                   Público   
4          Agência Transfusional               Privado-SUS   

  dados_informados_referem_se  \
0               Único serviço   
1               Único serviço   
2            Rede de serviços   
3               Único serviço   
4               Único serviço   

                                rede_estabelecimento  cnes  endereco  \
0                                                NaN   NaN       NaN   
1                                                NaN   NaN       NaN   
2  Agência Transfusional Unimed do Banco de Sangu...   NaN       NaN   
3                                                NaN   NaN       NaN   
4                                                NaN   NaN       NaN   

   triagem_clinica_total_doacao_espontanea_aptos  \
0                                           <NA>   
1                                           <NA>   
2                                             88   
3                                           <NA>   
4                                           <NA>   

   triagem_clinica_total_doacao_espontanea_inaptos  \
0                                             <NA>   
1                                             <NA>   
2                                               19   
3                                            

In [4]:
# --- 2. Defina as colunas para a chave e para ordenação ---
registros_antes = len(hemoprod_al)
print(f"Total de registros ANTES da remoção de duplicatas: {registros_antes}")
    

colunas_chave = [
        'cnpj', 
        'ano_referencia', 
        'periodo_referencia', 
        'razao_social_nome_fantasia'
    ]

coluna_data = 'data_envio'

# --- 3. Verifique se as colunas necessárias existem ---
colunas_necessarias = colunas_chave + [coluna_data]

if not all(col in hemoprod_al.columns for col in colunas_necessarias):
    print("\n--- ERRO ---")
    print("Uma ou mais colunas necessárias para a deduplicação não foram encontradas.")
    colunas_faltantes = [col for col in colunas_necessarias if col not in hemoprod_al.columns]
    print(f"Colunas necessárias: {colunas_necessarias}")
    print(f"Colunas faltantes no DataFrame: {colunas_faltantes}")
else:
    # --- 4. Prepare a coluna de data e ordene os dados ---
    # Converte a coluna 'data_envio' para datetime para garantir a ordenação correta.
    # 'errors='coerce'' transformará datas inválidas em NaT (Not a Time), que são tratadas como nulas.
    hemoprod_al[coluna_data] = pd.to_datetime(hemoprod_al[coluna_data], errors='coerce')

    # Ordena o DataFrame. Os registros com data de envio mais recente ficarão por último.
    print(f"\nOrdenando os dados por '{coluna_data}'...")
    hemoprod_al_ordenado = hemoprod_al.sort_values(by=coluna_data, ascending=True)

    # --- 5. Identifique e separe os registros duplicados e únicos ---
    # Em vez de usar drop_duplicates() diretamente, vamos usar duplicated()
    # para criar uma máscara booleana.
    # 'keep='last'' marca todas as ocorrências de uma chave como True, EXCETO a última (a mais recente).
    print(f"Identificando duplicatas com base na chave: {colunas_chave}...")
    mascara_duplicatas = hemoprod_al_ordenado.duplicated(subset=colunas_chave, keep='last')

    # O DataFrame de removidos conterá todas as linhas marcadas como True
    hemoprod_removidos = hemoprod_al_ordenado[mascara_duplicatas]
    
    # O DataFrame deduplicado conterá o INVERSO (~) da máscara (linhas marcadas como False)
    hemoprod_al_deduplicado = hemoprod_al_ordenado[~mascara_duplicatas]
    
    # Agora podemos contar os registros diretamente dos novos DataFrames
    registros_depois = len(hemoprod_al_deduplicado)
    registros_removidos = len(hemoprod_removidos) 
    
    # --- 6. Exiba o resultado ---
    print("\n--- Processo Concluído ---")
    print(f"Registros removidos: {registros_removidos}")
    print(f"Total de registros DEPOIS da remoção de duplicatas: {registros_depois}")

    # (Opcional) Exibe a amostra dos removidos
    print("\nAmostra dos dados REMOVIDOS (os mais antigos/duplicados):")
    display(hemoprod_removidos.head(10))

    # Você pode continuar a usar o DataFrame 'hemoprod_al_deduplicado' para suas análises
    print("\nAmostra dos dados únicos (os mais recentes para cada chave):")
    display(hemoprod_al_deduplicado.head(10))
    
    # Agora você tem o DataFrame 'hemoprod_removidos' salvo

Total de registros ANTES da remoção de duplicatas: 315

Ordenando os dados por 'data_envio'...
Identificando duplicatas com base na chave: ['cnpj', 'ano_referencia', 'periodo_referencia', 'razao_social_nome_fantasia']...

--- Processo Concluído ---
Registros removidos: 8
Total de registros DEPOIS da remoção de duplicatas: 307

Amostra dos dados REMOVIDOS (os mais antigos/duplicados):


id          data_envio  ultima_pagina idioma_inicial     semente  \
159  223 2025-03-13 18:07:11              4          pt-BR  1477628817   
186  254 2025-05-02 14:53:15              4          pt-BR   414284960   
214  285 2025-06-04 14:30:57              4          pt-BR  1680333359   
229  302 2025-07-02 12:59:32              4          pt-BR   687257106   
252  328 2025-08-04 14:37:56              4          pt-BR   305008609   
257  335 2025-08-06 08:21:33              4          pt-BR   804427324   
297  380 2025-10-01 17:06:49              4          pt-BR  1946453061   
298  381 2025-10-01 17:17:43              4          pt-BR  1261082595   

       codigo_acesso          data_inicio     data_ultima_acao  \
159  fukFXzEvovgFY3v  2025-03-13 17:00:24  2025-03-13 18:07:11   
186  99bt2srUJ7EjuAb  2025-05-02 14:39:35  2025-05-02 14:53:15   
214  7ij8hzNGbS9VM6O  2025-06-04 13:59:41  2025-06-04 14:30:57   
229  D86bHnoNVySMI3w  2025-07-02 11:57:27  2025-07-02 12:59:32   
252  99bt2srUJ7EjuAb  2025-08-04 14:30:23  2025-08-04 14:37:56   
257  D86bHnoNVySMI3w  2025-08-06 07:52:51  2025-08-06 08:21:33   
297  99bt2srUJ7EjuAb  2025-10-01 16:55:56  2025-10-01 17:06:49   
298  99bt2srUJ7EjuAb  2025-10-01 17:09:46  2025-10-01 17:17:43   

                 ip  identificacao_dado    tipo_envio  ano_referencia  \
159  186.249.59.155                 NaN      ORIGINAL            2025   
186    201.33.41.54                 NaN      ORIGINAL            2024   
214  186.249.59.157                 NaN      ORIGINAL            2025   
229   189.52.187.82                 NaN      ORIGINAL            2025   
252   190.15.107.82                 NaN      ORIGINAL            2025   
257   189.52.187.82                 NaN      ORIGINAL            2025   
297   190.15.107.84                 NaN      ORIGINAL            2025   
298   190.15.107.84                 NaN  RETIFICADORA            2025   

    periodo_referencia  identificacao_estabelecimento  \
159          Fevereiro                            NaN   
186              Abril                            NaN   
214               Maio                            NaN   
229              Junho                            NaN   
252              Julho                            NaN   
257              Julho                            NaN   
297           Setembro                            NaN   
298           Setembro                            NaN   

                          municipio  \
159                 Maceió, Alagoas   
186  São Miguel dos Campos, Alagoas   
214              Arapiraca, Alagoas   
229                 Maceió, Alagoas   
252  São Miguel dos Campos, Alagoas   
257                 Maceió, Alagoas   
297  São Miguel dos Campos, Alagoas   
298  São Miguel dos Campos, Alagoas   

                            razao_social_nome_fantasia  \
159  Hospital Geral do Estado Professor Oswaldo Bra...   
186  Santa Casa de Misericórdia de São Miguel dos C...   
214  Secretaria de Estado da Saúde - Hemocentro de ...   
229  Fundação Hospital da Agroindústria do Açúcar -...   
252  Santa Casa de Misericórdia de São Miguel dos C...   
257  Fundação Hospital da Agroindústria do Açúcar -...   
297  Santa Casa de Misericórdia de São Miguel dos C...   
298  Santa Casa de Misericórdia de São Miguel dos C...   

    razao_social_nome_fantasia_outros            cnpj  \
159                               NaN  12200259000246   
186                               NaN     12737680000   
214                               NaN  12200259000165   
229                               NaN   1229129000159   
252                               NaN     12737680000   
257                               NaN   1229129000159   
297                               NaN     12737680000   
298                               NaN     12737680000   

               tipo_estabelecimento natureza_estabelecimento  \
159          Agência Transfusional                   Público   
186          Agência Transfusional               Privad


Amostra dos dados únicos (os mais recentes para cada chave):


id          data_envio  ultima_pagina idioma_inicial     semente  \
0  21 2024-07-03 09:12:00              4          pt-BR        <NA>   
1  22 2024-07-03 18:36:00              4          pt-BR        <NA>   
2  26 2024-07-05 18:21:55              4          pt-BR     5371664   
3  28 2024-07-07 18:21:00              4          pt-BR        <NA>   
4  29 2024-07-07 18:39:39              4          pt-BR  1067738071   
5  30 2024-07-08 09:37:00              4          pt-BR        <NA>   
6  31 2024-07-08 13:36:00              4          pt-BR        <NA>   
7  34 2024-07-08 14:48:50              4          pt-BR   981201672   
8  35 2024-07-09 12:03:00              4          pt-BR        <NA>   
9  37 2024-07-10 10:19:00              4          pt-BR        <NA>   

     codigo_acesso          data_inicio     data_ultima_acao  \
0  mC2pcyfb6aHYhhG  2024-07-03 09:00:00  2024-07-03 09:12:00   
1  FPAwxbAGdnaP0uv  2024-07-03 18:21:00  2024-07-03 18:36:00   
2  VwcXLtA5rfFIUi9  2024-07-05 17:19:26  2024-07-05 18:21:55   
3  7qTz7fGLGpNNxUf  2024-07-07 17:40:00  2024-07-07 18:21:00   
4  XpuFs3JEYKeGWPJ  2024-07-07 18:27:15  2024-07-07 18:39:39   
5  zdJC1Bv8XoRbUGn  2024-07-08 09:29:00  2024-07-08 09:37:00   
6  zLOSbHBAabyowYH  2024-07-08 11:38:00  2024-07-08 13:36:00   
7  99bt2srUJ7EjuAb  2024-07-08 14:31:11  2024-07-08 14:48:50   
8  pLBxuEfTv0EU9G3  2024-07-09 11:03:00  2024-07-09 12:03:00   
9  LvPMJGUfL1n2a6S  2024-07-10 09:27:00  2024-07-10 10:19:00   

                                       ip  identificacao_dado    tipo_envio  \
0                          186.249.59.158                 NaN      ORIGINAL   
1                           186.249.60.28                 NaN      ORIGINAL   
2                            206.42.47.96                 NaN      ORIGINAL   
3                          190.102.52.160                 NaN      ORIGINAL   
4                          190.102.52.160                 NaN      ORIGINAL   
5  2804:14d:1289:8bfb:b4fb:13c8:940e:35a9                 NaN  RETIFICADORA   
6                          186.249.59.155                 NaN  RETIFICADORA   
7                           190.15.107.82                 NaN      ORIGINAL   
8                             168.0.8.187                 NaN      ORIGINAL   
9                          186.249.59.156                 NaN      ORIGINAL   

   ano_referencia periodo_referencia  identificacao_estabelecimento  \
0            2024              Junho                            NaN   
1            2024              Junho                            NaN   
2            2024              Junho                            NaN   
3            2024              Junho                            NaN   
4            2024              Junho                            NaN   
5            2024              Junho                            NaN   
6            2024              Junho                            NaN   
7            2024              Junho                            NaN   
8            2024              Junho                            NaN   
9            2023        Consolidado                            NaN   

                        municipio  \
0        Delmiro Gouveia, Alagoas   
1                 Maceió, Alagoas   
2                 Maceió, Alagoas   
3              Arapiraca, Alagoas   
4              Arapiraca, Alagoas   
5                 Maceió, Alagoas   
6     União dos Palmares, Alagoas   
7  São Miguel dos Campos, Alagoas   
8               Coruripe, Alagoas   
9                 Maceió, Alagoas   

                          razao_social_nome_fantasia  \
0  Secretaria de Estado da Saúde - Hospital Regio...   
1  Secretaria de Estado da Saúde - Hospital Metro...   
2           Banco de Sangue Oswaldo Calado - Hemopac   
3  Secretaria de Estado da Saúde - Unidade Emergê...   
4             Centro Hospitalar Manoel André - Chama   
5  Secretaria de Estado da Saúde - Hospital da Mu...   
6  Secretaria de Estado da Saúde - UBS União dos ...   
7  Santa

In [5]:
hemoprod_al_deduplicado.to_excel('dados_processados/hemoprod_al.xlsx', index=False)

## Hemoprod Amazonas

In [20]:
import pandas as pd
import os

# --- 1. Defina os caminhos para seus arquivos ---
# Ajuste os caminhos conforme a estrutura do seu projeto no notebook
dados_brutos_path = 'dados_brutos'
dicionario_path = 'dicionario_colunas_269.xlsx'
arquivo_dados_path = os.path.join(dados_brutos_path, 'Hemoprod_AM.xlsx')
nome_planilha = 'HEMOPROD - AMAZONAS'

try:
    # Carrega o arquivo de dados
    hemoprod_am = pd.read_excel(arquivo_dados_path, sheet_name=nome_planilha)
    print("Arquivo de dados carregado com sucesso.")
    print(f"Número de colunas original: {len(hemoprod_am.columns)}")

    # Carrega o arquivo de dicionário
    dicionario = pd.read_excel(dicionario_path)
    print("Arquivo de dicionário carregado com sucesso.")

    # --- 3. Limpeza Inicial dos Nomes das Colunas (ADICIONADO) ---
    # Mapeia as colunas, limpando espaços em branco no início e fim
    # e substituindo o caractere \xa0 (Non-breaking space) por um espaço normal.
    mapa_limpeza = {
        col: col.strip().replace('\xa0', ' ') 
        for col in hemoprod_am.columns
    }

    # Aplica a renomeação para limpar os nomes
    hemoprod_am = hemoprod_am.rename(columns=mapa_limpeza)
    print("Nomes das colunas do DataFrame limpos e padronizados (strip/\\xa0).")

    # --- 4. Crie o dicionário de mapeamento ---
    # Cria um dicionário no formato {'nome_original': 'nome_sql'} para uso no .rename()
    # NOTA: O 'nome_original' no dicionário TAMBÉM deve estar limpo para combinar.
    # Se o dicionário não estiver limpo, adicione a mesma limpeza aqui:
    dicionario['nome_original'] = dicionario['nome_original'].astype(str).str.strip().str.replace('\xa0', ' ')
    
    mapa_renomeacao = pd.Series(dicionario['nome_sql'].values, index=dicionario['nome_original']).to_dict()
    
    # Lista dos nomes de coluna no DataFrame atual APÓS a limpeza inicial
    colunas_atuais = set(hemoprod_am.columns)
    
    # Lista dos nomes originais de coluna no dicionário APÓS a limpeza (se aplicada)
    colunas_originais_dicionario = set(dicionario['nome_original'].tolist())
    
    # Lista dos nomes SQL (os desejados) no dicionário
    colunas_sql_desejadas = set(dicionario['nome_sql'].tolist())
    
    # --- 5. Renomeie as colunas com base no mapeamento (nome_original -> nome_sql) ---
    print("\n--- Processo de Renomeação ---")
    hemoprod_am.rename(columns=mapa_renomeacao, inplace=True)
    print("Colunas renomeadas com sucesso (apenas as que existiam no dicionário foram modificadas).")


   # --- 4. Inferir Tipos e Criar Mapeamento de Tipos ---
    
    # --- Lógica de Inferência customizada para 'Int64' ---
    tipos_inferidos = {}
    for col in hemoprod_am.columns:
        
        # 4.1. Tenta converter a coluna para o tipo que melhor representa seus dados (incluindo Int64/string/datetime)
        # O errors='ignore' é crucial para não falhar se a coluna não puder ser convertida
        coluna_convertida = pd.to_numeric(hemoprod_am[col], errors='coerce')
        
        # Se a conversão for bem-sucedida (não é totalmente NaN, nem totalmente string)
        if not coluna_convertida.isna().all() and coluna_convertida.dtype.kind in 'fi': # 'f' para float, 'i' para int
            
            # Se a coluna parecer um número, tentamos forçar para Int64
            # O .astype('Int64') usa o tipo inteiro que suporta NaN
            try:
                # Se for possível converter para Int64, use 'Int64'
                hemoprod_am[col] = hemoprod_am[col].astype('Int64')
                tipos_inferidos[col] = 'Int64'
            except Exception:
                # Se for numérico mas não puder ser Int64 (ex: float com muitas casas decimais), use 'float64'
                tipos_inferidos[col] = 'float64'
        
        # Verifica se é data/hora
        elif pd.api.types.is_datetime64_any_dtype(hemoprod_am[col]):
             tipos_inferidos[col] = 'datetime64[ns]'
             
        # Caso contrário, assume-se que é um texto/string
        else:
            tipos_inferidos[col] = 'object' # O padrão para string no pandas

    
    print("\nTipos de dados inferidos (amostra):")
    for i, (col, dtype) in enumerate(tipos_inferidos.items()):
        if i < 5:
            print(f"  {col}: {dtype}")
        if i == 5:
            print("  ...")
    
    # --- 5. Atualizar o DataFrame Dicionário ---
    
    # 5.1. Cria a coluna 'tipo_dados' no dicionário e preenche com os tipos inferidos
    dicionario['tipo_dados'] = dicionario['nome_sql'].map(tipos_inferidos)
    
    # 5.2. Trata colunas não encontradas no DataFrame de dados
    dicionario['tipo_dados'] = dicionario['tipo_dados'].fillna('object')
    
    print("\n--- Dicionário Atualizado ---")
    print("Coluna 'tipo_dados' criada com sucesso, com numéricos definidos como 'Int64' ou 'float64'.")
    
    # --- 6. Salvar o Dicionário Atualizado ---

    # Sugestão de novo caminho para salvar
    # novo_dicionario_path = 'dicionario_colunas_269_COM_TIPOS_V3.xlsx'
    
    # dicionario.to_excel(novo_dicionario_path, index=False)
    
    print(f"\n✅ Dicionário salvo com a nova coluna 'tipo_dados' em: {novo_dicionario_path}")
    print("\nPrimeiras linhas do dicionário atualizado:")
    display(dicionario.head())

    # --- 6. Análise de Colunas (Qualidade dos Dados) ---

    # 6.1. Colunas que não puderam ser renomeadas (existem no DF, mas não no 'nome_original' do dicionário)
    # Aqui usamos as colunas atuais ANTES da renomeação para ver o que sobrou.
    colunas_nao_mapeadas = [
        col for col in colunas_atuais 
        if col not in colunas_originais_dicionario
    ]

    print("-" * 30)
    print("Análise de Colunas do DataFrame (hemoprod_am):")
    print(f"Número de colunas não mapeadas: {len(colunas_nao_mapeadas)}")
    print(f"Colunas não mapeadas (manterão nome original): {colunas_nao_mapeadas}")
    
    # 6.2. Análise de Colunas Faltantes/A Mais (Comparação com 'nome_sql' desejado)
    colunas_apos_renomeacao = set(hemoprod_am.columns)
    
    colunas_faltantes = list(colunas_sql_desejadas - colunas_apos_renomeacao)
    colunas_a_mais = list(colunas_apos_renomeacao - colunas_sql_desejadas)

    print("-" * 30)
    print("Análise de Colunas (Comparação com a lista SQL DESEJADA):")
    print(f"Número de colunas FALTANTES: {len(colunas_faltantes)}")
    print(f"Colunas FALTANTES (deveriam estar, mas não estão): {colunas_faltantes}")
    print("-" * 30)
    print(f"Número de colunas A MAIS: {len(colunas_a_mais)}")
    print(f"Colunas A MAIS (estão no DF, mas não na lista SQL desejada): {colunas_a_mais}")
    print("-" * 30)

    # --- 7. Verifique o resultado ---
    print("\nInformações do DataFrame com as novas colunas:")
    hemoprod_am.info()
    
    print("\nAs 5 primeiras linhas com as novas colunas:")
    display(hemoprod_am.head())

except FileNotFoundError as e:
    print(f"\nErro de arquivo não encontrado: {e}")
except KeyError as e:
    print(f"\nErro de coluna não encontrada: {e}. Verifique se as colunas 'nome_original' e 'nome_sql' existem no seu arquivo de dicionário.")
except Exception as e:
    print(f"\nOcorreu um erro inesperado: {e}")

Arquivo de dados carregado com sucesso.
Número de colunas original: 270
Arquivo de dicionário carregado com sucesso.
Nomes das colunas do DataFrame limpos e padronizados (strip/\xa0).

--- Processo de Renomeação ---
Colunas renomeadas com sucesso (apenas as que existiam no dicionário foram modificadas).

Tipos de dados inferidos (amostra):
  id: Int64
  data_envio: object
  ultima_pagina: Int64
  idioma_inicial: object
  semente: Int64
  ...

--- Dicionário Atualizado ---
Coluna 'tipo_dados' criada com sucesso, com numéricos definidos como 'Int64' ou 'float64'.

✅ Dicionário salvo com a nova coluna 'tipo_dados' em: dicionario_colunas_269_COM_TIPOS_V2.xlsx

Primeiras linhas do dicionário atualizado:


nome_original        nome_sql  \
0  ID da resposta              id   
1   Data de envio      data_envio   
2   Última página   ultima_pagina   
3  Idioma inicial  idioma_inicial   
4         Semente         semente   

                                          comentario tipo_dados  
0  Identificador único e chave primária da submis...      Int64  
1   Data e hora exatas do envio final do formulário.     object  
2  Título da última página do formulário acessada...      Int64  
3  Idioma selecionado no início do preenchimento ...     object  
4  Valor interno de semente/aleatorização (uso té...      Int64

------------------------------
Análise de Colunas do DataFrame (hemoprod_am):
Número de colunas não mapeadas: 1
Colunas não mapeadas (manterão nome original): ['URL de referência']
------------------------------
Análise de Colunas (Comparação com a lista SQL DESEJADA):
Número de colunas FALTANTES: 0
Colunas FALTANTES (deveriam estar, mas não estão): []
------------------------------
Número de colunas A MAIS: 1
Colunas A MAIS (estão no DF, mas não na lista SQL desejada): ['URL de referência']
------------------------------

Informações do DataFrame com as novas colunas:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 32 entries, 0 to 31
Columns: 270 entries, id to hemoprod_3_observacoes
dtypes: Int64(229), float64(27), object(14)
memory usage: 74.8+ KB

As 5 primeiras linhas com as novas colunas:


id           data_envio  ultima_pagina idioma_inicial     semente  \
0   5  2023-10-26 11:56:58              4          pt-BR   534226503   
1   6  2023-10-26 12:54:31              4          pt-BR  1723372445   
2   9  2023-10-31 11:14:51              4          pt-BR  2072510604   
3  10  2023-10-31 12:16:31              4          pt-BR   411593062   
4  11  2023-10-31 13:06:36              4          pt-BR   542798905   

     codigo_acesso          data_inicio     data_ultima_acao             ip  \
0  1vXXcXvg3W0RfaG  2023-10-26 09:36:21  2023-10-26 11:56:58  200.129.161.9   
1  1vXXcXvg3W0RfaG  2023-10-26 12:27:08  2023-10-26 12:54:31  200.129.161.9   
2  1vXXcXvg3W0RfaG  2023-10-31 10:49:55  2023-10-31 11:14:51  200.129.161.9   
3  1vXXcXvg3W0RfaG  2023-10-31 11:17:44  2023-10-31 12:16:31  200.129.161.9   
4  1vXXcXvg3W0RfaG  2023-10-31 12:19:45  2023-10-31 13:06:36  200.129.161.9   

     URL de referência  identificacao_dado tipo_envio  ano_referencia  \
0  https://www.gov.br/                 NaN   ORIGINAL            2023   
1  https://www.gov.br/                 NaN   ORIGINAL            2023   
2  https://www.gov.br/                 NaN   ORIGINAL            2023   
3  https://www.gov.br/                 NaN   ORIGINAL            2023   
4  https://www.gov.br/                 NaN   ORIGINAL            2023   

  periodo_referencia  identificacao_estabelecimento         municipio  \
0            Janeiro                            NaN  Manaus, Amazonas   
1          Fevereiro                            NaN  Manaus, Amazonas   
2              Março                            NaN  Manaus, Amazonas   
3              Abril                            NaN  Manaus, Amazonas   
4               Maio                            NaN  Manaus, Amazonas   

                          razao_social_nome_fantasia  \
0  Fundação de Hemotologia e Hemoterapia do Amazo...   
1  Fundação de Hemotologia e Hemoterapia do Amazo...   
2  Fundação Hospitalar de Hematologia e Hemoterap...   
3  Fundação Hospitalar de Hematologia e Hemoterap...   
4  Fundação Hospitalar de Hematologia e Hemoterap...   

   razao_social_nome_fantasia_outros            cnpj    tipo_estabelecimento  \
0                                NaN  63678320000115  Hemocentro Coordenador   
1                                NaN  63678320000115  Hemocentro Coordenador   
2                                NaN  63678320000115  Hemocentro Coordenador   
3                                NaN  63678320000115  Hemocentro Coordenador   
4                                NaN  63678320000115  Hemocentro Coordenador   

  natureza_estabelecimento dados_informados_referem_se  rede_estabelecimento  \
0                  Público               Único serviço                   NaN   
1                  Público               Único serviço                   NaN   
2                  Público               Único serviço                   NaN   
3                  Público               Único serviço                   NaN   
4                  Público               Único serviço                   NaN   

   cnes  endereco  triagem_clinica_total_doacao_espontanea_aptos  \
0   NaN       NaN                                           2447   
1   NaN       NaN                                           2386   
2   NaN       NaN                                           2281   
3   NaN       NaN                                           2839   
4   NaN       NaN                                           2297   

   triagem_clinica_total_doacao_espontanea_inaptos  \
0                                              571   
1                                              651   
2                                              620   
3                                              617   
4                                              597   

   triagem_clinica_total_doacao_reposicao_aptos  \
0                                          2788   
1                                          2431   
2                              

In [17]:
# ASSUME QUE AS VARIÁVEIS 'hemoprod_al', 'dicionario', 'colunas_a_mais', 
# 'colunas_faltantes' E 'colunas_sql_desejadas' EXISTEM DA CÉLULA ANTERIOR.

print("--- 6. PADRONIZAÇÃO DO ESQUEMA (Remoção, Adição e Reordenação) ---")

# 6.1. REMOVE as Colunas a Mais
if colunas_a_mais:
    # Verificação de segurança: Só tenta dropar colunas que estão realmente no DF
    colunas_para_dropar = [col for col in colunas_a_mais if col in hemoprod_al.columns]
    hemoprod_am.drop(columns=colunas_para_dropar, inplace=True)
    print(f"✅ {len(colunas_para_dropar)} colunas a mais removidas.")
else:
    print("Nenhuma coluna a mais para remover.")

# 6.2. ADICIONA as Colunas Faltantes
if colunas_faltantes:
    
    # Prepara o sub-dicionário apenas com as colunas faltantes (para tipos)
    dicionario_faltante = dicionario[dicionario['nome_sql'].isin(colunas_faltantes)]
    
    for col_sql in colunas_faltantes:
        
        # Adiciona a coluna com valor nulo (NaN)
        hemoprod_am[col_sql] = np.nan 

        # --- Lógica Opcional de Conversão de Tipo (Baseada na coluna 'tipo_dados' no dicionário) ---
        # Tenta encontrar o tipo no dicionário (apenas se a coluna 'tipo_dados' existir e não estiver vazia)
        if 'tipo_dados' in dicionario.columns:
            tipo_desejado_row = dicionario_faltante[dicionario_faltante['nome_sql'] == col_sql]
            
            if not tipo_desejado_row.empty:
                tipo_desejado = tipo_desejado_row['tipo_dados'].iloc[0].lower()

                # Converte para o tipo, se for reconhecido
                if 'int' in tipo_desejado or 'float' in tipo_desejado:
                    # Usa 'float64' para números que podem ter NaNs, para evitar erros de Pandas
                    hemoprod_am[col_sql] = hemoprod_am[col_sql].astype('float64') 
                elif 'string' in tipo_desejado or 'object' in tipo_desejado:
                    # Converte para 'object' (string)
                    hemoprod_am[col_sql] = hemoprod_am[col_sql].astype('object')
                 
    print(f"✅ {len(colunas_faltantes)} colunas faltantes adicionadas e preenchidas com NaN.")
else:
    print("Nenhuma coluna faltante para adicionar.")


# 6.3. Reordena as colunas (Para garantir a ordem padronizada do dicionário)
colunas_finais = dicionario['nome_sql'].tolist()
# Garante que só as colunas que realmente existem no DF (após drop/adição) sejam usadas na reordenação
colunas_finais_presentes = [col for col in colunas_finais if col in hemoprod_am.columns]

# Esta é a linha que reordena o DataFrame
hemoprod_am = hemoprod_am[colunas_finais_presentes]
print("✅ Colunas reordenadas para seguir a ordem do dicionário.")


# --- 7. Verifique o resultado Final ---
print("\n--- Resultado Final ---")
print(f"Número de colunas final: {len(hemoprod_am.columns)}")
print("Informações do DataFrame padronizado:")
hemoprod_am.info()

print("\nAs 5 primeiras linhas com as colunas padronizadas:")
display(hemoprod_am.head())

--- 6. PADRONIZAÇÃO DO ESQUEMA (Remoção, Adição e Reordenação) ---
✅ 0 colunas a mais removidas.
Nenhuma coluna faltante para adicionar.
✅ Colunas reordenadas para seguir a ordem do dicionário.

--- Resultado Final ---
Número de colunas final: 269
Informações do DataFrame padronizado:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 32 entries, 0 to 31
Columns: 269 entries, id to hemoprod_3_observacoes
dtypes: Int64(229), float64(27), object(13)
memory usage: 74.5+ KB

As 5 primeiras linhas com as colunas padronizadas:


id           data_envio  ultima_pagina idioma_inicial     semente  \
0   5  2023-10-26 11:56:58              4          pt-BR   534226503   
1   6  2023-10-26 12:54:31              4          pt-BR  1723372445   
2   9  2023-10-31 11:14:51              4          pt-BR  2072510604   
3  10  2023-10-31 12:16:31              4          pt-BR   411593062   
4  11  2023-10-31 13:06:36              4          pt-BR   542798905   

     codigo_acesso          data_inicio     data_ultima_acao             ip  \
0  1vXXcXvg3W0RfaG  2023-10-26 09:36:21  2023-10-26 11:56:58  200.129.161.9   
1  1vXXcXvg3W0RfaG  2023-10-26 12:27:08  2023-10-26 12:54:31  200.129.161.9   
2  1vXXcXvg3W0RfaG  2023-10-31 10:49:55  2023-10-31 11:14:51  200.129.161.9   
3  1vXXcXvg3W0RfaG  2023-10-31 11:17:44  2023-10-31 12:16:31  200.129.161.9   
4  1vXXcXvg3W0RfaG  2023-10-31 12:19:45  2023-10-31 13:06:36  200.129.161.9   

   identificacao_dado tipo_envio  ano_referencia periodo_referencia  \
0                 NaN   ORIGINAL            2023            Janeiro   
1                 NaN   ORIGINAL            2023          Fevereiro   
2                 NaN   ORIGINAL            2023              Março   
3                 NaN   ORIGINAL            2023              Abril   
4                 NaN   ORIGINAL            2023               Maio   

   identificacao_estabelecimento         municipio  \
0                            NaN  Manaus, Amazonas   
1                            NaN  Manaus, Amazonas   
2                            NaN  Manaus, Amazonas   
3                            NaN  Manaus, Amazonas   
4                            NaN  Manaus, Amazonas   

                          razao_social_nome_fantasia  \
0  Fundação de Hemotologia e Hemoterapia do Amazo...   
1  Fundação de Hemotologia e Hemoterapia do Amazo...   
2  Fundação Hospitalar de Hematologia e Hemoterap...   
3  Fundação Hospitalar de Hematologia e Hemoterap...   
4  Fundação Hospitalar de Hematologia e Hemoterap...   

   razao_social_nome_fantasia_outros            cnpj    tipo_estabelecimento  \
0                                NaN  63678320000115  Hemocentro Coordenador   
1                                NaN  63678320000115  Hemocentro Coordenador   
2                                NaN  63678320000115  Hemocentro Coordenador   
3                                NaN  63678320000115  Hemocentro Coordenador   
4                                NaN  63678320000115  Hemocentro Coordenador   

  natureza_estabelecimento dados_informados_referem_se  rede_estabelecimento  \
0                  Público               Único serviço                   NaN   
1                  Público               Único serviço                   NaN   
2                  Público               Único serviço                   NaN   
3                  Público               Único serviço                   NaN   
4                  Público               Único serviço                   NaN   

   cnes  endereco  triagem_clinica_total_doacao_espontanea_aptos  \
0   NaN       NaN                                           2447   
1   NaN       NaN                                           2386   
2   NaN       NaN                                           2281   
3   NaN       NaN                                           2839   
4   NaN       NaN                                           2297   

   triagem_clinica_total_doacao_espontanea_inaptos  \
0                                              571   
1                                              651   
2                                              620   
3                                              617   
4                                              597   

   triagem_clinica_total_doacao_reposicao_aptos  \
0                                          2788   
1                                          2431   
2                                          3338   
3                                          3280   
4                                          3368   

   

In [9]:
#remover o url
hemoprod_am = hemoprod_am.drop(columns=['url'])

In [11]:
# --- 2. Defina as colunas para a chave e para ordenação ---
registros_antes = len(hemoprod_am)
print(f"Total de registros ANTES da remoção de duplicatas: {registros_antes}")
    

colunas_chave = [
        'cnpj', 
        'ano_referencia', 
        'periodo_referencia', 
        'razao_social_nome_fantasia'
    ]

coluna_data = 'data_envio'

# --- 3. Verifique se as colunas necessárias existem ---
colunas_necessarias = colunas_chave + [coluna_data]

if not all(col in hemoprod_am.columns for col in colunas_necessarias):
    print("\n--- ERRO ---")
    print("Uma ou mais colunas necessárias para a deduplicação não foram encontradas.")
    colunas_faltantes = [col for col in colunas_necessarias if col not in hemoprod_am.columns]
    print(f"Colunas necessárias: {colunas_necessarias}")
    print(f"Colunas faltantes no DataFrame: {colunas_faltantes}")
else:
    # --- 4. Prepare a coluna de data e ordene os dados ---
    # Converte a coluna 'data_envio' para datetime para garantir a ordenação correta.
    # 'errors='coerce'' transformará datas inválidas em NaT (Not a Time), que são tratadas como nulas.
    hemoprod_am[coluna_data] = pd.to_datetime(hemoprod_am[coluna_data], errors='coerce')

    # Ordena o DataFrame. Os registros com data de envio mais recente ficarão por último.
    print(f"\nOrdenando os dados por '{coluna_data}'...")
    hemoprod_am_ordenado = hemoprod_am.sort_values(by=coluna_data, ascending=True)

    # --- 5. Identifique e separe os registros duplicados e únicos ---
    # Em vez de usar drop_duplicates() diretamente, vamos usar duplicated()
    # para criar uma máscara booleana.
    # 'keep='last'' marca todas as ocorrências de uma chave como True, EXCETO a última (a mais recente).
    print(f"Identificando duplicatas com base na chave: {colunas_chave}...")
    mascara_duplicatas = hemoprod_am_ordenado.duplicated(subset=colunas_chave, keep='last')

    # O DataFrame de removidos conterá todas as linhas marcadas como True
    hemoprod_removidos = hemoprod_am_ordenado[mascara_duplicatas]
    
    # O DataFrame deduplicado conterá o INVERSO (~) da máscara (linhas marcadas como False)
    hemoprod_am_deduplicado = hemoprod_am_ordenado[~mascara_duplicatas]
    
    # Agora podemos contar os registros diretamente dos novos DataFrames
    registros_depois = len(hemoprod_am_deduplicado)
    registros_removidos = len(hemoprod_removidos) 
    
    # --- 6. Exiba o resultado ---
    print("\n--- Processo Concluído ---")
    print(f"Registros removidos: {registros_removidos}")
    print(f"Total de registros DEPOIS da remoção de duplicatas: {registros_depois}")

    # (Opcional) Exibe a amostra dos removidos
    print("\nAmostra dos dados REMOVIDOS (os mais antigos/duplicados):")
    display(hemoprod_removidos.head(10))

    # Você pode continuar a usar o DataFrame 'hemoprod_am_deduplicado' para suas análises
    print("\nAmostra dos dados únicos (os mais recentes para cada chave):")
    display(hemoprod_am_deduplicado.head(10))

    hemoprod_am.describe()
    
    # Agora você tem o DataFrame 'hemoprod_removidos' salvo

Total de registros ANTES da remoção de duplicatas: 32

Ordenando os dados por 'data_envio'...
Identificando duplicatas com base na chave: ['cnpj', 'ano_referencia', 'periodo_referencia', 'razao_social_nome_fantasia']...

--- Processo Concluído ---
Registros removidos: 0
Total de registros DEPOIS da remoção de duplicatas: 32

Amostra dos dados REMOVIDOS (os mais antigos/duplicados):


Empty DataFrame
Columns: [id, data_envio, ultima_pagina, idioma_inicial, semente, codigo_acesso, data_inicio, data_ultima_acao, ip, identificacao_dado, tipo_envio, ano_referencia, periodo_referencia, identificacao_estabelecimento, municipio, razao_social_nome_fantasia, razao_social_nome_fantasia_outros, cnpj, tipo_estabelecimento, natureza_estabelecimento, dados_informados_referem_se, rede_estabelecimento, cnes, endereco, triagem_clinica_total_doacao_espontanea_aptos, triagem_clinica_total_doacao_espontanea_inaptos, triagem_clinica_total_doacao_reposicao_aptos, triagem_clinica_total_doacao_reposicao_inaptos, triagem_clinica_total_doacao_autologa_aptos, triagem_clinica_total_doacao_autologa_inaptos, total_doador_primeira_vez_aptos, total_doador_primeira_vez_inaptos, total_doador_repeticao_aptos, total_doador_repeticao_inaptos, total_doador_esporadico_aptos, total_doador_esporadico_inaptos, total_doador_masculino_aptos, total_doador_masculino_inaptos, total_doador_feminino_aptos, total_doador_feminino_inaptos, total_doador_menor_de_18_anos_aptos, total_doador_menor_de_18_anos_inaptos, total_doador_18_ate_29_anos_aptos, total_doador_18_ate_29_anos_inaptos, total_doador_acima_de_29_anos_aptos, total_doador_acima_de_29_anos_inaptos, total_candidatos_inaptos_anemia_masculino, total_candidatos_inaptos_anemia_feminino, total_candidatos_inaptos_anemia_total, total_candidatos_inaptos_hipertensao_masculino, total_candidatos_inaptos_hipertensao_feminino, total_candidatos_inaptos_hipertensao_total, total_candidatos_inaptos_hipotensao_masculino, total_candidatos_inaptos_hipotensao_feminino, total_candidatos_inaptos_hipotensao_total, total_candidatos_inaptos_alcoolismo_masculino, total_candidatos_inaptos_alcoolismo_feminino, total_candidatos_inaptos_alcoolismo_total, total_candidatos_inaptos_comportamento_risco_dst_masculino, total_candidatos_inaptos_comportamento_risco_dst_feminino, total_candidatos_inaptos_comportamento_risco_dst_total, total_candidatos_inaptos_uso_drogas_masculino, total_candidatos_inaptos_uso_drogas_feminino, total_candidatos_inaptos_uso_drogas_total, total_candidatos_inaptos_hepatite_masculino, total_candidatos_inaptos_hepatite_feminino, total_candidatos_inaptos_hepatite_total, total_candidatos_inaptos_doenca_chagas_masculino, total_candidatos_inaptos_doenca_chagas_feminino, total_candidatos_inaptos_doenca_chagas_total, total_candidatos_inaptos_malaria_masculino, total_candidatos_inaptos_malaria_feminino, total_candidatos_inaptos_malaria_total, total_candidatos_inaptos_outras_masculino, total_candidatos_inaptos_outras_feminino, total_candidatos_inaptos_outras_total, coleta_total_candidatos_desistentes, total_interrupcoes_coleta_dificuldade_puncao_venosa, total_interrupcoes_coleta_reacao_vagal, total_interrupcoes_coleta_outros_motivos, total_coletas_sangue_total, total_coletas_aferese, hemoprod_1_observacoes, exames_triagem_doenca_doenca_chagas_amostras_testadas, exames_triagem_doenca_doenca_chagas_amostras_reagentes, exames_triagem_doenca_hiv_amostras_testadas, exames_triagem_doenca_hiv_amostras_reagentes, exames_triagem_doenca_sifilis_amostras_testadas, `exames_triagem_doenca_sifilis_amostras_reagentes, exames_triagem_doenca_hepatite_b_hbs_ag_amostras_testadas, exames_triagem_doenca_hepatite_b_hbs_ag_amostras_reagentes, exames_triagem_doenca_hepatite_b_anti_hbc_amostras_testadas, exames_triagem_doenca_hepatite_b_anti_hbc_amostras_reagentes, exames_triagem_doenca_hepatite_c_amostras_testadas, exames_triagem_doenca_hepatite_c_amostras_reagentes, exames_triagem_doenca_htlv_i_ii_amostras_testadas, exames_triagem_doenca_htlv_i_ii_amostras_reagentes, exames_triagem_doenca_malaria_amostras_testadas, exames_triagem_doenca_malaria_amostras_reagentes, exames_triagem_doenca_hbv_teste_nat_amostras_testadas, ...]
Index: []


Amostra dos dados únicos (os mais recentes para cada chave):


id          data_envio  ultima_pagina idioma_inicial     semente  \
0   5 2023-10-26 11:56:58              4          pt-BR   534226503   
1   6 2023-10-26 12:54:31              4          pt-BR  1723372445   
2   9 2023-10-31 11:14:51              4          pt-BR  2072510604   
3  10 2023-10-31 12:16:31              4          pt-BR   411593062   
4  11 2023-10-31 13:06:36              4          pt-BR   542798905   
5  12 2023-10-31 13:36:54              4          pt-BR   320740727   
6  13 2023-11-14 12:54:29              4          pt-BR   543006545   
7  15 2023-12-01 17:54:03              4          pt-BR   917042517   
8  16 2023-12-01 18:34:34              4          pt-BR  1436508263   
9  19 2024-01-09 17:47:00              4          pt-BR        <NA>   

     codigo_acesso          data_inicio     data_ultima_acao             ip  \
0  1vXXcXvg3W0RfaG  2023-10-26 09:36:21  2023-10-26 11:56:58  200.129.161.9   
1  1vXXcXvg3W0RfaG  2023-10-26 12:27:08  2023-10-26 12:54:31  200.129.161.9   
2  1vXXcXvg3W0RfaG  2023-10-31 10:49:55  2023-10-31 11:14:51  200.129.161.9   
3  1vXXcXvg3W0RfaG  2023-10-31 11:17:44  2023-10-31 12:16:31  200.129.161.9   
4  1vXXcXvg3W0RfaG  2023-10-31 12:19:45  2023-10-31 13:06:36  200.129.161.9   
5  1vXXcXvg3W0RfaG  2023-10-31 13:18:44  2023-10-31 13:36:54  200.129.161.9   
6  1vXXcXvg3W0RfaG  2023-11-14 12:33:53  2023-11-14 12:54:29  200.129.161.9   
7  1vXXcXvg3W0RfaG  2023-12-01 17:11:25  2023-12-01 17:54:03  200.129.161.9   
8  1vXXcXvg3W0RfaG  2023-12-01 18:00:09  2023-12-01 18:34:34  200.129.161.9   
9  1vXXcXvg3W0RfaG  2024-01-09 17:05:00  2024-01-09 17:47:00  200.129.161.9   

   identificacao_dado    tipo_envio  ano_referencia periodo_referencia  \
0                 NaN      ORIGINAL            2023            Janeiro   
1                 NaN      ORIGINAL            2023          Fevereiro   
2                 NaN      ORIGINAL            2023              Março   
3                 NaN      ORIGINAL            2023              Abril   
4                 NaN      ORIGINAL            2023               Maio   
5                 NaN      ORIGINAL            2023              Junho   
6                 NaN      ORIGINAL            2023              Julho   
7                 NaN      ORIGINAL            2023             Agosto   
8                 NaN      ORIGINAL            2023           Setembro   
9                 NaN  RETIFICADORA            2023            Outubro   

   identificacao_estabelecimento         municipio  \
0                            NaN  Manaus, Amazonas   
1                            NaN  Manaus, Amazonas   
2                            NaN  Manaus, Amazonas   
3                            NaN  Manaus, Amazonas   
4                            NaN  Manaus, Amazonas   
5                            NaN  Manaus, Amazonas   
6                            NaN  Manaus, Amazonas   
7                            NaN  Manaus, Amazonas   
8                            NaN  Manaus, Amazonas   
9                            NaN  Manaus, Amazonas   

                          razao_social_nome_fantasia  \
0  Fundação de Hemotologia e Hemoterapia do Amazo...   
1  Fundação de Hemotologia e Hemoterapia do Amazo...   
2  Fundação Hospitalar de Hematologia e Hemoterap...   
3  Fundação Hospitalar de Hematologia e Hemoterap...   
4  Fundação Hospitalar de Hematologia e Hemoterap...   
5  Fundação Hospitalar de Hematologia e Hemoterap...   
6  Fundação de Hemotologia e Hemoterapia do Amazo...   
7  Fundação de Hemotologia e Hemoterapia do Amazo...   
8  Fundação de Hemotologia e Hemoterapia do Amazo...   
9  Fundação de Hemotologia e Hemoterapia do Amazo...   

   razao_social_nome_fantasia_outros            cnpj    tipo_estabelecimento  \
0                                NaN  63678320000115  Hemocentro Coordenador   
1                                NaN  63678320000115  Hemocentro Coordenador   
2                                NaN  63678320000115  Hemocentro Coordenador   
3   

In [13]:
hemoprod_am.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 32 entries, 0 to 31
Columns: 269 entries, id to hemoprod_3_observacoes
dtypes: Int64(229), datetime64[ns](1), float64(27), object(12)
memory usage: 74.5+ KB


In [14]:
hemoprod_am_deduplicado.to_excel('dados_processados/hemoprod_am.xlsx', index=False)

## Hemoprod Amapa

In [19]:
import pandas as pd
import os

# --- 1. Defina os caminhos para seus arquivos ---
# Ajuste os caminhos conforme a estrutura do seu projeto no notebook
dados_brutos_path = 'dados_brutos'
dicionario_path = 'dicionario_colunas_269.xlsx'
arquivo_dados_path = os.path.join(dados_brutos_path, 'Hemoprod_AP.xlsx')
nome_planilha = 'HEMOPROD - AMAPA'

try:
    # Carrega o arquivo de dados
    hemoprod_ap = pd.read_excel(arquivo_dados_path, sheet_name=nome_planilha)
    print("Arquivo de dados carregado com sucesso.")
    print(f"Número de colunas original: {len(hemoprod_ap.columns)}")

    # Carrega o arquivo de dicionário
    dicionario = pd.read_excel(dicionario_path)
    print("Arquivo de dicionário carregado com sucesso.")

    # --- 3. Limpeza Inicial dos Nomes das Colunas (ADICIONADO) ---
    # Mapeia as colunas, limpando espaços em branco no início e fim
    # e substituindo o caractere \xa0 (Non-breaking space) por um espaço normal.
    mapa_limpeza = {
        col: col.strip().replace('\xa0', ' ') 
        for col in hemoprod_ap.columns
    }

    # Aplica a renomeação para limpar os nomes
    hemoprod_ap = hemoprod_ap.rename(columns=mapa_limpeza)
    print("Nomes das colunas do DataFrame limpos e padronizados (strip/\\xa0).")

    # --- 4. Crie o dicionário de mapeamento ---
    # Cria um dicionário no formato {'nome_original': 'nome_sql'} para uso no .rename()
    # NOTA: O 'nome_original' no dicionário TAMBÉM deve estar limpo para combinar.
    # Se o dicionário não estiver limpo, adicione a mesma limpeza aqui:
    dicionario['nome_original'] = dicionario['nome_original'].astype(str).str.strip().str.replace('\xa0', ' ')
    
    mapa_renomeacao = pd.Series(dicionario['nome_sql'].values, index=dicionario['nome_original']).to_dict()
    
    # Lista dos nomes de coluna no DataFrame atual APÓS a limpeza inicial
    colunas_atuais = set(hemoprod_ap.columns)
    
    # Lista dos nomes originais de coluna no dicionário APÓS a limpeza (se aplicada)
    colunas_originais_dicionario = set(dicionario['nome_original'].tolist())
    
    # Lista dos nomes SQL (os desejados) no dicionário
    colunas_sql_desejadas = set(dicionario['nome_sql'].tolist())
    
    # --- 5. Renomeie as colunas com base no mapeamento (nome_original -> nome_sql) ---
    print("\n--- Processo de Renomeação ---")
    hemoprod_ap.rename(columns=mapa_renomeacao, inplace=True)
    print("Colunas renomeadas com sucesso (apenas as que existiam no dicionário foram modificadas).")


   # --- 4. Inferir Tipos e Criar Mapeamento de Tipos ---
    
    # --- Lógica de Inferência customizada para 'Int64' ---
    tipos_inferidos = {}
    for col in hemoprod_ap.columns:
        
        # 4.1. Tenta converter a coluna para o tipo que melhor representa seus dados (incluindo Int64/string/datetime)
        # O errors='ignore' é crucial para não falhar se a coluna não puder ser convertida
        coluna_convertida = pd.to_numeric(hemoprod_ap[col], errors='coerce')
        
        # Se a conversão for bem-sucedida (não é totalmente NaN, nem totalmente string)
        if not coluna_convertida.isna().all() and coluna_convertida.dtype.kind in 'fi': # 'f' para float, 'i' para int
            
            # Se a coluna parecer um número, tentamos forçar para Int64
            # O .astype('Int64') usa o tipo inteiro que suporta NaN
            try:
                # Se for possível converter para Int64, use 'Int64'
                hemoprod_ap[col] = hemoprod_ap[col].astype('Int64')
                tipos_inferidos[col] = 'Int64'
            except Exception:
                # Se for numérico mas não puder ser Int64 (ex: float com muitas casas decimais), use 'float64'
                tipos_inferidos[col] = 'float64'
        
        # Verifica se é data/hora
        elif pd.api.types.is_datetime64_any_dtype(hemoprod_ap[col]):
             tipos_inferidos[col] = 'datetime64[ns]'
             
        # Caso contrário, assume-se que é um texto/string
        else:
            tipos_inferidos[col] = 'object' # O padrão para string no pandas

    
    print("\nTipos de dados inferidos (amostra):")
    for i, (col, dtype) in enumerate(tipos_inferidos.items()):
        if i < 5:
            print(f"  {col}: {dtype}")
        if i == 5:
            print("  ...")
    
    # --- 5. Atualizar o DataFrame Dicionário ---
    
    # 5.1. Cria a coluna 'tipo_dados' no dicionário e preenche com os tipos inferidos
    dicionario['tipo_dados'] = dicionario['nome_sql'].map(tipos_inferidos)
    
    # 5.2. Trata colunas não encontradas no DataFrame de dados
    dicionario['tipo_dados'] = dicionario['tipo_dados'].fillna('object')
    
    print("\n--- Dicionário Atualizado ---")
    print("Coluna 'tipo_dados' criada com sucesso, com numéricos definidos como 'Int64' ou 'float64'.")
    
    # --- 6. Salvar o Dicionário Atualizado ---

    # Sugestão de novo caminho para salvar
    # novo_dicionario_path = 'dicionario_colunas_269_COM_TIPOS_V3.xlsx'
    
    # dicionario.to_excel(novo_dicionario_path, index=False)
    
    print(f"\n✅ Dicionário salvo com a nova coluna 'tipo_dados' em: {novo_dicionario_path}")
    print("\nPrimeiras linhas do dicionário atualizado:")
    display(dicionario.head())

    # --- 6. Análise de Colunas (Qualidade dos Dados) ---

    # 6.1. Colunas que não puderam ser renomeadas (existem no DF, mas não no 'nome_original' do dicionário)
    # Aqui usamos as colunas atuais ANTES da renomeação para ver o que sobrou.
    colunas_nao_mapeadas = [
        col for col in colunas_atuais 
        if col not in colunas_originais_dicionario
    ]

    print("-" * 30)
    print("Análise de Colunas do DataFrame (hemoprod_ap):")
    print(f"Número de colunas não mapeadas: {len(colunas_nao_mapeadas)}")
    print(f"Colunas não mapeadas (manterão nome original): {colunas_nao_mapeadas}")
    
    # 6.2. Análise de Colunas Faltantes/A Mais (Comparação com 'nome_sql' desejado)
    colunas_apos_renomeacao = set(hemoprod_ap.columns)
    
    colunas_faltantes = list(colunas_sql_desejadas - colunas_apos_renomeacao)
    colunas_a_mais = list(colunas_apos_renomeacao - colunas_sql_desejadas)

    print("-" * 30)
    print("Análise de Colunas (Comparação com a lista SQL DESEJADA):")
    print(f"Número de colunas FALTANTES: {len(colunas_faltantes)}")
    print(f"Colunas FALTANTES (deveriam estar, mas não estão): {colunas_faltantes}")
    print("-" * 30)
    print(f"Número de colunas A MAIS: {len(colunas_a_mais)}")
    print(f"Colunas A MAIS (estão no DF, mas não na lista SQL desejada): {colunas_a_mais}")
    print("-" * 30)

    # --- 7. Verifique o resultado ---
    print("\nInformações do DataFrame com as novas colunas:")
    hemoprod_ap.info()
    
    print("\nAs 5 primeiras linhas com as novas colunas:")
    display(hemoprod_ap.head())

except FileNotFoundError as e:
    print(f"\nErro de arquivo não encontrado: {e}")
except KeyError as e:
    print(f"\nErro de coluna não encontrada: {e}. Verifique se as colunas 'nome_original' e 'nome_sql' existem no seu arquivo de dicionário.")
except Exception as e:
    print(f"\nOcorreu um erro inesperado: {e}")

Arquivo de dados carregado com sucesso.
Número de colunas original: 269
Arquivo de dicionário carregado com sucesso.
Nomes das colunas do DataFrame limpos e padronizados (strip/\xa0).

--- Processo de Renomeação ---
Colunas renomeadas com sucesso (apenas as que existiam no dicionário foram modificadas).

Tipos de dados inferidos (amostra):
  id: Int64
  data_envio: object
  ultima_pagina: Int64
  idioma_inicial: object
  semente: Int64
  ...

--- Dicionário Atualizado ---
Coluna 'tipo_dados' criada com sucesso, com numéricos definidos como 'Int64' ou 'float64'.

✅ Dicionário salvo com a nova coluna 'tipo_dados' em: dicionario_colunas_269_COM_TIPOS_V2.xlsx

Primeiras linhas do dicionário atualizado:


nome_original        nome_sql  \
0  ID da resposta              id   
1   Data de envio      data_envio   
2   Última página   ultima_pagina   
3  Idioma inicial  idioma_inicial   
4         Semente         semente   

                                          comentario tipo_dados  
0  Identificador único e chave primária da submis...      Int64  
1   Data e hora exatas do envio final do formulário.     object  
2  Título da última página do formulário acessada...      Int64  
3  Idioma selecionado no início do preenchimento ...     object  
4  Valor interno de semente/aleatorização (uso té...      Int64

------------------------------
Análise de Colunas do DataFrame (hemoprod_ap):
Número de colunas não mapeadas: 0
Colunas não mapeadas (manterão nome original): []
------------------------------
Análise de Colunas (Comparação com a lista SQL DESEJADA):
Número de colunas FALTANTES: 0
Colunas FALTANTES (deveriam estar, mas não estão): []
------------------------------
Número de colunas A MAIS: 0
Colunas A MAIS (estão no DF, mas não na lista SQL desejada): []
------------------------------

Informações do DataFrame com as novas colunas:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1 entries, 0 to 0
Columns: 269 entries, id to hemoprod_3_observacoes
dtypes: Int64(247), float64(8), object(14)
memory usage: 2.5+ KB

As 5 primeiras linhas com as novas colunas:


id           data_envio  ultima_pagina idioma_inicial     semente  \
0   8  2025-06-16 13:29:53              4          pt-BR  1663392622   

     codigo_acesso          data_inicio     data_ultima_acao              ip  \
0  oQ8x1U42tODTlWA  2025-06-16 12:28:39  2025-06-16 13:29:53  177.84.201.126   

   identificacao_dado    tipo_envio  ano_referencia periodo_referencia  \
0                 NaN  RETIFICADORA            2024        Consolidado   

   identificacao_estabelecimento      municipio  \
0                            NaN  Macapá, Amapá   

                          razao_social_nome_fantasia  \
0  Secretaria de Estado de Saúde do Amapá - Insti...   

   razao_social_nome_fantasia_outros           cnpj    tipo_estabelecimento  \
0                                NaN  1762561000190  Hemocentro Coordenador   

  natureza_estabelecimento dados_informados_referem_se  \
0                  Público            Rede de serviços   

                                rede_estabelecimento  cnes  endereco  \
0  Instituto de Hematologia e Hemoterapia do Amap...   NaN       NaN   

   triagem_clinica_total_doacao_espontanea_aptos  \
0                                           6228   

   triagem_clinica_total_doacao_espontanea_inaptos  \
0                                             1306   

   triagem_clinica_total_doacao_reposicao_aptos  \
0                                         10187   

   triagem_clinica_total_doacao_reposicao_inaptos  \
0                                            2806   

   triagem_clinica_total_doacao_autologa_aptos  \
0                                            0   

   triagem_clinica_total_doacao_autologa_inaptos  \
0                                              0   

   total_doador_primeira_vez_aptos  total_doador_primeira_vez_inaptos  \
0                             3712                               2052   

   total_doador_repeticao_aptos  total_doador_repeticao_inaptos  \
0                         12693                            2058   

   total_doador_esporadico_aptos  total_doador_esporadico_inaptos  \
0                              0                                0   

   total_doador_masculino_aptos  total_doador_masculino_inaptos  \
0                         10078                            1922   

   total_doador_feminino_aptos  total_doador_feminino_inaptos  \
0                         6338                           2190   

   total_doador_menor_de_18_anos_aptos  total_doador_menor_de_18_anos_inaptos  \
0                                  120                                     36   

   total_doador_18_ate_29_anos_aptos  total_doador_18_ate_29_anos_inaptos  \
0                               5180                                 1662   

   total_doador_acima_de_29_anos_aptos  total_doador_acima_de_29_anos_inaptos  \
0                                11117                                   2414   

   total_candidatos_inaptos_anemia_masculino  \
0                                          0   

   total_candidatos_inaptos_anemia_feminino  \
0                                         0   

   total_candidatos_inaptos_anemia_total  \
0                                    514   

   total_candidatos_inaptos_hipertensao_masculino  \
0                                               0   

   total_candidatos_inaptos_hipertensao_feminino  \
0                                              0   

   total_candidatos_inaptos_hipertensao_total  \
0                                         163   

   total_candidatos_inaptos_hipotensao_masculino  \
0                                              0   

   total_candidatos_inaptos_hipotensao_feminino  \
0                                             0   

   total_candidatos_inaptos_hipotensao_total  \
0                                          1   

   total_candidatos_inaptos_alcoolismo_masculino  \
0                                              0   

   total_candidatos_inaptos_alcoolismo_feminino  \
0                                             0   

   total

In [ ]:
# hemoprod_ap.head()

ID da resposta        Data de envio  Última página Idioma inicial  \
0               8  2025-06-16 13:29:53              4          pt-BR   

      Semente Código de acesso       Data de início  Data da última ação  \
0  1663392622  oQ8x1U42tODTlWA  2025-06-16 12:28:39  2025-06-16 13:29:53   

      Endereço IP  IDENTIFICAÇÃO DO DADO   \
0  177.84.201.126                     NaN   

  Tipo de Informação  Antes de responder ao formulário, declare o tipo de informação que será inserida.    \
0                                       RETIFICADORA                                                        

   Ano de referência  Período de referência  \
0                2024           Consolidado   

   IDENTIFICAÇÃO DO ESTABELECIMENTO       Município  \
0                                NaN  Macapá, Amapá   

                       Razão Social - Nome Fantasia   \
0  Secretaria de Estado de Saúde do Amapá - Insti...   

   Razão Social - Nome Fantasia  [Outros]           CNPJ  \
0                                     NaN  1762561000190   

  Tipo de estabelecimento Natureza do estabelecimento  \
0  Hemocentro Coordenador                     Público   

  Os dados informados referem-se à um(a):   \
0                         Rede de serviços   

  Cite os estabelecimentos que compõem a rede  Informe o Tipo de Estabelecimento, o Nome Fantasia e o Município de localização de cada um.   \
0  Instituto de Hematologia e Hemoterapia do Amap...                                                                                          

   CNES - Cadastro Nacional de Estabelecimentos de Saúde   Endereço  \
0                                                NaN            NaN   

   2. Triagem Clínica  2.1 Total de candidatos quanto ao tipo de doação  [Espontânea][Aptos]  \
0                                               6228                                           

   2. Triagem Clínica  2.1 Total de candidatos quanto ao tipo de doação  [Espontânea][Inaptos]  \
0                                               1306                                             

   2. Triagem Clínica  2.1 Total de candidatos quanto ao tipo de doação  [Reposição][Aptos]  \
0                                              10187                                          

   2. Triagem Clínica  2.1 Total de candidatos quanto ao tipo de doação  [Reposição][Inaptos]  \
0                                               2806                                            

   2. Triagem Clínica  2.1 Total de candidatos quanto ao tipo de doação  [Autóloga][Aptos]  \
0                                                  0                                         

   2. Triagem Clínica  2.1 Total de candidatos quanto ao tipo de doação  [Autóloga][Inaptos]  \
0                                                  0                                           

   2.2 Total de candidatos quanto ao tipo de doador  [Primeira vez][Aptos]  \
0                                               3712                         

   2.2 Total de candidatos quanto ao tipo de doador  [Primeira vez][Inaptos]  \
0                                               2052                           

   2.2 Total de candidatos quanto ao tipo de doador  [Repetição][Aptos]  \
0                                              12693                      

   2.2 Total de candidatos quanto ao tipo de doador  [Repetição][Inaptos]  \
0                                               2058                        

   2.2 Total de candidatos quanto ao tipo de doador  [Esporádico][Aptos]  \
0                                                  0                       

   2.2 Total de candidatos quanto ao tipo de doador  [Esporádico][Inaptos]  \
0                                                  0                         

   2.3 Total de candidatos quanto ao gênero do doador  [Masculino][Aptos]  \
0                                              10078                        

   2.3 Total de candidatos quanto ao gênero do doador  [Masculino][Ina

In [ ]:
# print("--- Nomes das Colunas (um por linha) ---")
# for coluna in hemoprod_ap.columns:
#     print(coluna + ",") 

--- Nomes das Colunas (um por linha) ---
ID da resposta,
Data de envio,
Última página,
Idioma inicial,
Semente,
Código de acesso,
Data de início,
Data da última ação,
Endereço IP,
IDENTIFICAÇÃO DO DADO ,
Tipo de Informação  Antes de responder ao formulário, declare o tipo de informação que será inserida.  ,
Ano de referência ,
Período de referência,
IDENTIFICAÇÃO DO ESTABELECIMENTO ,
Município,
Razão Social - Nome Fantasia ,
Razão Social - Nome Fantasia  [Outros],
CNPJ,
Tipo de estabelecimento,
Natureza do estabelecimento,
Os dados informados referem-se à um(a): ,
Cite os estabelecimentos que compõem a rede  Informe o Tipo de Estabelecimento, o Nome Fantasia e o Município de localização de cada um. ,
CNES - Cadastro Nacional de Estabelecimentos de Saúde ,
Endereço,
2. Triagem Clínica  2.1 Total de candidatos quanto ao tipo de doação  [Espontânea][Aptos],
2. Triagem Clínica  2.1 Total de candidatos quanto ao tipo de doação  [Espontânea][Inaptos],
2. Triagem Clínica  2.1 Total de candida

In [18]:
import os
import pandas as pd

dados_brutos_path = 'dados_brutos'

arquivo_dados_path = os.path.join(dados_brutos_path, 'Hemoprod_AP.xlsx')
nome_planilha = 'HEMOPROD - AMAPA'

dicionario_path_ap = ('./dicionario_colunas_269.xlsx')
# dicionario_path_ap = ('./dicionario_colunas_270.xlsx')

dicionario_ap = pd.read_excel(dicionario_path_ap, sheet_name='Sheet1')

# --- 2. Carregue os dados e o dicionário ---
try:
    # Carrega o arquivo de dados
    hemoprod_ap = pd.read_excel(arquivo_dados_path, sheet_name=nome_planilha)
    print("Arquivo de dados carregado com sucesso.")
    print(f"Número de colunas original: {len(hemoprod_ap.columns)}")

    # Carrega o arquivo de dicionário
    dicionario = pd.read_excel(dicionario_path_ap)
    print("Arquivo de dicionário carregado com sucesso.")

    # --- 3. Extraia a lista de novos nomes ---
    # Pega os valores da coluna 'nome_sql' e converte para uma lista
    novos_nomes = dicionario['nome_sql'].tolist()
    print(f"Número de novos nomes no dicionário: {len(novos_nomes)}")

    # --- 4. Verificação de segurança (MUITO IMPORTANTE) ---
    # Garante que o número de colunas é o mesmo antes de renomear
    if len(hemoprod_ap.columns) == len(novos_nomes):
        print("\nO número de colunas corresponde. Renomeando...")
        
        # --- 5. Substitua os nomes das colunas ---
        # Esta é a linha principal que faz a substituição direta
        hemoprod_ap.columns = novos_nomes
        
        print("Colunas renomeadas com sucesso!")
        
        # --- 6. Verifique o resultado ---
        print("\nInformações do DataFrame com as novas colunas:")
        hemoprod_ap.info()
        
        print("\nAs 5 primeiras linhas com as novas colunas:")
        display(hemoprod_ap.head())

    else:
        # Mensagem de erro se o número de colunas for diferente
        print("\n--- ERRO ---")
        print("A renomeação foi cancelada. O número de colunas no arquivo de dados não é igual ao número de nomes no dicionário.")
        print(f"Colunas no arquivo de dados: {len(hemoprod_ap.columns)}")
        print(f"Nomes no dicionário: {len(novos_nomes)}")

except FileNotFoundError as e:
    print(f"\nErro de arquivo não encontrado: {e}")
except KeyError as e:
    print(f"\nErro de coluna não encontrada: {e}. Verifique se a coluna 'nome_sql' existe no seu arquivo de dicionário.")
except Exception as e:
    print(f"\nOcorreu um erro inesperado: {e}")



Arquivo de dados carregado com sucesso.
Número de colunas original: 269
Arquivo de dicionário carregado com sucesso.
Número de novos nomes no dicionário: 269

O número de colunas corresponde. Renomeando...
Colunas renomeadas com sucesso!

Informações do DataFrame com as novas colunas:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1 entries, 0 to 0
Columns: 269 entries, id to hemoprod_3_observacoes
dtypes: float64(8), int64(247), object(14)
memory usage: 2.2+ KB

As 5 primeiras linhas com as novas colunas:


id           data_envio  ultima_pagina idioma_inicial     semente  \
0   8  2025-06-16 13:29:53              4          pt-BR  1663392622   

     codigo_acesso          data_inicio     data_ultima_acao              ip  \
0  oQ8x1U42tODTlWA  2025-06-16 12:28:39  2025-06-16 13:29:53  177.84.201.126   

   identificacao_dado    tipo_envio  ano_referencia periodo_referencia  \
0                 NaN  RETIFICADORA            2024        Consolidado   

   identificacao_estabelecimento      municipio  \
0                            NaN  Macapá, Amapá   

                          razao_social_nome_fantasia  \
0  Secretaria de Estado de Saúde do Amapá - Insti...   

   razao_social_nome_fantasia_outros           cnpj    tipo_estabelecimento  \
0                                NaN  1762561000190  Hemocentro Coordenador   

  natureza_estabelecimento dados_informados_referem_se  \
0                  Público            Rede de serviços   

                                rede_estabelecimento  cnes  endereco  \
0  Instituto de Hematologia e Hemoterapia do Amap...   NaN       NaN   

   triagem_clinica_total_doacao_espontanea_aptos  \
0                                           6228   

   triagem_clinica_total_doacao_espontanea_inaptos  \
0                                             1306   

   triagem_clinica_total_doacao_reposicao_aptos  \
0                                         10187   

   triagem_clinica_total_doacao_reposicao_inaptos  \
0                                            2806   

   triagem_clinica_total_doacao_autologa_aptos  \
0                                            0   

   triagem_clinica_total_doacao_autologa_inaptos  \
0                                              0   

   total_doador_primeira_vez_aptos  total_doador_primeira_vez_inaptos  \
0                             3712                               2052   

   total_doador_repeticao_aptos  total_doador_repeticao_inaptos  \
0                         12693                            2058   

   total_doador_esporadico_aptos  total_doador_esporadico_inaptos  \
0                              0                                0   

   total_doador_masculino_aptos  total_doador_masculino_inaptos  \
0                         10078                            1922   

   total_doador_feminino_aptos  total_doador_feminino_inaptos  \
0                         6338                           2190   

   total_doador_menor_de_18_anos_aptos  total_doador_menor_de_18_anos_inaptos  \
0                                  120                                     36   

   total_doador_18_ate_29_anos_aptos  total_doador_18_ate_29_anos_inaptos  \
0                               5180                                 1662   

   total_doador_acima_de_29_anos_aptos  total_doador_acima_de_29_anos_inaptos  \
0                                11117                                   2414   

   total_candidatos_inaptos_anemia_masculino  \
0                                          0   

   total_candidatos_inaptos_anemia_feminino  \
0                                         0   

   total_candidatos_inaptos_anemia_total  \
0                                    514   

   total_candidatos_inaptos_hipertensao_masculino  \
0                                               0   

   total_candidatos_inaptos_hipertensao_feminino  \
0                                              0   

   total_candidatos_inaptos_hipertensao_total  \
0                                         163   

   total_candidatos_inaptos_hipotensao_masculino  \
0                                              0   

   total_candidatos_inaptos_hipotensao_feminino  \
0                                             0   

   total_candidatos_inaptos_hipotensao_total  \
0                                          1   

   total_candidatos_inaptos_alcoolismo_masculino  \
0                                              0   

   total_candidatos_inaptos_alcoolismo_feminino  \
0                                             0   

   total

In [26]:
# --- 2. Defina as colunas para a chave e para ordenação ---
registros_antes = len(hemoprod_ap)
print(f"Total de registros ANTES da remoção de duplicatas: {registros_antes}")
    

colunas_chave = [
        'cnpj', 
        'ano_referencia', 
        'periodo_referencia', 
        'razao_social_nome_fantasia'
    ]

coluna_data = 'data_envio'

# --- 3. Verifique se as colunas necessárias existem ---
colunas_necessarias = colunas_chave + [coluna_data]

if not all(col in hemoprod_ap.columns for col in colunas_necessarias):
    print("\n--- ERRO ---")
    print("Uma ou mais colunas necessárias para a deduplicação não foram encontradas.")
    colunas_faltantes = [col for col in colunas_necessarias if col not in hemoprod_ap.columns]
    print(f"Colunas necessárias: {colunas_necessarias}")
    print(f"Colunas faltantes no DataFrame: {colunas_faltantes}")
else:
    # --- 4. Prepare a coluna de data e ordene os dados ---
    # Converte a coluna 'data_envio' para datetime para garantir a ordenação correta.
    # 'errors='coerce'' transformará datas inválidas em NaT (Not a Time), que são tratadas como nulas.
    hemoprod_ap[coluna_data] = pd.to_datetime(hemoprod_ap[coluna_data], errors='coerce')

    # Ordena o DataFrame. Os registros com data de envio mais recente ficarão por último.
    print(f"\nOrdenando os dados por '{coluna_data}'...")
    hemoprod_ap_ordenado = hemoprod_ap.sort_values(by=coluna_data, ascending=True)

    # --- 5. Identifique e separe os registros duplicados e únicos ---
    # Em vez de usar drop_duplicates() diretamente, vamos usar duplicated()
    # para criar uma máscara booleana.
    # 'keep='last'' marca todas as ocorrências de uma chave como True, EXCETO a última (a mais recente).
    print(f"Identificando duplicatas com base na chave: {colunas_chave}...")
    mascara_duplicatas = hemoprod_ap_ordenado.duplicated(subset=colunas_chave, keep='last')

    # O DataFrame de removidos conterá todas as linhas marcadas como True
    hemoprod_removidos = hemoprod_ap_ordenado[mascara_duplicatas]
    
    # O DataFrame deduplicado conterá o INVERSO (~) da máscara (linhas marcadas como False)
    hemoprod_ap_deduplicado = hemoprod_ap_ordenado[~mascara_duplicatas]
    
    # Agora podemos contar os registros diretamente dos novos DataFrames
    registros_depois = len(hemoprod_ap_deduplicado)
    registros_removidos = len(hemoprod_removidos) 
    
    # --- 6. Exiba o resultado ---
    print("\n--- Processo Concluído ---")
    print(f"Registros removidos: {registros_removidos}")
    print(f"Total de registros DEPOIS da remoção de duplicatas: {registros_depois}")

    # (Opcional) Exibe a amostra dos removidos
    print("\nAmostra dos dados REMOVIDOS (os mais antigos/duplicados):")
    display(hemoprod_removidos.head(10))

    # Você pode continuar a usar o DataFrame 'hemoprod_ap_deduplicado' para suas análises
    print("\nAmostra dos dados únicos (os mais recentes para cada chave):")
    display(hemoprod_ap_deduplicado.head(10))
    
    # Agora você tem o DataFrame 'hemoprod_removidos' salvo

Total de registros ANTES da remoção de duplicatas: 1

Ordenando os dados por 'data_envio'...
Identificando duplicatas com base na chave: ['cnpj', 'ano_referencia', 'periodo_referencia', 'razao_social_nome_fantasia']...

--- Processo Concluído ---
Registros removidos: 0
Total de registros DEPOIS da remoção de duplicatas: 1

Amostra dos dados REMOVIDOS (os mais antigos/duplicados):


Empty DataFrame
Columns: [id, data_envio, ultima_pagina, idioma_inicial, semente, codigo_acesso, data_inicio, data_ultima_acao, ip, identificacao_dado, tipo_envio, ano_referencia, periodo_referencia, identificacao_estabelecimento, municipio, razao_social_nome_fantasia, razao_social_nome_fantasia_outros, cnpj, tipo_estabelecimento, natureza_estabelecimento, dados_informados_referem_se, rede_estabelecimento, cnes, endereco, triagem_clinica_total_doacao_espontanea_aptos, triagem_clinica_total_doacao_espontanea_inaptos, triagem_clinica_total_doacao_reposicao_aptos, triagem_clinica_total_doacao_reposicao_inaptos, triagem_clinica_total_doacao_autologa_aptos, triagem_clinica_total_doacao_autologa_inaptos, total_doador_primeira_vez_aptos, total_doador_primeira_vez_inaptos, total_doador_repeticao_aptos, total_doador_repeticao_inaptos, total_doador_esporadico_aptos, total_doador_esporadico_inaptos, total_doador_masculino_aptos, total_doador_masculino_inaptos, total_doador_feminino_aptos, total_doador_feminino_inaptos, total_doador_menor_de_18_anos_aptos, total_doador_menor_de_18_anos_inaptos, total_doador_18_ate_29_anos_aptos, total_doador_18_ate_29_anos_inaptos, total_doador_acima_de_29_anos_aptos, total_doador_acima_de_29_anos_inaptos, total_candidatos_inaptos_anemia_masculino, total_candidatos_inaptos_anemia_feminino, total_candidatos_inaptos_anemia_total, total_candidatos_inaptos_hipertensao_masculino, total_candidatos_inaptos_hipertensao_feminino, total_candidatos_inaptos_hipertensao_total, total_candidatos_inaptos_hipotensao_masculino, total_candidatos_inaptos_hipotensao_feminino, total_candidatos_inaptos_hipotensao_total, total_candidatos_inaptos_alcoolismo_masculino, total_candidatos_inaptos_alcoolismo_feminino, total_candidatos_inaptos_alcoolismo_total, total_candidatos_inaptos_comportamento_risco_dst_masculino, total_candidatos_inaptos_comportamento_risco_dst_feminino, total_candidatos_inaptos_comportamento_risco_dst_total, total_candidatos_inaptos_uso_drogas_masculino, total_candidatos_inaptos_uso_drogas_feminino, total_candidatos_inaptos_uso_drogas_total, total_candidatos_inaptos_hepatite_masculino, total_candidatos_inaptos_hepatite_feminino, total_candidatos_inaptos_hepatite_total, total_candidatos_inaptos_doenca_chagas_masculino, total_candidatos_inaptos_doenca_chagas_feminino, total_candidatos_inaptos_doenca_chagas_total, total_candidatos_inaptos_malaria_masculino, total_candidatos_inaptos_malaria_feminino, total_candidatos_inaptos_malaria_total, total_candidatos_inaptos_outras_masculino, total_candidatos_inaptos_outras_feminino, total_candidatos_inaptos_outras_total, coleta_total_candidatos_desistentes, total_interrupcoes_coleta_dificuldade_puncao_venosa, total_interrupcoes_coleta_reacao_vagal, total_interrupcoes_coleta_outros_motivos, total_coletas_sangue_total, total_coletas_aferese, hemoprod_1_observacoes, exames_triagem_doenca_doenca_chagas_amostras_testadas, exames_triagem_doenca_doenca_chagas_amostras_reagentes, exames_triagem_doenca_hiv_amostras_testadas, exames_triagem_doenca_hiv_amostras_reagentes, exames_triagem_doenca_sifilis_amostras_testadas, `exames_triagem_doenca_sifilis_amostras_reagentes, exames_triagem_doenca_hepatite_b_hbs_ag_amostras_testadas, exames_triagem_doenca_hepatite_b_hbs_ag_amostras_reagentes, exames_triagem_doenca_hepatite_b_anti_hbc_amostras_testadas, exames_triagem_doenca_hepatite_b_anti_hbc_amostras_reagentes, exames_triagem_doenca_hepatite_c_amostras_testadas, exames_triagem_doenca_hepatite_c_amostras_reagentes, exames_triagem_doenca_htlv_i_ii_amostras_testadas, exames_triagem_doenca_htlv_i_ii_amostras_reagentes, exames_triagem_doenca_malaria_amostras_testadas, exames_triagem_doenca_malaria_amostras_reagentes, exames_triagem_doenca_hbv_teste_nat_amostras_testadas, ...]
Index: []


Amostra dos dados únicos (os mais recentes para cada chave):


id          data_envio  ultima_pagina idioma_inicial     semente  \
0   8 2025-06-16 13:29:53              4          pt-BR  1663392622   

     codigo_acesso          data_inicio     data_ultima_acao              ip  \
0  oQ8x1U42tODTlWA  2025-06-16 12:28:39  2025-06-16 13:29:53  177.84.201.126   

   identificacao_dado    tipo_envio  ano_referencia periodo_referencia  \
0                 NaN  RETIFICADORA            2024        Consolidado   

   identificacao_estabelecimento      municipio  \
0                            NaN  Macapá, Amapá   

                          razao_social_nome_fantasia  \
0  Secretaria de Estado de Saúde do Amapá - Insti...   

   razao_social_nome_fantasia_outros           cnpj    tipo_estabelecimento  \
0                                NaN  1762561000190  Hemocentro Coordenador   

  natureza_estabelecimento dados_informados_referem_se  \
0                  Público            Rede de serviços   

                                rede_estabelecimento  cnes  endereco  \
0  Instituto de Hematologia e Hemoterapia do Amap...   NaN       NaN   

   triagem_clinica_total_doacao_espontanea_aptos  \
0                                           6228   

   triagem_clinica_total_doacao_espontanea_inaptos  \
0                                             1306   

   triagem_clinica_total_doacao_reposicao_aptos  \
0                                         10187   

   triagem_clinica_total_doacao_reposicao_inaptos  \
0                                            2806   

   triagem_clinica_total_doacao_autologa_aptos  \
0                                            0   

   triagem_clinica_total_doacao_autologa_inaptos  \
0                                              0   

   total_doador_primeira_vez_aptos  total_doador_primeira_vez_inaptos  \
0                             3712                               2052   

   total_doador_repeticao_aptos  total_doador_repeticao_inaptos  \
0                         12693                            2058   

   total_doador_esporadico_aptos  total_doador_esporadico_inaptos  \
0                              0                                0   

   total_doador_masculino_aptos  total_doador_masculino_inaptos  \
0                         10078                            1922   

   total_doador_feminino_aptos  total_doador_feminino_inaptos  \
0                         6338                           2190   

   total_doador_menor_de_18_anos_aptos  total_doador_menor_de_18_anos_inaptos  \
0                                  120                                     36   

   total_doador_18_ate_29_anos_aptos  total_doador_18_ate_29_anos_inaptos  \
0                               5180                                 1662   

   total_doador_acima_de_29_anos_aptos  total_doador_acima_de_29_anos_inaptos  \
0                                11117                                   2414   

   total_candidatos_inaptos_anemia_masculino  \
0                                          0   

   total_candidatos_inaptos_anemia_feminino  \
0                                         0   

   total_candidatos_inaptos_anemia_total  \
0                                    514   

   total_candidatos_inaptos_hipertensao_masculino  \
0                                               0   

   total_candidatos_inaptos_hipertensao_feminino  \
0                                              0   

   total_candidatos_inaptos_hipertensao_total  \
0                                         163   

   total_candidatos_inaptos_hipotensao_masculino  \
0                                              0   

   total_candidatos_inaptos_hipotensao_feminino  \
0                                             0   

   total_candidatos_inaptos_hipotensao_total  \
0                                          1   

   total_candidatos_inaptos_alcoolismo_masculino  \
0                                              0   

   total_candidatos_inaptos_alcoolismo_feminino  \
0                                             0   

   total_c

In [29]:
hemoprod_ap_deduplicado.to_excel('dados_processados/hemoprod_ap.xlsx', index=False)

## Hemoprod Bahia

In [14]:
arquivo_dados_path = os.path.join(dados_brutos_path, 'Hemoprod_BA.xlsx')
nome_planilha = 'HEMOPROD - BAHIA'
hemoprod_ba = pd.read_excel(arquivo_dados_path, sheet_name=nome_planilha)
print("Arquivo de dados carregado com sucesso.")
print(f"Número de colunas original: {len(hemoprod_ba.columns)}")

try:
    # Lê apenas o cabeçalho do arquivo original para obter os nomes das colunas
    # df_original = pd.read_excel(arquivo_dados_path, nrows=0)
    colunas_originais = hemoprod_ba.columns.tolist()

    # Cria um novo DataFrame para o dicionário
    dicionario_df = pd.DataFrame({
        'nome_original': colunas_originais,
        'nome_sql': ''  # Adiciona uma coluna vazia para os novos nomes
    })

    # Salva o DataFrame do dicionário em um novo arquivo Excel
    dicionario_df.to_excel('dicionario_ba.xlsx', index=False)

    print(f"Arquivo de dicionário dicionario.xlsx gerado com sucesso!")
    print(f"O arquivo contém {len(colunas_originais)} colunas originais.")
    print("Agora você pode preencher a coluna 'nome_sql' com os nomes desejados.")

except FileNotFoundError:
    print(f"Erro: O arquivo de dados '{arquivo_dados_path}' não foi encontrado.")
except Exception as e:
    print(f"Ocorreu um erro inesperado: {e}")

Arquivo de dados carregado com sucesso.
Número de colunas original: 269
Arquivo de dicionário dicionario.xlsx gerado com sucesso!
O arquivo contém 269 colunas originais.
Agora você pode preencher a coluna 'nome_sql' com os nomes desejados.


In [30]:
import os
import pandas as pd

dados_brutos_path = 'dados_brutos'

arquivo_dados_path = os.path.join(dados_brutos_path, 'Hemoprod_BA.xlsx')
nome_planilha = 'HEMOPROD - BAHIA'

dicionario_path_ba = ('./dicionario_colunas_269.xlsx')
# dicionario_path_ap = ('./dicionario_colunas_270.xlsx')

dicionario_ba = pd.read_excel(dicionario_path_ba, sheet_name='Sheet1')

# --- 2. Carregue os dados e o dicionário ---
try:
    # Carrega o arquivo de dados
    hemoprod_ba = pd.read_excel(arquivo_dados_path, sheet_name=nome_planilha)
    print("Arquivo de dados carregado com sucesso.")
    print(f"Número de colunas original: {len(hemoprod_ba.columns)}")

    # Carrega o arquivo de dicionário
    dicionario = pd.read_excel(dicionario_path_ba)
    print("Arquivo de dicionário carregado com sucesso.")

    # --- 3. Extraia a lista de novos nomes ---
    # Pega os valores da coluna 'nome_sql' e converte para uma lista
    novos_nomes = dicionario['nome_sql'].tolist()
    print(f"Número de novos nomes no dicionário: {len(novos_nomes)}")

    # --- 4. Verificação de segurança (MUITO IMPORTANTE) ---
    # Garante que o número de colunas é o mesmo antes de renomear
    if len(hemoprod_ba.columns) == len(novos_nomes):
        print("\nO número de colunas corresponde. Renomeando...")
        
        # --- 5. Substitua os nomes das colunas ---
        # Esta é a linha principal que faz a substituição direta
        hemoprod_ba.columns = novos_nomes
        
        print("Colunas renomeadas com sucesso!")
        
        # --- 6. Verifique o resultado ---
        print("\nInformações do DataFrame com as novas colunas:")
        hemoprod_ba.info()
        
        print("\nAs 5 primeiras linhas com as novas colunas:")
        display(hemoprod_ba.head())

    else:
        # Mensagem de erro se o número de colunas for diferente
        print("\n--- ERRO ---")
        print("A renomeação foi cancelada. O número de colunas no arquivo de dados não é igual ao número de nomes no dicionário.")
        print(f"Colunas no arquivo de dados: {len(hemoprod_ba.columns)}")
        print(f"Nomes no dicionário: {len(novos_nomes)}")

except FileNotFoundError as e:
    print(f"\nErro de arquivo não encontrado: {e}")
except KeyError as e:
    print(f"\nErro de coluna não encontrada: {e}. Verifique se a coluna 'nome_sql' existe no seu arquivo de dicionário.")
except Exception as e:
    print(f"\nOcorreu um erro inesperado: {e}")



Arquivo de dados carregado com sucesso.
Número de colunas original: 269
Arquivo de dicionário carregado com sucesso.
Número de novos nomes no dicionário: 269

O número de colunas corresponde. Renomeando...
Colunas renomeadas com sucesso!

Informações do DataFrame com as novas colunas:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 975 entries, 0 to 974
Columns: 269 entries, id to hemoprod_3_observacoes
dtypes: float64(247), int64(4), object(18)
memory usage: 2.0+ MB

As 5 primeiras linhas com as novas colunas:


id           data_envio  ultima_pagina idioma_inicial       semente  \
0   8  2023-06-23 10:10:16              4          pt-BR  2.080744e+09   
1  14  2023-07-03 10:51:45              4          pt-BR  1.347364e+09   
2  15  2023-07-03 11:05:14              4          pt-BR  1.577556e+09   
3  16  2023-07-03 11:39:48              4          pt-BR  2.101298e+09   
4  17  2023-07-03 11:53:51              4          pt-BR  1.447849e+09   

     codigo_acesso          data_inicio     data_ultima_acao          ip  \
0  HmkD8Fq6Obb0Spm  2023-06-23 09:53:53  2023-06-23 10:10:16  10.0.0.119   
1  7wrQGPKvZXmav1F  2023-07-03 10:28:12  2023-07-03 10:51:45  10.0.0.205   
2  7wrQGPKvZXmav1F  2023-07-03 10:54:08  2023-07-03 11:05:14   10.0.0.81   
3  7wrQGPKvZXmav1F  2023-07-03 11:07:27  2023-07-03 11:39:48  10.0.0.155   
4  7wrQGPKvZXmav1F  2023-07-03 11:40:45  2023-07-03 11:53:51  10.0.0.224   

   identificacao_dado tipo_envio  ano_referencia periodo_referencia  \
0                 NaN   ORIGINAL            2023              Junho   
1                 NaN   ORIGINAL            2023              Junho   
2                 NaN   ORIGINAL            2023              Junho   
3                 NaN   ORIGINAL            2023              Junho   
4                 NaN   ORIGINAL            2023              Junho   

   identificacao_estabelecimento            municipio  \
0                            NaN  Paulo Afonso, Bahia   
1                            NaN      Salvador, Bahia   
2                            NaN      Salvador, Bahia   
3                            NaN      Salvador, Bahia   
4                            NaN      Salvador, Bahia   

                          razao_social_nome_fantasia  \
0  Fundação de Hemoterapia e Hematologia do Estad...   
1  Hemato Serviços de Hemoterapia Ltda - AgênciaT...   
2  Hemato Serviços de Hemoterapia Ltda - Hospital...   
3  Hemato Serviços de Hemoterapia Ltda - Hospital...   
4  Hemato Serviços de Hemoterapia Ltda - Hospital...   

  razao_social_nome_fantasia_outros            cnpj  \
0                               NaN  34306340000167   
1                               NaN  13894995001952   
2                               NaN  13894995002924   
3                               NaN  13894995002096   
4                               NaN  13894995002177   

             tipo_estabelecimento natureza_estabelecimento  \
0  Unidade de Coleta e Transfusão                  Público   
1          Agência Transfusional                   Privado   
2          Agência Transfusional                   Privado   
3          Agência Transfusional                   Privado   
4          Agência Transfusional                   Privado   

  dados_informados_referem_se rede_estabelecimento  cnes  endereco  \
0               Único serviço                  NaN   NaN       NaN   
1               Único serviço                  NaN   NaN       NaN   
2               Único serviço                  NaN   NaN       NaN   
3               Único serviço                  NaN   NaN       NaN   
4               Único serviço                  NaN   NaN       NaN   

   triagem_clinica_total_doacao_espontanea_aptos  \
0                                           72.0   
1                                            NaN   
2                                            NaN   
3                                            NaN   
4                                            NaN   

   triagem_clinica_total_doacao_espontanea_inaptos  \
0                                              7.0   
1                                              NaN   
2                                              NaN   
3                                              NaN   
4                                              NaN   

   triagem_clinica_total_doacao_reposicao_aptos  \
0                                         169.0   
1                                           NaN   
2                                           NaN   
3                          

In [31]:
# --- 2. Defina as colunas para a chave e para ordenação ---
registros_antes = len(hemoprod_ba)
print(f"Total de registros ANTES da remoção de duplicatas: {registros_antes}")
    

colunas_chave = [
        'cnpj', 
        'ano_referencia', 
        'periodo_referencia', 
        'razao_social_nome_fantasia'
    ]

coluna_data = 'data_envio'

# --- 3. Verifique se as colunas necessárias existem ---
colunas_necessarias = colunas_chave + [coluna_data]

if not all(col in hemoprod_ba.columns for col in colunas_necessarias):
    print("\n--- ERRO ---")
    print("Uma ou mais colunas necessárias para a deduplicação não foram encontradas.")
    colunas_faltantes = [col for col in colunas_necessarias if col not in hemoprod_ba.columns]
    print(f"Colunas necessárias: {colunas_necessarias}")
    print(f"Colunas faltantes no DataFrame: {colunas_faltantes}")
else:
    # --- 4. Prepare a coluna de data e ordene os dados ---
    # Converte a coluna 'data_envio' para datetime para garantir a ordenação correta.
    # 'errors='coerce'' transformará datas inválidas em NaT (Not a Time), que são tratadas como nulas.
    hemoprod_ba[coluna_data] = pd.to_datetime(hemoprod_ba[coluna_data], errors='coerce')

    # Ordena o DataFrame. Os registros com data de envio mais recente ficarão por último.
    print(f"\nOrdenando os dados por '{coluna_data}'...")
    hemoprod_ba_ordenado = hemoprod_ba.sort_values(by=coluna_data, ascending=True)

    # --- 5. Identifique e separe os registros duplicados e únicos ---
    # Em vez de usar drop_duplicates() diretamente, vamos usar duplicated()
    # para criar uma máscara booleana.
    # 'keep='last'' marca todas as ocorrências de uma chave como True, EXCETO a última (a mais recente).
    print(f"Identificando duplicatas com base na chave: {colunas_chave}...")
    mascara_duplicatas = hemoprod_ba_ordenado.duplicated(subset=colunas_chave, keep='last')

    # O DataFrame de removidos conterá todas as linhas marcadas como True
    hemoprod_removidos = hemoprod_ba_ordenado[mascara_duplicatas]
    
    # O DataFrame deduplicado conterá o INVERSO (~) da máscara (linhas marcadas como False)
    hemoprod_ba_deduplicado = hemoprod_ba_ordenado[~mascara_duplicatas]
    
    # Agora podemos contar os registros diretamente dos novos DataFrames
    registros_depois = len(hemoprod_ba_deduplicado)
    registros_removidos = len(hemoprod_removidos) 
    
    # --- 6. Exiba o resultado ---
    print("\n--- Processo Concluído ---")
    print(f"Registros removidos: {registros_removidos}")
    print(f"Total de registros DEPOIS da remoção de duplicatas: {registros_depois}")

    # (Opcional) Exibe a amostra dos removidos
    print("\nAmostra dos dados REMOVIDOS (os mais antigos/duplicados):")
    display(hemoprod_removidos.head(10))

    # Você pode continuar a usar o DataFrame 'hemoprod_ba_deduplicado' para suas análises
    print("\nAmostra dos dados únicos (os mais recentes para cada chave):")
    display(hemoprod_ba_deduplicado.head(10))
    
    # Agora você tem o DataFrame 'hemoprod_removidos' salvo

Total de registros ANTES da remoção de duplicatas: 975

Ordenando os dados por 'data_envio'...
Identificando duplicatas com base na chave: ['cnpj', 'ano_referencia', 'periodo_referencia', 'razao_social_nome_fantasia']...

--- Processo Concluído ---
Registros removidos: 267
Total de registros DEPOIS da remoção de duplicatas: 708

Amostra dos dados REMOVIDOS (os mais antigos/duplicados):


id          data_envio  ultima_pagina idioma_inicial       semente  \
15   35 2023-07-25 18:57:03              4          pt-BR  8.145631e+08   
43   80 2023-08-29 10:07:51              4          pt-BR  5.958126e+08   
45   82 2023-08-29 10:30:05              4          pt-BR  5.452058e+08   
49   86 2023-08-29 11:04:52              4          pt-BR  2.571943e+08   
48   85 2023-08-29 11:18:03              4          pt-BR  1.370018e+09   
64  102 2023-08-30 15:22:09              4          pt-BR  1.818467e+09   
68  106 2023-09-05 16:39:34              4          pt-BR  9.265733e+08   
83  122 2023-09-14 11:12:59              4          pt-BR  1.138337e+09   
84  123 2023-09-14 11:35:25              4          pt-BR  9.184684e+08   
85  124 2023-09-14 11:53:47              4          pt-BR  9.135868e+08   

      codigo_acesso          data_inicio     data_ultima_acao          ip  \
15  DzGNznkdlkYXGXd  2023-07-25 17:53:17  2023-07-25 18:57:03  10.0.1.142   
43  imTjpvSprA4zOL8  2023-08-29 09:11:27  2023-08-29 10:07:51  10.0.1.142   
45  imTjpvSprA4zOL8  2023-08-29 10:12:30  2023-08-29 10:30:05   10.0.0.14   
49  imTjpvSprA4zOL8  2023-08-29 10:49:50  2023-08-29 11:04:52  10.0.1.165   
48  JJwphczDMci1pkA  2023-08-29 10:47:22  2023-08-29 11:18:03  10.0.1.142   
64  JJwphczDMci1pkA  2023-08-30 14:41:48  2023-08-30 15:22:09  10.0.1.142   
68  BYdy6aYsfjnKIfz  2023-09-05 16:08:21  2023-09-05 16:39:34  10.0.1.165   
83  WYaohNKxPeSzlHo  2023-09-14 10:31:58  2023-09-14 11:12:59  10.0.0.173   
84  WYaohNKxPeSzlHo  2023-09-14 11:14:35  2023-09-14 11:35:25  10.0.0.173   
85  WYaohNKxPeSzlHo  2023-09-14 11:36:33  2023-09-14 11:53:47  10.0.0.187   

    identificacao_dado    tipo_envio  ano_referencia periodo_referencia  \
15                 NaN  RETIFICADORA            2023            Janeiro   
43                 NaN      ORIGINAL            2023            Janeiro   
45                 NaN      ORIGINAL            2023            Janeiro   
49                 NaN      ORIGINAL            2023          Fevereiro   
48                 NaN      ORIGINAL            2023            Janeiro   
64                 NaN  RETIFICADORA            2023             Agosto   
68                 NaN      ORIGINAL            2023             Agosto   
83                 NaN      ORIGINAL            2023            Janeiro   
84                 NaN      ORIGINAL            2023          Fevereiro   
85                 NaN      ORIGINAL            2023              Março   

    identificacao_estabelecimento                 municipio  \
15                            NaN           Salvador, Bahia   
43                            NaN           Guanambi, Bahia   
45                            NaN           Guanambi, Bahia   
49                            NaN           Guanambi, Bahia   
48                            NaN  Ribeira do Pombal, Bahia   
64                            NaN  Ribeira do Pombal, Bahia   
68                            NaN           Salvador, Bahia   
83                            NaN          Itaberaba, Bahia   
84                            NaN          Itaberaba, Bahia   
85                            NaN          Itaberaba, Bahia   

                           razao_social_nome_fantasia  \
15  Fundação de Hemoterapia e Hematologia do Estad...   
43  Fundação de Hemoterapia e Hematologia do Estad...   
45  Fundação de Hemoterapia e Hematologia do Estad...   
49  Fundação de Hemoterapia e Hematologia do Estad...   
48  Fundação de Hemoterapia e Hematologia do Estad...   
64  Fundação de Hemoterapia e Hematologia do Estad...   
68  Fundação de Hemoterapia e Hematologia do Estad...   
83  Fundação de Hemoterapia e Hematologia do Estad...   
84  Fundação de Hemoterapia e Hematologia do Estad...   
85  Fundação de Hemoterapia e Hematologia do Estad...   

   razao_social_nome_fantasia_outros            cnpj  \
15                               NaN  34306340000167   
43                               NaN  34306340000167   
45             


Amostra dos dados únicos (os mais recentes para cada chave):


id          data_envio  ultima_pagina idioma_inicial       semente  \
0   8 2023-06-23 10:10:16              4          pt-BR  2.080744e+09   
1  14 2023-07-03 10:51:45              4          pt-BR  1.347364e+09   
2  15 2023-07-03 11:05:14              4          pt-BR  1.577556e+09   
3  16 2023-07-03 11:39:48              4          pt-BR  2.101298e+09   
4  17 2023-07-03 11:53:51              4          pt-BR  1.447849e+09   
5  18 2023-07-03 12:08:00              4          pt-BR           NaN   
6  19 2023-07-03 12:57:53              4          pt-BR  7.263269e+08   
7  20 2023-07-06 11:50:48              4          pt-BR  2.404039e+08   
8  26 2023-07-18 09:22:03              4          pt-BR  7.320812e+08   
9  28 2023-07-19 08:39:00              4          pt-BR  8.295624e+08   

     codigo_acesso          data_inicio     data_ultima_acao           ip  \
0  HmkD8Fq6Obb0Spm  2023-06-23 09:53:53  2023-06-23 10:10:16   10.0.0.119   
1  7wrQGPKvZXmav1F  2023-07-03 10:28:12  2023-07-03 10:51:45   10.0.0.205   
2  7wrQGPKvZXmav1F  2023-07-03 10:54:08  2023-07-03 11:05:14    10.0.0.81   
3  7wrQGPKvZXmav1F  2023-07-03 11:07:27  2023-07-03 11:39:48   10.0.0.155   
4  7wrQGPKvZXmav1F  2023-07-03 11:40:45  2023-07-03 11:53:51   10.0.0.224   
5  7wrQGPKvZXmav1F  2023-07-03 11:55:00  2023-07-03 12:08:00   10.0.0.187   
6  7wrQGPKvZXmav1F  2023-07-03 12:15:03  2023-07-03 12:57:53   10.0.0.155   
7  BYdy6aYsfjnKIfz  2023-07-06 11:22:05  2023-07-06 11:50:48   10.0.1.139   
8  EnVVfjbu4V8Lcnx  2023-07-18 08:49:19  2023-07-18 09:22:03  10.0.36.236   
9  EnVVfjbu4V8Lcnx  2023-07-19 08:18:04  2023-07-19 08:39:00   10.0.0.155   

   identificacao_dado tipo_envio  ano_referencia periodo_referencia  \
0                 NaN   ORIGINAL            2023              Junho   
1                 NaN   ORIGINAL            2023              Junho   
2                 NaN   ORIGINAL            2023              Junho   
3                 NaN   ORIGINAL            2023              Junho   
4                 NaN   ORIGINAL            2023              Junho   
5                 NaN   ORIGINAL            2023              Junho   
6                 NaN   ORIGINAL            2023              Junho   
7                 NaN   ORIGINAL            2023              Junho   
8                 NaN   ORIGINAL            2022        Consolidado   
9                 NaN   ORIGINAL            2023            Janeiro   

   identificacao_estabelecimento            municipio  \
0                            NaN  Paulo Afonso, Bahia   
1                            NaN      Salvador, Bahia   
2                            NaN      Salvador, Bahia   
3                            NaN      Salvador, Bahia   
4                            NaN      Salvador, Bahia   
5                            NaN      Salvador, Bahia   
6                            NaN      Salvador, Bahia   
7                            NaN      Salvador, Bahia   
8                            NaN      Salvador, Bahia   
9                            NaN      Salvador, Bahia   

                          razao_social_nome_fantasia  \
0  Fundação de Hemoterapia e Hematologia do Estad...   
1  Hemato Serviços de Hemoterapia Ltda - AgênciaT...   
2  Hemato Serviços de Hemoterapia Ltda - Hospital...   
3  Hemato Serviços de Hemoterapia Ltda - Hospital...   
4  Hemato Serviços de Hemoterapia Ltda - Hospital...   
5  Hemato Serviços de Hemoterapia Ltda - Hospital...   
6  Hemato Serviços de Hemoterapia Ltda - Hospital...   
7  Fundação de Hemoterapia e Hematologia do Estad...   
8  Secretaria de Saúde do Estado da Bahia - Hospi...   
9  Secretaria de Saúde do Estado da Bahia - Hospi...   

                   razao_social_nome_fantasia_outros            cnpj  \
0                                                NaN  34306340000167   
1                                                NaN  13894995001952   
2                                                NaN  13894995002924   
3                                   

In [32]:
hemoprod_ba_deduplicado.to_excel('dados_processados/hemoprod_ba.xlsx', index=False)

## Hemoprod Ceara

In [ ]:
import os
import pandas as pd

dados_brutos_path = 'dados_brutos'

arquivo_dados_path = os.path.join(dados_brutos_path, 'Hemoprod_CE.xlsx')
nome_planilha = 'Planilha1'

dicionario_path_ce = ('./dicionario_colunas_269.xlsx')
# dicionario_path_ap = ('./dicionario_colunas_270.xlsx')

dicionario_ce = pd.read_excel(dicionario_path_ce, sheet_name='Sheet1')

# --- 2. Carregue os dados e o dicionário ---
try:
    # Carrega o arquivo de dados
    hemoprod_ce = pd.read_excel(arquivo_dados_path, sheet_name=nome_planilha)
    print("Arquivo de dados carregado com sucesso.")
    print(f"Número de colunas original: {len(hemoprod_ce.columns)}")

    # Carrega o arquivo de dicionário
    dicionario = pd.read_excel(dicionario_path_ce)
    print("Arquivo de dicionário carregado com sucesso.")

    # --- 3. Extraia a lista de novos nomes ---
    # Pega os valores da coluna 'nome_sql' e converte para uma lista
    novos_nomes = dicionario['nome_sql'].tolist()
    print(f"Número de novos nomes no dicionário: {len(novos_nomes)}")

    # --- 4. Verificação de segurança (MUITO IMPORTANTE) ---
    # Garante que o número de colunas é o mesmo antes de renomear
    if len(hemoprod_ce.columns) == len(novos_nomes):
        print("\nO número de colunas corresponde. Renomeando...")
        
        # --- 5. Substitua os nomes das colunas ---
        # Esta é a linha principal que faz a substituição direta
        hemoprod_ce.columns = novos_nomes
        
        print("Colunas renomeadas com sucesso!")
        
        # --- 6. Verifique o resultado ---
        print("\nInformações do DataFrame com as novas colunas:")
        hemoprod_ce.info()
        
        print("\nAs 5 primeiras linhas com as novas colunas:")
        display(hemoprod_ce.head())

    else:
        # Mensagem de erro se o número de colunas for diferente
        print("\n--- ERRO ---")
        print("A renomeação foi cancelada. O número de colunas no arquivo de dados não é igual ao número de nomes no dicionário.")
        print(f"Colunas no arquivo de dados: {len(hemoprod_ce.columns)}")
        print(f"Nomes no dicionário: {len(novos_nomes)}")

except FileNotFoundError as e:
    print(f"\nErro de arquivo não encontrado: {e}")
except KeyError as e:
    print(f"\nErro de coluna não encontrada: {e}. Verifique se a coluna 'nome_sql' existe no seu arquivo de dicionário.")
except Exception as e:
    print(f"\nOcorreu um erro inesperado: {e}")



Arquivo de dados carregado com sucesso.
Número de colunas original: 269
Arquivo de dicionário carregado com sucesso.
Número de novos nomes no dicionário: 269

O número de colunas corresponde. Renomeando...
Colunas renomeadas com sucesso!

Informações do DataFrame com as novas colunas:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 228 entries, 0 to 227
Columns: 269 entries, id to hemoprod_3_observacoes
dtypes: datetime64[ns](3), float64(253), object(13)
memory usage: 479.3+ KB

As 5 primeiras linhas com as novas colunas:


id          data_envio  ultima_pagina idioma_inicial       semente  \
0   8.0 2023-04-06 15:58:18            4.0          pt-BR  4.992114e+08   
1   9.0 2023-04-13 16:24:27            4.0          pt-BR  1.541636e+09   
2  10.0 2023-04-14 11:50:10            4.0          pt-BR  6.238845e+08   
3  11.0 2023-05-08 13:07:37            4.0          pt-BR  1.913022e+08   
4  12.0 2023-06-05 12:49:59            4.0          pt-BR  5.152217e+08   

     codigo_acesso         data_inicio    data_ultima_acao            ip  \
0  s16oIPSgdM8DdUr 2023-04-06 15:20:49 2023-04-06 15:58:18  10.0.113.219   
1  s16oIPSgdM8DdUr 2023-04-13 15:49:43 2023-04-13 16:24:27  10.0.113.219   
2  s16oIPSgdM8DdUr 2023-04-14 11:13:36 2023-04-14 11:50:10    10.0.0.195   
3  s16oIPSgdM8DdUr 2023-05-08 12:47:48 2023-05-08 13:07:37    10.0.52.31   
4  s16oIPSgdM8DdUr 2023-06-05 12:35:25 2023-06-05 12:49:59      10.0.0.4   

   identificacao_dado tipo_envio  ano_referencia periodo_referencia  \
0                 NaN   ORIGINAL          2023.0              Março   
1                 NaN   ORIGINAL          2023.0            Janeiro   
2                 NaN   ORIGINAL          2023.0          Fevereiro   
3                 NaN   ORIGINAL          2023.0              Abril   
4                 NaN   ORIGINAL          2023.0               Maio   

   identificacao_estabelecimento         municipio  \
0                            NaN  Fortaleza, Ceará   
1                            NaN  Fortaleza, Ceará   
2                            NaN  Fortaleza, Ceará   
3                            NaN  Fortaleza, Ceará   
4                            NaN  Fortaleza, Ceará   

                          razao_social_nome_fantasia  \
0  Fujisan Centro de Hemoterapia e Hematologia do...   
1  Fujisan Centro de Hemoterapia e Hematologia do...   
2  Fujisan Centro de Hemoterapia e Hematologia do...   
3  Fujisan Centro de Hemoterapia e Hematologia do...   
4  Fujisan Centro de Hemoterapia e Hematologia do...   

   razao_social_nome_fantasia_outros          cnpj   tipo_estabelecimento  \
0                                NaN  7.871680e+12  Núcleo de Hemoterapia   
1                                NaN  7.871680e+12  Núcleo de Hemoterapia   
2                                NaN  7.871680e+12  Núcleo de Hemoterapia   
3                                NaN  7.871680e+12  Núcleo de Hemoterapia   
4                                NaN  7.871680e+12  Núcleo de Hemoterapia   

  natureza_estabelecimento dados_informados_referem_se rede_estabelecimento  \
0                  Privado               Único serviço                  NaN   
1                  Privado               Único serviço                  NaN   
2                  Privado               Único serviço                  NaN   
3                  Privado               Único serviço                  NaN   
4                  Privado               Único serviço                  NaN   

   cnes  endereco  triagem_clinica_total_doacao_espontanea_aptos  \
0   NaN       NaN                                          483.0   
1   NaN       NaN                                          358.0   
2   NaN       NaN                                          563.0   
3   NaN       NaN                                          564.0   
4   NaN       NaN                                          504.0   

   triagem_clinica_total_doacao_espontanea_inaptos  \
0                                            104.0   
1                                             38.0   
2                                             66.0   
3                                             67.0   
4                                            137.0   

   triagem_clinica_total_doacao_reposicao_aptos  \
0                                        1722.0   
1                                        1257.0   
2                                        1292.0   
3                                        1393.0   
4                                        2136.0   

   triagem_clinica_total_doac

In [40]:
# --- 2. Defina as colunas para a chave e para ordenação ---
registros_antes = len(hemoprod_ce)
print(f"Total de registros ANTES da remoção de duplicatas: {registros_antes}")
    

colunas_chave = [
        'cnpj', 
        'ano_referencia', 
        'periodo_referencia', 
        'razao_social_nome_fantasia'
    ]

coluna_data = 'data_envio'

# --- 3. Verifique se as colunas necessárias existem ---
colunas_necessarias = colunas_chave + [coluna_data]

if not all(col in hemoprod_ce.columns for col in colunas_necessarias):
    print("\n--- ERRO ---")
    print("Uma ou mais colunas necessárias para a deduplicação não foram encontradas.")
    colunas_faltantes = [col for col in colunas_necessarias if col not in hemoprod_ce.columns]
    print(f"Colunas necessárias: {colunas_necessarias}")
    print(f"Colunas faltantes no DataFrame: {colunas_faltantes}")
else:
    # --- 4. Prepare a coluna de data e ordene os dados ---
    # Converte a coluna 'data_envio' para datetime para garantir a ordenação correta.
    # 'errors='coerce'' transformará datas inválidas em NaT (Not a Time), que são tratadas como nulas.
    hemoprod_ce[coluna_data] = pd.to_datetime(hemoprod_ce[coluna_data], errors='coerce')

    # Ordena o DataFrame. Os registros com data de envio mais recente ficarão por último.
    print(f"\nOrdenando os dados por '{coluna_data}'...")
    hemoprod_ce_ordenado = hemoprod_ce.sort_values(by=coluna_data, ascending=True)

    # --- 5. Identifique e separe os registros duplicados e únicos ---
    # Em vez de usar drop_duplicates() diretamente, vamos usar duplicated()
    # para criar uma máscara booleana.
    # 'keep='last'' marca todas as ocorrências de uma chave como True, EXCETO a última (a mais recente).
    print(f"Identificando duplicatas com cese na chave: {colunas_chave}...")
    mascara_duplicatas = hemoprod_ce_ordenado.duplicated(subset=colunas_chave, keep='last')

    # O DataFrame de removidos conterá todas as linhas marcadas como True
    hemoprod_removidos = hemoprod_ce_ordenado[mascara_duplicatas]
    
    # O DataFrame deduplicado conterá o INVERSO (~) da máscara (linhas marcadas como False)
    hemoprod_ce_deduplicado = hemoprod_ce_ordenado[~mascara_duplicatas]
    
    # Agora podemos contar os registros diretamente dos novos DataFrames
    registros_depois = len(hemoprod_ce_deduplicado)
    registros_removidos = len(hemoprod_removidos) 
    
    # --- 6. Exice o resultado ---
    print("\n--- Processo Concluído ---")
    print(f"Registros removidos: {registros_removidos}")
    print(f"Total de registros DEPOIS da remoção de duplicatas: {registros_depois}")

    # (Opcional) Exibe a amostra dos removidos
    print("\nAmostra dos dados REMOVIDOS (os mais antigos/duplicados):")
    display(hemoprod_removidos.head(10))

    # Você pode continuar a usar o DataFrame 'hemoprod_ce_deduplicado' para suas análises
    print("\nAmostra dos dados únicos (os mais recentes para cada chave):")
    display(hemoprod_ce_deduplicado.head(10))
    
    # Agora você tem o DataFrame 'hemoprod_removidos' salvo

Total de registros ANTES da remoção de duplicatas: 228

Ordenando os dados por 'data_envio'...
Identificando duplicatas com cese na chave: ['cnpj', 'ano_referencia', 'periodo_referencia', 'razao_social_nome_fantasia']...

--- Processo Concluído ---
Registros removidos: 162
Total de registros DEPOIS da remoção de duplicatas: 66

Amostra dos dados REMOVIDOS (os mais antigos/duplicados):


id          data_envio  ultima_pagina idioma_inicial       semente  \
170  180.0 2025-02-24 18:44:45            4.0          pt-BR  1.426538e+09   
183  185.0 2025-03-20 15:08:49            4.0          pt-BR  4.062604e+08   
11     NaN                 NaT            NaN            NaN           NaN   
12     NaN                 NaT            NaN            NaN           NaN   
13     NaN                 NaT            NaN            NaN           NaN   
14     NaN                 NaT            NaN            NaN           NaN   
15     NaN                 NaT            NaN            NaN           NaN   
17     NaN                 NaT            NaN            NaN           NaN   
18     NaN                 NaT            NaN            NaN           NaN   
19     NaN                 NaT            NaN            NaN           NaN   

       codigo_acesso         data_inicio    data_ultima_acao              ip  \
170  Qg5Ni6JhOAJCeU3 2025-02-24 18:17:55 2025-02-24 18:44:45  189.90.161.242   
183  Qg5Ni6JhOAJCeU3 2025-03-20 13:47:35 2025-03-20 15:08:49  189.90.161.242   
11               NaN                 NaT                 NaT             NaN   
12               NaN                 NaT                 NaT             NaN   
13               NaN                 NaT                 NaT             NaN   
14               NaN                 NaT                 NaT             NaN   
15               NaN                 NaT                 NaT             NaN   
17               NaN                 NaT                 NaT             NaN   
18               NaN                 NaT                 NaT             NaN   
19               NaN                 NaT                 NaT             NaN   

     identificacao_dado    tipo_envio  ano_referencia periodo_referencia  \
170                 NaN      ORIGINAL          2025.0            Janeiro   
183                 NaN  RETIFICADORA          2025.0            Janeiro   
11                  NaN           NaN             NaN                NaN   
12                  NaN           NaN             NaN                NaN   
13                  NaN           NaN             NaN                NaN   
14                  NaN           NaN             NaN                NaN   
15                  NaN           NaN             NaN                NaN   
17                  NaN           NaN             NaN                NaN   
18                  NaN           NaN             NaN                NaN   
19                  NaN           NaN             NaN                NaN   

     identificacao_estabelecimento         municipio  \
170                            NaN  Fortaleza, Ceará   
183                            NaN  Fortaleza, Ceará   
11                             NaN               NaN   
12                             NaN               NaN   
13                             NaN               NaN   
14                             NaN               NaN   
15                             NaN               NaN   
17                             NaN               NaN   
18                             NaN               NaN   
19                             NaN               NaN   

                            razao_social_nome_fantasia  \
170  Secretaria de Estado de Saúde do Ceará - Centr...   
183  Secretaria de Estado de Saúde do Ceará - Centr...   
11                                                 NaN   
12                                                 NaN   
13                                                 NaN   
14                                                 NaN   
15                                                 NaN   
17                                                 NaN   
18                                                 NaN   
19                                                 NaN   

     razao_social_nome_fantasia_outros          cnpj    tipo_estabelecimento  \
170                                NaN  7.954570e+12  Hemocentro Coordenador   
183            


Amostra dos dados únicos (os mais recentes para cada chave):


id          data_envio  ultima_pagina idioma_inicial       semente  \
0    8.0 2023-04-06 15:58:18            4.0          pt-BR  4.992114e+08   
1    9.0 2023-04-13 16:24:27            4.0          pt-BR  1.541636e+09   
2   10.0 2023-04-14 11:50:10            4.0          pt-BR  6.238845e+08   
3   11.0 2023-05-08 13:07:37            4.0          pt-BR  1.913022e+08   
4   12.0 2023-06-05 12:49:59            4.0          pt-BR  5.152217e+08   
5   13.0 2023-07-06 12:31:00            4.0          pt-BR  1.195322e+08   
6   27.0 2023-08-07 15:22:16            4.0          pt-BR  1.786051e+09   
7   71.0 2023-09-06 14:46:06            4.0          pt-BR  5.018145e+08   
8  122.0 2023-10-11 11:16:26            4.0          pt-BR  1.697986e+09   
9  125.0 2023-11-07 11:38:48            4.0          pt-BR  1.177000e+09   

     codigo_acesso         data_inicio    data_ultima_acao             ip  \
0  s16oIPSgdM8DdUr 2023-04-06 15:20:49 2023-04-06 15:58:18   10.0.113.219   
1  s16oIPSgdM8DdUr 2023-04-13 15:49:43 2023-04-13 16:24:27   10.0.113.219   
2  s16oIPSgdM8DdUr 2023-04-14 11:13:36 2023-04-14 11:50:10     10.0.0.195   
3  s16oIPSgdM8DdUr 2023-05-08 12:47:48 2023-05-08 13:07:37     10.0.52.31   
4  s16oIPSgdM8DdUr 2023-06-05 12:35:25 2023-06-05 12:49:59       10.0.0.4   
5  s16oIPSgdM8DdUr 2023-07-06 12:18:24 2023-07-06 12:31:00      10.0.0.39   
6  s16oIPSgdM8DdUr 2023-08-07 15:08:52 2023-08-07 15:22:16     10.0.0.173   
7  s16oIPSgdM8DdUr 2023-09-06 14:15:36 2023-09-06 14:46:06     10.0.1.139   
8  s16oIPSgdM8DdUr 2023-10-11 10:59:37 2023-10-11 11:16:26  201.20.107.34   
9  s16oIPSgdM8DdUr 2023-11-07 11:20:21 2023-11-07 11:38:48  201.20.107.34   

   identificacao_dado tipo_envio  ano_referencia periodo_referencia  \
0                 NaN   ORIGINAL          2023.0              Março   
1                 NaN   ORIGINAL          2023.0            Janeiro   
2                 NaN   ORIGINAL          2023.0          Fevereiro   
3                 NaN   ORIGINAL          2023.0              Abril   
4                 NaN   ORIGINAL          2023.0               Maio   
5                 NaN   ORIGINAL          2023.0              Junho   
6                 NaN   ORIGINAL          2023.0              Julho   
7                 NaN   ORIGINAL          2023.0             Agosto   
8                 NaN   ORIGINAL          2023.0           Setembro   
9                 NaN   ORIGINAL          2023.0            Outubro   

   identificacao_estabelecimento         municipio  \
0                            NaN  Fortaleza, Ceará   
1                            NaN  Fortaleza, Ceará   
2                            NaN  Fortaleza, Ceará   
3                            NaN  Fortaleza, Ceará   
4                            NaN  Fortaleza, Ceará   
5                            NaN  Fortaleza, Ceará   
6                            NaN  Fortaleza, Ceará   
7                            NaN  Fortaleza, Ceará   
8                            NaN  Fortaleza, Ceará   
9                            NaN  Fortaleza, Ceará   

                          razao_social_nome_fantasia  \
0  Fujisan Centro de Hemoterapia e Hematologia do...   
1  Fujisan Centro de Hemoterapia e Hematologia do...   
2  Fujisan Centro de Hemoterapia e Hematologia do...   
3  Fujisan Centro de Hemoterapia e Hematologia do...   
4  Fujisan Centro de Hemoterapia e Hematologia do...   
5  Fujisan Centro de Hemoterapia e Hematologia do...   
6  Fujisan Centro de Hemoterapia e Hematologia do...   
7  Fujisan Centro de Hemoterapia e Hematologia do...   
8  Fujisan Centro de Hemoterapia e Hematologia do...   
9  Fujisan Centro de Hemoterapia e Hematologia do...   

   razao_social_nome_fantasia_outros          cnpj   tipo_estabelecimento  \
0                                NaN  7.871680e+12  Núcleo de Hemoterapia   
1                                NaN  7.871680e+12  Núcleo de Hemoterapia   
2                                NaN  7.871680e+12  Núcleo de Hemoterapia   
3                  

In [41]:
hemoprod_ce_deduplicado.to_excel('dados_processados/hemoprod_ce.xlsx', index=False)

## Hemoprod Distrito Federal

In [42]:
import os
import pandas as pd

dados_brutos_path = 'dados_brutos'

arquivo_dados_path = os.path.join(dados_brutos_path, 'Hemoprod_DF.xlsx')
nome_planilha = 'HEMOPROD - DISTRITOFEDERAL'

dicionario_path_df = ('./dicionario_colunas_269.xlsx')
# dicionario_path_ap = ('./dicionario_colunas_270.xlsx')

dicionario_df = pd.read_excel(dicionario_path_df, sheet_name='Sheet1')

# --- 2. Carregue os dados e o dicionário ---
try:
    # Carrega o arquivo de dados
    hemoprod_df = pd.read_excel(arquivo_dados_path, sheet_name=nome_planilha)
    print("Arquivo de dados carregado com sucesso.")
    print(f"Número de colunas original: {len(hemoprod_df.columns)}")

    # Carrega o arquivo de dicionário
    dicionario = pd.read_excel(dicionario_path_df)
    print("Arquivo de dicionário carregado com sucesso.")

    # --- 3. Extraia a lista de novos nomes ---
    # Pega os valores da coluna 'nome_sql' e converte para uma lista
    novos_nomes = dicionario['nome_sql'].tolist()
    print(f"Número de novos nomes no dicionário: {len(novos_nomes)}")

    # --- 4. Verificação de segurança (MUITO IMPORTANTE) ---
    # Garante que o número de colunas é o mesmo antes de renomear
    if len(hemoprod_df.columns) == len(novos_nomes):
        print("\nO número de colunas corresponde. Renomeando...")
        
        # --- 5. Substitua os nomes das colunas ---
        # Esta é a linha principal que faz a substituição direta
        hemoprod_df.columns = novos_nomes
        
        print("Colunas renomeadas com sucesso!")
        
        # --- 6. Verifique o resultado ---
        print("\nInformações do DataFrame com as novas colunas:")
        hemoprod_df.info()
        
        print("\nAs 5 primeiras linhas com as novas colunas:")
        display(hemoprod_df.head())

    else:
        # Mensagem de erro se o número de colunas for diferente
        print("\n--- ERRO ---")
        print("A renomeação foi cancelada. O número de colunas no arquivo de dados não é igual ao número de nomes no dicionário.")
        print(f"Colunas no arquivo de dados: {len(hemoprod_df.columns)}")
        print(f"Nomes no dicionário: {len(novos_nomes)}")

except FileNotFoundError as e:
    print(f"\nErro de arquivo não encontrado: {e}")
except KeyError as e:
    print(f"\nErro de coluna não encontrada: {e}. Verifique se a coluna 'nome_sql' existe no seu arquivo de dicionário.")
except Exception as e:
    print(f"\nOcorreu um erro inesperado: {e}")



Arquivo de dados carregado com sucesso.
Número de colunas original: 269
Arquivo de dicionário carregado com sucesso.
Número de novos nomes no dicionário: 269

O número de colunas corresponde. Renomeando...
Colunas renomeadas com sucesso!

Informações do DataFrame com as novas colunas:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 184 entries, 0 to 183
Columns: 269 entries, id to hemoprod_3_observacoes
dtypes: float64(250), int64(4), object(15)
memory usage: 386.8+ KB

As 5 primeiras linhas com as novas colunas:


id           data_envio  ultima_pagina idioma_inicial  semente  \
0  11  2023-05-10 11:29:00              4          pt-BR      NaN   
1  12  2023-05-10 12:22:00              4          pt-BR      NaN   
2  14  2023-05-15 12:56:00              4          pt-BR      NaN   
3  15  2023-05-15 14:31:00              4          pt-BR      NaN   
4  16  2023-05-15 16:23:00              4          pt-BR      NaN   

     codigo_acesso          data_inicio     data_ultima_acao           ip  \
0  rPK9T4H3U3oa2a9  2023-05-10 11:01:00  2023-05-10 11:29:00    10.0.0.30   
1  MIXePx6p2p5vAoy  2023-05-10 12:03:00  2023-05-10 12:22:00    10.0.4.36   
2  WZ4ZIXCj3uWhwAH  2023-05-15 12:04:00  2023-05-15 12:56:00   10.0.3.242   
3  iehHllaeyrYagiU  2023-05-15 14:10:00  2023-05-15 14:31:00  10.0.51.170   
4  1aorcIMzUajACtF  2023-05-15 14:42:00  2023-05-15 16:23:00    10.0.0.84   

   identificacao_dado tipo_envio  ano_referencia periodo_referencia  \
0                 NaN   ORIGINAL            2023              Abril   
1                 NaN   ORIGINAL            2023              Abril   
2                 NaN   ORIGINAL            2023              Abril   
3                 NaN   ORIGINAL            2023              Abril   
4                 NaN   ORIGINAL            2023              Abril   

   identificacao_estabelecimento                   municipio  \
0                            NaN  Brasília, Distrito Federal   
1                            NaN  Brasília, Distrito Federal   
2                            NaN  Brasília, Distrito Federal   
3                            NaN  Brasília, Distrito Federal   
4                            NaN  Brasília, Distrito Federal   

                          razao_social_nome_fantasia  \
0  Grupo Gestor de Serviços em Hemoterapia (GSH) ...   
1  Grupo Gestor de Serviços em Hemoterapia (GSH) ...   
2  Grupo Gestor de Serviços em Hemoterapia (GSH) ...   
3  Grupo Gestor de Serviços em Hemoterapia (GSH) ...   
4  Grupo Gestor de Serviços em Hemoterapia (GSH) ...   

            razao_social_nome_fantasia_outros           cnpj  \
0               GSH - AT HOSPITAL SANTA LUZIA  8397078001841   
1              GSH - AT HOSPITAL SANTA HELENA  8397078002066   
2                 AT HOSPITAL SANTA LÚCIA SUL     8397078003   
3        BANCO DE SANGUE BRASÍLIA - GRUPO GSH  9397078002490   
4  AT Hosipital Santa Lucia Norte - Brasilia   8397078003038   

     tipo_estabelecimento natureza_estabelecimento  \
0  Agência Transfusional                   Privado   
1  Agência Transfusional                   Privado   
2  Agência Transfusional                   Privado   
3       Unidade de Coleta                  Privado   
4  Agência Transfusional                   Privado   

  dados_informados_referem_se  rede_estabelecimento  cnes  endereco  \
0               Único serviço                   NaN   NaN       NaN   
1               Único serviço                   NaN   NaN       NaN   
2               Único serviço                   NaN   NaN       NaN   
3               Único serviço                   NaN   NaN       NaN   
4               Único serviço                   NaN   NaN       NaN   

   triagem_clinica_total_doacao_espontanea_aptos  \
0                                            NaN   
1                                            NaN   
2                                            NaN   
3                                          247.0   
4                                            NaN   

   triagem_clinica_total_doacao_espontanea_inaptos  \
0                                              NaN   
1                                              NaN   
2                                              NaN   
3                                             33.0   
4                                              NaN   

   triagem_clinica_total_doacao_reposicao_aptos  \
0                                           NaN   
1                                           NaN   
2                                           NaN 

In [43]:
# --- 2. Defina as colunas para a chave e para ordenação ---
registros_antes = len(hemoprod_df)
print(f"Total de registros ANTES da remoção de duplicatas: {registros_antes}")
    

colunas_chave = [
        'cnpj', 
        'ano_referencia', 
        'periodo_referencia', 
        'razao_social_nome_fantasia'
    ]

coluna_data = 'data_envio'

# --- 3. Verifique se as colunas necessárias existem ---
colunas_necessarias = colunas_chave + [coluna_data]

if not all(col in hemoprod_df.columns for col in colunas_necessarias):
    print("\n--- ERRO ---")
    print("Uma ou mais colunas necessárias para a deduplicação não foram encontradas.")
    colunas_faltantes = [col for col in colunas_necessarias if col not in hemoprod_df.columns]
    print(f"Colunas necessárias: {colunas_necessarias}")
    print(f"Colunas faltantes no DataFrame: {colunas_faltantes}")
else:
    # --- 4. Prepare a coluna de data e ordene os dados ---
    # Converte a coluna 'data_envio' para datetime para garantir a ordenação correta.
    # 'errors='coerce'' transformará datas inválidas em NaT (Not a Time), que são tratadas como nulas.
    hemoprod_df[coluna_data] = pd.to_datetime(hemoprod_df[coluna_data], errors='coerce')

    # Ordena o DataFrame. Os registros com data de envio mais recente ficarão por último.
    print(f"\nOrdenando os dados por '{coluna_data}'...")
    hemoprod_df_ordenado = hemoprod_df.sort_values(by=coluna_data, ascending=True)

    # --- 5. Identifique e separe os registros duplicados e únicos ---
    # Em vez de usar drop_duplicates() diretamente, vamos usar duplicated()
    # para criar uma máscara booleana.
    # 'keep='last'' marca todas as ocorrências de uma chave como True, EXCETO a última (a mais recente).
    print(f"Identificando duplicatas com cese na chave: {colunas_chave}...")
    mascara_duplicatas = hemoprod_df_ordenado.duplicated(subset=colunas_chave, keep='last')

    # O DataFrame de removidos conterá todas as linhas marcadas como True
    hemoprod_removidos = hemoprod_df_ordenado[mascara_duplicatas]
    
    # O DataFrame deduplicado conterá o INVERSO (~) da máscara (linhas marcadas como False)
    hemoprod_df_deduplicado = hemoprod_df_ordenado[~mascara_duplicatas]
    
    # Agora podemos contar os registros diretamente dos novos DataFrames
    registros_depois = len(hemoprod_df_deduplicado)
    registros_removidos = len(hemoprod_removidos) 
    
    # --- 6. Exice o resultado ---
    print("\n--- Processo Concluído ---")
    print(f"Registros removidos: {registros_removidos}")
    print(f"Total de registros DEPOIS da remoção de duplicatas: {registros_depois}")

    # (Opcional) Exibe a amostra dos removidos
    print("\nAmostra dos dados REMOVIDOS (os mais antigos/duplicados):")
    display(hemoprod_removidos.head(10))

    # Você pode continuar a usar o DataFrame 'hemoprod_ce_deduplicado' para suas análises
    print("\nAmostra dos dados únicos (os mais recentes para cada chave):")
    display(hemoprod_df_deduplicado.head(10))
    
    # Agora você tem o DataFrame 'hemoprod_removidos' salvo

Total de registros ANTES da remoção de duplicatas: 184

Ordenando os dados por 'data_envio'...
Identificando duplicatas com cese na chave: ['cnpj', 'ano_referencia', 'periodo_referencia', 'razao_social_nome_fantasia']...

--- Processo Concluído ---
Registros removidos: 1
Total de registros DEPOIS da remoção de duplicatas: 183

Amostra dos dados REMOVIDOS (os mais antigos/duplicados):


id          data_envio  ultima_pagina idioma_inicial       semente  \
166  214 2025-07-11 15:42:42              4          pt-BR  1.813328e+09   

       codigo_acesso          data_inicio     data_ultima_acao             ip  \
166  x2aCGP57HelTDzN  2025-07-11 15:28:30  2025-07-11 15:42:42  164.163.2.146   

     identificacao_dado tipo_envio  ano_referencia periodo_referencia  \
166                 NaN   ORIGINAL            2025              Julho   

     identificacao_estabelecimento                   municipio  \
166                            NaN  Brasília, Distrito Federal   

                            razao_social_nome_fantasia  \
166  Grupo Gestor de Serviços em Hemoterapia (GSH) ...   

    razao_social_nome_fantasia_outros           cnpj    tipo_estabelecimento  \
166                               NaN  8397078003038  Agência Transfusional    

    natureza_estabelecimento dados_informados_referem_se  \
166                  Privado               Único serviço   

     rede_estabelecimento  cnes  endereco  \
166                   NaN   NaN       NaN   

     triagem_clinica_total_doacao_espontanea_aptos  \
166                                            NaN   

     triagem_clinica_total_doacao_espontanea_inaptos  \
166                                              NaN   

     triagem_clinica_total_doacao_reposicao_aptos  \
166                                           NaN   

     triagem_clinica_total_doacao_reposicao_inaptos  \
166                                             NaN   

     triagem_clinica_total_doacao_autologa_aptos  \
166                                          NaN   

     triagem_clinica_total_doacao_autologa_inaptos  \
166                                            NaN   

     total_doador_primeira_vez_aptos  total_doador_primeira_vez_inaptos  \
166                              NaN                                NaN   

     total_doador_repeticao_aptos  total_doador_repeticao_inaptos  \
166                           NaN                             NaN   

     total_doador_esporadico_aptos  total_doador_esporadico_inaptos  \
166                            NaN                              NaN   

     total_doador_masculino_aptos  total_doador_masculino_inaptos  \
166                           NaN                             NaN   

     total_doador_feminino_aptos  total_doador_feminino_inaptos  \
166                          NaN                            NaN   

     total_doador_menor_de_18_anos_aptos  \
166                                  NaN   

     total_doador_menor_de_18_anos_inaptos  total_doador_18_ate_29_anos_aptos  \
166                                    NaN                                NaN   

     total_doador_18_ate_29_anos_inaptos  total_doador_acima_de_29_anos_aptos  \
166                                  NaN                                  NaN   

     total_doador_acima_de_29_anos_inaptos  \
166                                    NaN   

     total_candidatos_inaptos_anemia_masculino  \
166                                        NaN   

     total_candidatos_inaptos_anemia_feminino  \
166                                       NaN   

     total_candidatos_inaptos_anemia_total  \
166                                    NaN   

     total_candidatos_inaptos_hipertensao_masculino  \
166                                             NaN   

     total_candidatos_inaptos_hipertensao_feminino  \
166                                            NaN   

     total_candidatos_inaptos_hipertensao_total  \
166                                         NaN   

     total_candidatos_inaptos_hipotensao_masculino  \
166                                            NaN   

     total_candidatos_inaptos_hipotensao_feminino  \
166                                           NaN   

     total_candidatos_inaptos_hipotensao_total  \
166                                        NaN   

     total_candidatos_inaptos_alcoolismo_masculino  \
166                                            NaN   

     tota


Amostra dos dados únicos (os mais recentes para cada chave):


id          data_envio  ultima_pagina idioma_inicial       semente  \
0  11 2023-05-10 11:29:00              4          pt-BR           NaN   
1  12 2023-05-10 12:22:00              4          pt-BR           NaN   
2  14 2023-05-15 12:56:00              4          pt-BR           NaN   
3  15 2023-05-15 14:31:00              4          pt-BR           NaN   
4  16 2023-05-15 16:23:00              4          pt-BR           NaN   
5  18 2023-05-17 15:23:00              4          pt-BR           NaN   
6  19 2023-06-05 15:52:52              4          pt-BR  2.315950e+08   
7  21 2023-06-07 17:23:07              4          pt-BR  7.123911e+08   
9  24 2023-06-12 15:01:50              4          pt-BR  1.024446e+09   
8  23 2023-06-12 15:06:58              4          pt-BR  1.246938e+09   

     codigo_acesso          data_inicio     data_ultima_acao           ip  \
0  rPK9T4H3U3oa2a9  2023-05-10 11:01:00  2023-05-10 11:29:00    10.0.0.30   
1  MIXePx6p2p5vAoy  2023-05-10 12:03:00  2023-05-10 12:22:00    10.0.4.36   
2  WZ4ZIXCj3uWhwAH  2023-05-15 12:04:00  2023-05-15 12:56:00   10.0.3.242   
3  iehHllaeyrYagiU  2023-05-15 14:10:00  2023-05-15 14:31:00  10.0.51.170   
4  1aorcIMzUajACtF  2023-05-15 14:42:00  2023-05-15 16:23:00    10.0.0.84   
5  EIeniMV1W4lx2lU  2023-05-17 13:51:00  2023-05-17 15:23:00   10.0.52.31   
6  rPK9T4H3U3oa2a9  2023-06-05 15:30:34  2023-06-05 15:52:52    10.0.0.56   
7  MIXePx6p2p5vAoy  2023-06-07 17:07:10  2023-06-07 17:23:07   10.0.4.216   
9  iehHllaeyrYagiU  2023-06-12 14:44:28  2023-06-12 15:01:50    10.0.0.37   
8  x2aCGP57HelTDzN  2023-06-12 14:19:12  2023-06-12 15:06:58    10.0.0.90   

   identificacao_dado tipo_envio  ano_referencia periodo_referencia  \
0                 NaN   ORIGINAL            2023              Abril   
1                 NaN   ORIGINAL            2023              Abril   
2                 NaN   ORIGINAL            2023              Abril   
3                 NaN   ORIGINAL            2023              Abril   
4                 NaN   ORIGINAL            2023              Abril   
5                 NaN   ORIGINAL            2023              Abril   
6                 NaN   ORIGINAL            2023               Maio   
7                 NaN   ORIGINAL            2023               Maio   
9                 NaN   ORIGINAL            2023               Maio   
8                 NaN   ORIGINAL            2023               Maio   

   identificacao_estabelecimento                   municipio  \
0                            NaN  Brasília, Distrito Federal   
1                            NaN  Brasília, Distrito Federal   
2                            NaN  Brasília, Distrito Federal   
3                            NaN  Brasília, Distrito Federal   
4                            NaN  Brasília, Distrito Federal   
5                            NaN  Brasília, Distrito Federal   
6                            NaN  Brasília, Distrito Federal   
7                            NaN  Brasília, Distrito Federal   
9                            NaN  Brasília, Distrito Federal   
8                            NaN  Brasília, Distrito Federal   

                          razao_social_nome_fantasia  \
0  Grupo Gestor de Serviços em Hemoterapia (GSH) ...   
1  Grupo Gestor de Serviços em Hemoterapia (GSH) ...   
2  Grupo Gestor de Serviços em Hemoterapia (GSH) ...   
3  Grupo Gestor de Serviços em Hemoterapia (GSH) ...   
4  Grupo Gestor de Serviços em Hemoterapia (GSH) ...   
5  Grupo Gestor de Serviços em Hemoterapia (GSH) ...   
6  Grupo Gestor de Serviços em Hemoterapia (GSH) ...   
7  Grupo Gestor de Serviços em Hemoterapia (GSH) ...   
9  Grupo Gestor de Serviços em Hemoterapia (GSH) ...   
8  Grupo Gestor de Serviços em Hemoterapia (GSH) ...   

            razao_social_nome_fantasia_outros           cnpj  \
0               GSH - AT HOSPITAL SANTA LUZIA  8397078001841   
1              GSH - AT HOSPITAL SANTA HELENA  8397078002066   
2                 AT HOSPITAL SANTA LÚCIA SUL     83970

In [44]:
hemoprod_df_deduplicado.to_excel('dados_processados/hemoprod_df.xlsx', index=False)

## Hemoprod Espirito Santo

In [ ]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)


In [ ]:
import os
import pandas as pd

dados_brutos_path = 'dados_brutos'

arquivo_dados_path = os.path.join(dados_brutos_path, 'Hemoprod_ES.xlsx')
nome_planilha = 'HEMOPROD - ESPIRITOSANTO'

dicionario_path_es = ('./dicionario_colunas_269.xlsx')
# dicionario_path_ap = ('./dicionario_colunas_270.xlsx')

dicionario_es = pd.read_excel(dicionario_path_es, sheet_name='Sheet1')

# --- 2. Carregue os dados e o dicionário ---
try:
    # Carrega o arquivo de dados
    hemoprod_es = pd.read_excel(arquivo_dados_path, sheet_name=nome_planilha)
    print("Arquivo de dados carregado com sucesso.")
    print(f"Número de colunas original: {len(hemoprod_es.columns)}")

    # Carrega o arquivo de dicionário
    dicionario = pd.read_excel(dicionario_path_es)
    print("Arquivo de dicionário carregado com sucesso.")

    # --- 3. Extraia a lista de novos nomes ---
    # Pega os valores da coluna 'nome_sql' e converte para uma lista
    novos_nomes = dicionario['nome_sql'].tolist()
    print(f"Número de novos nomes no dicionário: {len(novos_nomes)}")

    # --- 4. Verificação de segurança (MUITO IMPORTANTE) ---
    # Garante que o número de colunas é o mesmo antes de renomear
    if len(hemoprod_es.columns) == len(novos_nomes):
        print("\nO número de colunas corresponde. Renomeando...")
        
        # --- 5. Substitua os nomes das colunas ---
        # Esta é a linha principal que faz a substituição direta
        hemoprod_es.columns = novos_nomes
        
        print("Colunas renomeadas com sucesso!")
        
        # --- 6. Verifique o resultado ---
        print("\nInformações do DataFrame com as novas colunas:")
        hemoprod_es.info()
        
        print("\nAs 5 primeiras linhas com as novas colunas:")
        display(hemoprod_es.head())

    else:
        # Mensagem de erro se o número de colunas for diferente
        print("\n--- ERRO ---")
        print("A renomeação foi cancelada. O número de colunas no arquivo de dados não é igual ao número de nomes no dicionário.")
        print(f"Colunas no arquivo de dados: {len(hemoprod_es.columns)}")
        print(f"Nomes no dicionário: {len(novos_nomes)}")

except FileNotFoundError as e:
    print(f"\nErro de arquivo não encontrado: {e}")
except KeyError as e:
    print(f"\nErro de coluna não encontrada: {e}. Verifique se a coluna 'nome_sql' existe no seu arquivo de dicionário.")
except Exception as e:
    print(f"\nOcorreu um erro inesperado: {e}")



Arquivo de dados carregado com sucesso.
Número de colunas original: 257
Arquivo de dicionário carregado com sucesso.
Número de novos nomes no dicionário: 270

--- ERRO ---
A renomeação foi cancelada. O número de colunas no arquivo de dados não é igual ao número de nomes no dicionário.
Colunas no arquivo de dados: 257
Nomes no dicionário: 270


In [51]:
arquivo_dados_path = os.path.join(dados_brutos_path, 'Hemoprod_CE.xlsx')
nome_planilha = 'Planilha1'
hemoprod_ce1 = pd.read_excel(arquivo_dados_path, sheet_name=nome_planilha)

colunas_padrao = set(hemoprod_ce1.columns)
colunas_estado = set(hemoprod_es.columns)

colunas_faltantes = list(colunas_padrao - colunas_estado)

colunas_a_mais = list(colunas_estado - colunas_padrao)

print(f"Número de colunas faltantes: {len(colunas_faltantes)}")
print(f"Colunas faltantes (a serem adicionadas): {colunas_faltantes}")
print("-" * 30)
print(f"Número de colunas a mais: {len(colunas_a_mais)}")
print(f"Colunas a mais (a serem dropadas): {colunas_a_mais}")


Número de colunas faltantes: 15
Colunas faltantes (a serem adicionadas): ['6. Produção Hemoterápica  6.1(a) Entradas\xa0  [Concentrado de Plaquetas de Aférese][Recebidas]', 'Cite os estabelecimentos que compõem a rede  Informe o Tipo de Estabelecimento, o Nome Fantasia\xa0e o Município de localização de cada um. ', '6.1(b) Perdas  [Concentrado de Plaquetas de Aférese][Outros motivos]', 'Ano de referência\xa0 ', '6. Produção Hemoterápica  6.1(a) Entradas\xa0  [Concentrado de Plaquetas de Aférese][Devolvidas]', '6.1(b) Perdas  [Concentrado de Plaquetas de Aférese][Validade]', '6.1(d) Distribuição para outros serviços  \xa0  [Concentrado de Plaquetas de Aférese][Total]', '6.1(c) Tranfusões  [Concentrado de Plaquetas de Aférese][Total]', '6.1(d) Distribuição para outros serviços  \xa0  [Concentrado de Plaquetas de Aférese][Com exame pré-transfusional ]', '6. Produção Hemoterápica  6.1(a) Entradas\xa0  [Concentrado de Plaquetas de Aférese][Produzidas]', '6.1(d) Distribuição para outros serv

In [52]:
colunas_a_mais = ['Período de referência [Outros]', 'Município [Outros]', 'URL de referência']

# Conta quantos valores *não são nulos* em cada uma dessas colunas
contagem_nao_nulos = hemoprod_es[colunas_a_mais].count()

print("Contagem de valores NÃO-NULOS (preenchidos) por coluna:")
print(contagem_nao_nulos)

Contagem de valores NÃO-NULOS (preenchidos) por coluna:
Período de referência [Outros]     19
Município [Outros]                  0
URL de referência                 610
dtype: int64


In [53]:
if colunas_a_mais:
    hemoprod_es = hemoprod_es.drop(columns=colunas_a_mais, errors='ignore')
    print(f"Colunas a mais removidas: {colunas_a_mais}")
else:
    print("Nenhuma coluna para remover.")

# 2. ADICIONAR as colunas faltantes e preenchê-las com zero (0)
for coluna in colunas_faltantes:
    # Cria a nova coluna no hemoprod_es preenchida com 0
    hemoprod_es[coluna] = 0

print(f"Colunas faltantes adicionadas e zeradas: {colunas_faltantes}")

# 3. REORDENAR as colunas do hemoprod_es na mesma ordem do df_padrao
# A lista de colunas do df_padrao agora é o nosso gabarito final
ordem_padrao = hemoprod_ce1.columns.tolist()

# Reorganiza as colunas do hemoprod_es
hemoprod_es = hemoprod_es[ordem_padrao]

print("-" * 50)
print("Processo concluído:")
print(f"Total de colunas após o ajuste: {len(hemoprod_es.columns)}")
print("A ordem das colunas no df_estado agora corresponde à ordem do df_padrao.")

Colunas a mais removidas: ['Período de referência [Outros]', 'Município [Outros]', 'URL de referência']
Colunas faltantes adicionadas e zeradas: ['6. Produção Hemoterápica  6.1(a) Entradas\xa0  [Concentrado de Plaquetas de Aférese][Recebidas]', 'Cite os estabelecimentos que compõem a rede  Informe o Tipo de Estabelecimento, o Nome Fantasia\xa0e o Município de localização de cada um. ', '6.1(b) Perdas  [Concentrado de Plaquetas de Aférese][Outros motivos]', 'Ano de referência\xa0 ', '6. Produção Hemoterápica  6.1(a) Entradas\xa0  [Concentrado de Plaquetas de Aférese][Devolvidas]', '6.1(b) Perdas  [Concentrado de Plaquetas de Aférese][Validade]', '6.1(d) Distribuição para outros serviços  \xa0  [Concentrado de Plaquetas de Aférese][Total]', '6.1(c) Tranfusões  [Concentrado de Plaquetas de Aférese][Total]', '6.1(d) Distribuição para outros serviços  \xa0  [Concentrado de Plaquetas de Aférese][Com exame pré-transfusional ]', '6. Produção Hemoterápica  6.1(a) Entradas\xa0  [Concentrado de P

In [54]:
# Mapeia as colunas, limpando espaços em branco no início e fim
# e substituindo o caractere \xa0 por um espaço normal.
novos_nomes = {col: col.strip().replace('\xa0', ' ') for col in hemoprod_es.columns}

# Aplica a renomeação
hemoprod_es = hemoprod_es.rename(columns=novos_nomes)

print("Nomes das colunas limpos e padronizados.")

Nomes das colunas limpos e padronizados.


In [55]:
# Nomes das colunas após a limpeza (ajuste se a coluna original tiver nome diferente)
coluna_periodo_limpa = 'Período de referência'
coluna_ano_limpa = 'Ano de referência' # Ou apenas 'Ano de referencia'

# Nota: Certifique-se de que a sua coluna original do período esteja na ordem correta,
# caso contrário, a lógica de reordenação no final fará o trabalho.

# 1. Criar ou sobrescrever a coluna 'Ano de referencia' (limpa)
# O split divide a string e o str[1] pega o ano
hemoprod_es[coluna_ano_limpa] = hemoprod_es[coluna_periodo_limpa].astype(str).str.split('/').str[1]

# 2. Atualizar a coluna original 'Período de referência' (para ter só o mês)
# O split divide a string e o str[0] pega o mês
hemoprod_es[coluna_periodo_limpa] = hemoprod_es[coluna_periodo_limpa].astype(str).str.split('/').str[0]

print("Separação de mês e ano concluída nas colunas limpas.")
print(hemoprod_es[[coluna_periodo_limpa, coluna_ano_limpa]].head())

Separação de mês e ano concluída nas colunas limpas.
  Período de referência Ano de referência
0               Outubro              2022
1               Outubro              2022
2               Outubro              2022
3               Outubro              2022
4              Novembro              2022


In [56]:
set(hemoprod_es.columns)

{'2. Triagem Clínica  2.1 Total de candidatos quanto ao tipo de doação  [Autóloga][Aptos]',
 '2. Triagem Clínica  2.1 Total de candidatos quanto ao tipo de doação  [Autóloga][Inaptos]',
 '2. Triagem Clínica  2.1 Total de candidatos quanto ao tipo de doação  [Espontânea][Aptos]',
 '2. Triagem Clínica  2.1 Total de candidatos quanto ao tipo de doação  [Espontânea][Inaptos]',
 '2. Triagem Clínica  2.1 Total de candidatos quanto ao tipo de doação  [Reposição][Aptos]',
 '2. Triagem Clínica  2.1 Total de candidatos quanto ao tipo de doação  [Reposição][Inaptos]',
 '2.2 Total de candidatos quanto ao tipo de doador  [Esporádico][Aptos]',
 '2.2 Total de candidatos quanto ao tipo de doador  [Esporádico][Inaptos]',
 '2.2 Total de candidatos quanto ao tipo de doador  [Primeira vez][Aptos]',
 '2.2 Total de candidatos quanto ao tipo de doador  [Primeira vez][Inaptos]',
 '2.2 Total de candidatos quanto ao tipo de doador  [Repetição][Aptos]',
 '2.2 Total de candidatos quanto ao tipo de doador  [Repeti

In [57]:
hemoprod_es.head()

ID da resposta        Data de envio  Última página Idioma inicial  Semente  \
0              15  2022-11-28 11:00:00              4          pt-BR      NaN   
1              16  2022-11-28 11:20:00              4          pt-BR      NaN   
2              17  2022-11-28 11:09:00              4          pt-BR      NaN   
3              20  2022-11-30 13:53:00              4          pt-BR      NaN   
4              22  2022-12-01 09:57:00              4          pt-BR      NaN   

  Código de acesso       Data de início  Data da última ação  Endereço IP  \
0  vxvDL62C5ez3TbL  2022-11-28 10:49:00  2022-11-28 11:00:00  10.0.11.157   
1  Sgje9tqyifI28Jl  2022-11-28 10:54:00  2022-11-28 11:20:00   10.0.0.216   
2  vxvDL62C5ez3TbL  2022-11-28 11:04:00  2022-11-28 11:09:00   10.0.0.216   
3  z6fJe1OkT46z0Yn  2022-11-30 13:38:00  2022-11-30 13:53:00   10.0.7.253   
4  VSR5a1w4grp1UkS  2022-12-01 09:43:00  2022-12-01 09:57:00  10.0.11.127   

   IDENTIFICAÇÃO DO DADO  \
0                    NaN   
1                    NaN   
2                    NaN   
3                    NaN   
4                    NaN   

  Tipo de Informação  Antes de responder ao formulário, declare o tipo de informação que será inserida.  \
0                                           ORIGINAL                                                      
1                                           ORIGINAL                                                      
2                                           ORIGINAL                                                      
3                                           ORIGINAL                                                      
4                                           ORIGINAL                                                      

  Ano de referência Período de referência  IDENTIFICAÇÃO DO ESTABELECIMENTO  \
0              2022               Outubro                               NaN   
1              2022               Outubro                               NaN   
2              2022               Outubro                               NaN   
3              2022               Outubro                               NaN   
4              2022              Novembro                               NaN   

                                 Município  \
0                    Serra, Espírito Santo   
1                  Vitória, Espírito Santo   
2                    Serra, Espírito Santo   
3                 Colatina, Espírito Santo   
4  Venda Nova do Imigrante, Espírito Santo   

                        Razão Social - Nome Fantasia  \
0  Hemomed Medicina Transfusional Ltda - Hospital...   
1                     Pronto Socorro Milena Gottardi   
2  Hemomed Medicina Transfusional Ltda - Hospital...   
3                          Casa de Saúde Santa Maria   
4  Associação Social Filantrópica Hospital Padre ...   

  Razão Social - Nome Fantasia  [Outros]          CNPJ  \
0                                    NaN  5.674518e+12   
1                                    NaN  2.708061e+13   
2                                    NaN  5.674518e+12   
3                                    NaN  2.749061e+13   
4                                    NaN  2.744380e+13   

  Tipo de estabelecimento Natureza do estabelecimento  \
0  Agência Transfusional                      Público   
1  Agência Transfusional                      Público   
2  Agência Transfusional                      Privado   
3  Agência Transfusional                  Privado-SUS   
4  Agência Transfusional                  Privado-SUS   

   Os dados informados referem-se à um(a):  \
0                                        0   
1                                        0   
2                                        0   
3                                        0   
4                                        0   

   Cite os estabelecimentos que compõem a rede  Informe o Tipo de Estabelecimento, o Nome Fantasia e o Município de localização de cada um.  \
0                                       

In [19]:
hemoprod_es.head()

ID da resposta        Data de envio  Última página Idioma inicial  Semente  \
0              15  2022-11-28 11:00:00              4          pt-BR      NaN   
1              16  2022-11-28 11:20:00              4          pt-BR      NaN   
2              17  2022-11-28 11:09:00              4          pt-BR      NaN   
3              20  2022-11-30 13:53:00              4          pt-BR      NaN   
4              22  2022-12-01 09:57:00              4          pt-BR      NaN   

  Código de acesso       Data de início  Data da última ação  Endereço IP  \
0  vxvDL62C5ez3TbL  2022-11-28 10:49:00  2022-11-28 11:00:00  10.0.11.157   
1  Sgje9tqyifI28Jl  2022-11-28 10:54:00  2022-11-28 11:20:00   10.0.0.216   
2  vxvDL62C5ez3TbL  2022-11-28 11:04:00  2022-11-28 11:09:00   10.0.0.216   
3  z6fJe1OkT46z0Yn  2022-11-30 13:38:00  2022-11-30 13:53:00   10.0.7.253   
4  VSR5a1w4grp1UkS  2022-12-01 09:43:00  2022-12-01 09:57:00  10.0.11.127   

   IDENTIFICAÇÃO DO DADO   \
0                     NaN   
1                     NaN   
2                     NaN   
3                     NaN   
4                     NaN   

  Tipo de Informação  Antes de responder ao formulário, declare o tipo de informação que será inserida.    \
0                                           ORIGINAL                                                        
1                                           ORIGINAL                                                        
2                                           ORIGINAL                                                        
3                                           ORIGINAL                                                        
4                                           ORIGINAL                                                        

   Ano de referência   Período de referência  \
0                    0               Outubro   
1                    0               Outubro   
2                    0               Outubro   
3                    0               Outubro   
4                    0              Novembro   

   IDENTIFICAÇÃO DO ESTABELECIMENTO                                 Município  \
0                                NaN                    Serra, Espírito Santo   
1                                NaN                  Vitória, Espírito Santo   
2                                NaN                    Serra, Espírito Santo   
3                                NaN                 Colatina, Espírito Santo   
4                                NaN  Venda Nova do Imigrante, Espírito Santo   

                       Razão Social - Nome Fantasia   \
0  Hemomed Medicina Transfusional Ltda - Hospital...   
1                     Pronto Socorro Milena Gottardi   
2  Hemomed Medicina Transfusional Ltda - Hospital...   
3                          Casa de Saúde Santa Maria   
4  Associação Social Filantrópica Hospital Padre ...   

  Razão Social - Nome Fantasia  [Outros]          CNPJ  \
0                                    NaN  5.674518e+12   
1                                    NaN  2.708061e+13   
2                                    NaN  5.674518e+12   
3                                    NaN  2.749061e+13   
4                                    NaN  2.744380e+13   

  Tipo de estabelecimento Natureza do estabelecimento  \
0  Agência Transfusional                      Público   
1  Agência Transfusional                      Público   
2  Agência Transfusional                      Privado   
3  Agência Transfusional                  Privado-SUS   
4  Agência Transfusional                  Privado-SUS   

   Os dados informados referem-se à um(a):   \
0                                         0   
1                                         0   
2                                         0   
3                                         0   
4                                         0   

   Cite os estabelecimentos que compõem a rede  Informe o Tipo de Estabelecimento, o Nome Fantasia e o Município de localização de cada

In [61]:
# Carrega o arquivo de dicionário
dicionario_path_es = ('./dicionario_colunas_269.xlsx')
dicionario = pd.read_excel(dicionario_path_es)
print("Arquivo de dicionário carregado com sucesso.")

# --- 3. Extraia a lista de novos nomes ---
# Pega os valores da coluna 'nome_sql' e converte para uma lista
novos_nomes = dicionario['nome_sql'].tolist()
print(f"Número de novos nomes no dicionário: {len(novos_nomes)}")

# --- 4. Verificação de segurança (MUITO IMPORTANTE) ---
# Garante que o número de colunas é o mesmo antes de renomear
if len(hemoprod_es.columns) == len(novos_nomes):
    print("\nO número de colunas corresponde. Renomeando...")
    
    # --- 5. Substitua os nomes das colunas ---
    # Esta é a linha principal que faz a substituição direta
    hemoprod_es.columns = novos_nomes
    
    print("Colunas renomeadas com sucesso!")
    
    # --- 6. Verifique o resultado ---
    print("\nInformações do DataFrame com as novas colunas:")
    hemoprod_es.info()
    
    print("\nAs 5 primeiras linhas com as novas colunas:")
    display(hemoprod_es.head())

else:
    # Mensagem de erro se o número de colunas for diferente
    print("\n--- ERRO ---")
    print("A renomeação foi cancelada. O número de colunas no arquivo de dados não é igual ao número de nomes no dicionário.")
    print(f"Colunas no arquivo de dados: {len(hemoprod_es.columns)}")
    print(f"Nomes no dicionário: {len(novos_nomes)}")


Arquivo de dicionário carregado com sucesso.
Número de novos nomes no dicionário: 269

O número de colunas corresponde. Renomeando...
Colunas renomeadas com sucesso!

Informações do DataFrame com as novas colunas:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1827 entries, 0 to 1826
Columns: 269 entries, id to hemoprod_3_observacoes
dtypes: float64(237), int64(16), object(16)
memory usage: 3.7+ MB

As 5 primeiras linhas com as novas colunas:


id           data_envio  ultima_pagina idioma_inicial  semente  \
0  15  2022-11-28 11:00:00              4          pt-BR      NaN   
1  16  2022-11-28 11:20:00              4          pt-BR      NaN   
2  17  2022-11-28 11:09:00              4          pt-BR      NaN   
3  20  2022-11-30 13:53:00              4          pt-BR      NaN   
4  22  2022-12-01 09:57:00              4          pt-BR      NaN   

     codigo_acesso          data_inicio     data_ultima_acao           ip  \
0  vxvDL62C5ez3TbL  2022-11-28 10:49:00  2022-11-28 11:00:00  10.0.11.157   
1  Sgje9tqyifI28Jl  2022-11-28 10:54:00  2022-11-28 11:20:00   10.0.0.216   
2  vxvDL62C5ez3TbL  2022-11-28 11:04:00  2022-11-28 11:09:00   10.0.0.216   
3  z6fJe1OkT46z0Yn  2022-11-30 13:38:00  2022-11-30 13:53:00   10.0.7.253   
4  VSR5a1w4grp1UkS  2022-12-01 09:43:00  2022-12-01 09:57:00  10.0.11.127   

   identificacao_dado tipo_envio ano_referencia periodo_referencia  \
0                 NaN   ORIGINAL           2022            Outubro   
1                 NaN   ORIGINAL           2022            Outubro   
2                 NaN   ORIGINAL           2022            Outubro   
3                 NaN   ORIGINAL           2022            Outubro   
4                 NaN   ORIGINAL           2022           Novembro   

   identificacao_estabelecimento                                municipio  \
0                            NaN                    Serra, Espírito Santo   
1                            NaN                  Vitória, Espírito Santo   
2                            NaN                    Serra, Espírito Santo   
3                            NaN                 Colatina, Espírito Santo   
4                            NaN  Venda Nova do Imigrante, Espírito Santo   

                          razao_social_nome_fantasia  \
0  Hemomed Medicina Transfusional Ltda - Hospital...   
1                     Pronto Socorro Milena Gottardi   
2  Hemomed Medicina Transfusional Ltda - Hospital...   
3                          Casa de Saúde Santa Maria   
4  Associação Social Filantrópica Hospital Padre ...   

  razao_social_nome_fantasia_outros          cnpj    tipo_estabelecimento  \
0                               NaN  5.674518e+12  Agência Transfusional    
1                               NaN  2.708061e+13  Agência Transfusional    
2                               NaN  5.674518e+12  Agência Transfusional    
3                               NaN  2.749061e+13  Agência Transfusional    
4                               NaN  2.744380e+13  Agência Transfusional    

  natureza_estabelecimento  dados_informados_referem_se  rede_estabelecimento  \
0                  Público                            0                     0   
1                  Público                            0                     0   
2                  Privado                            0                     0   
3              Privado-SUS                            0                     0   
4              Privado-SUS                            0                     0   

   cnes  endereco  triagem_clinica_total_doacao_espontanea_aptos  \
0   NaN       NaN                                            NaN   
1   NaN       NaN                                            NaN   
2   NaN       NaN                                            NaN   
3   NaN       NaN                                            NaN   
4   NaN       NaN                                            NaN   

   triagem_clinica_total_doacao_espontanea_inaptos  \
0                                              NaN   
1                                              NaN   
2                                              NaN   
3                                              NaN   
4                                              NaN   

   triagem_clinica_total_doacao_reposicao_aptos  \
0                                           NaN   
1                                           NaN   
2                                           NaN   
3               

In [62]:
print("--- Nomes das Colunas (um por linha) ---")
for coluna in hemoprod_es.columns:
    print(coluna + ",") 

--- Nomes das Colunas (um por linha) ---
id,
data_envio,
ultima_pagina,
idioma_inicial,
semente,
codigo_acesso,
data_inicio,
data_ultima_acao,
ip,
identificacao_dado,
tipo_envio,
ano_referencia,
periodo_referencia,
identificacao_estabelecimento,
municipio,
razao_social_nome_fantasia,
razao_social_nome_fantasia_outros,
cnpj,
tipo_estabelecimento,
natureza_estabelecimento,
dados_informados_referem_se,
rede_estabelecimento,
cnes,
endereco,
triagem_clinica_total_doacao_espontanea_aptos,
triagem_clinica_total_doacao_espontanea_inaptos,
triagem_clinica_total_doacao_reposicao_aptos,
triagem_clinica_total_doacao_reposicao_inaptos,
triagem_clinica_total_doacao_autologa_aptos,
triagem_clinica_total_doacao_autologa_inaptos,
total_doador_primeira_vez_aptos,
total_doador_primeira_vez_inaptos,
total_doador_repeticao_aptos,
total_doador_repeticao_inaptos,
total_doador_esporadico_aptos,
total_doador_esporadico_inaptos,
total_doador_masculino_aptos,
total_doador_masculino_inaptos,
total_doador_feminino

In [63]:
import numpy as np
import pandas as pd

# Suponha que esta é a sua lista de colunas que devem ser vazias, e não 0
colunas_para_vazias = [
    'dados_informados_referem_se',
    'rede_estabelecimento',
    
]

# Itera sobre cada coluna na lista
for coluna in colunas_para_vazias:
    # Verifica se a coluna existe no DataFrame antes de tentar fazer a substituição
    if coluna in hemoprod_es.columns:
        # Substitui todos os valores '0' por pd.NA (valor ausente/vazio)
        hemoprod_es[coluna] = hemoprod_es[coluna].replace(0, pd.NA)
        print(f"Coluna '{coluna}' corrigida: 0 substituído por pd.NA.")
    else:
        print(f"Atenção: Coluna '{coluna}' não encontrada no DataFrame.")

print("\nSubstituição concluída.")

Coluna 'dados_informados_referem_se' corrigida: 0 substituído por pd.NA.
Coluna 'rede_estabelecimento' corrigida: 0 substituído por pd.NA.

Substituição concluída.


In [67]:
# Coluna a ser verificada (já limpa e separada)
coluna_mes = 'periodo_referencia'

# O padrão Regex r'.*\d+.*' verifica se a string contém UM OU MAIS dígitos (0-9)
# O .str.contains() retorna True ou False para cada linha
registros_com_numero = hemoprod_es[coluna_mes].astype(str).str.contains(r'\d+', na=False)

# 1. Contar quantos registros têm números
total_com_numero = registros_com_numero.sum()

print(f"Total de registros na coluna '{coluna_mes}' que contêm números: {total_com_numero}")

if total_com_numero > 0:
    print("-" * 50)
    print("Amostra dos registros que contêm números:")
    
    # 2. Exibir os registros com problema (as 5 primeiras ocorrências)
    linhas_problema = hemoprod_es[registros_com_numero]
    print(linhas_problema[[coluna_mes]].head(55))
    
    # Opcional: Se você quiser ver a linha inteira para entender o contexto
    # print(linhas_problema.head())
    
else:
    print("Nenhum registro encontrado com números na coluna de meses. Os dados parecem limpos.")

Total de registros na coluna 'periodo_referencia' que contêm números: 53
--------------------------------------------------
Amostra dos registros que contêm números:
    periodo_referencia
46    Consolidado 2022
55    Consolidado 2022
57    Consolidado 2022
58    Consolidado 2022
61    Consolidado 2022
66    Consolidado 2022
70    Consolidado 2022
72    Consolidado 2022
80    Consolidado 2022
81    Consolidado 2022
91    Consolidado 2022
94    Consolidado 2022
95    Consolidado 2022
98    Consolidado 2022
103   Consolidado 2022
106   Consolidado 2022
107   Consolidado 2022
108   Consolidado 2022
109   Consolidado 2022
110   Consolidado 2022
111   Consolidado 2022
112   Consolidado 2022
115   Consolidado 2022
116   Consolidado 2022
117   Consolidado 2022
118   Consolidado 2022
119   Consolidado 2022
120   Consolidado 2022
121   Consolidado 2022
122   Consolidado 2022
123   Consolidado 2022
126   Consolidado 2022
127   Consolidado 2022
128   Consolidado 2022
129   Consolidado 2022
130   

In [68]:
import pandas as pd
import numpy as np
# Colunas a serem corrigidas
coluna_periodo = 'periodo_referencia'
coluna_ano = 'ano_referencia'

# 1. Identificar as linhas onde o período ainda contém o ano (e assumimos que é um caso de "Consolidado XXXX")
# Regex para encontrar qualquer texto seguido por 4 dígitos (o ano)
filtro_consolidado = hemoprod_es[coluna_periodo].astype(str).str.contains(r'\d{4}', na=False)

if filtro_consolidado.any():
    print(f"Encontrados {filtro_consolidado.sum()} registros que precisam de correção manual.")
    
    # 2. Extrair o Ano (4 dígitos consecutivos)
    # A função extract() é ideal para isso
    ano_extraido = hemoprod_es.loc[filtro_consolidado, coluna_periodo].str.extract(r'(\d{4})', expand=False)
    
    # 3. Preencher a coluna 'Ano de referencia' com o valor extraído
    hemoprod_es.loc[filtro_consolidado, coluna_ano] = ano_extraido
    
    # 4. Limpar a coluna 'Período de referência'
    # Remove os 4 dígitos e qualquer espaço antes ou depois deles, deixando apenas o texto como "Consolidado"
    hemoprod_es.loc[filtro_consolidado, coluna_periodo] = (
        hemoprod_es.loc[filtro_consolidado, coluna_periodo]
                 .str.replace(r'\s*\d{4}', '', regex=True) # Remove o ano e espaços
                 .str.strip() # Remove qualquer espaço residual no início/fim
    )
    
    print("Correção aplicada com sucesso.")
    print("-" * 50)
    print("Amostra dos registros corrigidos:")
    # Mostrar as 5 primeiras linhas que foram corrigidas
    print(hemoprod_es.loc[filtro_consolidado, [coluna_periodo, coluna_ano]].head())

else:
    print("Nenhum caso de período que ainda contenha o ano foi encontrado. O DataFrame está limpo.")

Encontrados 53 registros que precisam de correção manual.
Correção aplicada com sucesso.
--------------------------------------------------
Amostra dos registros corrigidos:
   periodo_referencia ano_referencia
46        Consolidado           2022
55        Consolidado           2022
57        Consolidado           2022
58        Consolidado           2022
61        Consolidado           2022


In [69]:
# --- 2. Defina as colunas para a chave e para ordenação ---
registros_antes = len(hemoprod_es)
print(f"Total de registros ANTES da remoção de duplicatas: {registros_antes}")
    

colunas_chave = [
        'cnpj', 
        'ano_referencia', 
        'periodo_referencia', 
        'razao_social_nome_fantasia'
    ]

coluna_data = 'data_envio'

# --- 3. Verifique se as colunas necessárias existem ---
colunas_necessarias = colunas_chave + [coluna_data]

if not all(col in hemoprod_es.columns for col in colunas_necessarias):
    print("\n--- ERRO ---")
    print("Uma ou mais colunas necessárias para a deduplicação não foram encontradas.")
    colunas_faltantes = [col for col in colunas_necessarias if col not in hemoprod_es.columns]
    print(f"Colunas necessárias: {colunas_necessarias}")
    print(f"Colunas faltantes no DataFrame: {colunas_faltantes}")
else:
    # --- 4. Prepare a coluna de data e ordene os dados ---
    # Converte a coluna 'data_envio' para datetime para garantir a ordenação correta.
    # 'errors='coerce'' transformará datas inválidas em NaT (Not a Time), que são tratadas como nulas.
    hemoprod_es[coluna_data] = pd.to_datetime(hemoprod_es[coluna_data], errors='coerce')

    # Ordena o DataFrame. Os registros com data de envio mais recente ficarão por último.
    print(f"\nOrdenando os dados por '{coluna_data}'...")
    hemoprod_es_ordenado = hemoprod_es.sort_values(by=coluna_data, ascending=True)

    # --- 5. Identifique e separe os registros duplicados e únicos ---
    # Em vez de usar drop_duplicates() diretamente, vamos usar duplicated()
    # para criar uma máscara booleana.
    # 'keep='last'' marca todas as ocorrências de uma chave como True, EXCETO a última (a mais recente).
    print(f"Identificando duplicatas com cese na chave: {colunas_chave}...")
    mascara_duplicatas = hemoprod_es_ordenado.duplicated(subset=colunas_chave, keep='last')

    # O DataFrame de removidos conterá todas as linhas marcadas como True
    hemoprod_removidos = hemoprod_es_ordenado[mascara_duplicatas]
    
    # O DataFrame deduplicado conterá o INVERSO (~) da máscara (linhas marcadas como False)
    hemoprod_es_deduplicado = hemoprod_es_ordenado[~mascara_duplicatas]
    
    # Agora podemos contar os registros diretamente dos novos DataFrames
    registros_depois = len(hemoprod_es_deduplicado)
    registros_removidos = len(hemoprod_removidos) 
    
    # --- 6. Exice o resultado ---
    print("\n--- Processo Concluído ---")
    print(f"Registros removidos: {registros_removidos}")
    print(f"Total de registros DEPOIS da remoção de duplicatas: {registros_depois}")

    # (Opcional) Exibe a amostra dos removidos
    print("\nAmostra dos dados REMOVIDOS (os mais antigos/duplicados):")
    display(hemoprod_removidos.head(10))

    # Você pode continuar a usar o DataFrame 'hemoprod_ce_deduplicado' para suas análises
    print("\nAmostra dos dados únicos (os mais recentes para cada chave):")
    display(hemoprod_es_deduplicado.head(10))
    
    # Agora você tem o DataFrame 'hemoprod_removidos' salvo

Total de registros ANTES da remoção de duplicatas: 1827

Ordenando os dados por 'data_envio'...
Identificando duplicatas com cese na chave: ['cnpj', 'ano_referencia', 'periodo_referencia', 'razao_social_nome_fantasia']...

--- Processo Concluído ---
Registros removidos: 83
Total de registros DEPOIS da remoção de duplicatas: 1744

Amostra dos dados REMOVIDOS (os mais antigos/duplicados):


id          data_envio  ultima_pagina idioma_inicial       semente  \
23    58 2022-12-13 14:32:00              4          pt-BR           NaN   
29    65 2022-12-14 14:36:00              4          pt-BR           NaN   
55   104 2023-01-06 14:18:00              4          pt-BR           NaN   
74   126 2023-01-10 10:50:00              4          pt-BR           NaN   
120  193 2023-01-30 11:48:54              4          pt-BR  1.112983e+09   
142  218 2023-02-06 08:15:00              4          pt-BR           NaN   
148  226 2023-02-07 14:34:51              4          pt-BR  1.750521e+09   
180  262 2023-02-15 16:17:00              4          pt-BR           NaN   
278  386 2023-05-02 15:11:18              4          pt-BR  1.087423e+09   
286  394 2023-05-04 13:40:05              4          pt-BR  5.294624e+07   

       codigo_acesso          data_inicio     data_ultima_acao           ip  \
23   4LWfMHVP36HzcXG  2022-12-13 13:30:00  2022-12-13 14:32:00   10.0.0.213   
29   upC3Y7lQmhhIeqY  2022-12-14 14:21:00  2022-12-14 14:36:00    10.0.0.38   
55   upC3Y7lQmhhIeqY  2023-01-06 13:49:00  2023-01-06 14:18:00    10.0.0.38   
74   jIrWf3pgMmwH9DC  2023-01-10 10:25:00  2023-01-10 10:50:00    10.0.0.51   
120  JOMetCb5zt7woLp  2023-01-30 11:35:10  2023-01-30 11:48:54  10.0.95.255   
142  QdX9UPpG5VWQkM9  2023-02-06 07:56:00  2023-02-06 08:15:00  10.0.95.255   
148  vxvDL62C5ez3TbL  2023-02-07 14:13:11  2023-02-07 14:34:51     10.0.0.1   
180  m6RWd9YaEjE2SWp  2023-02-15 16:07:00  2023-02-15 16:17:00  10.0.17.255   
278  ONRtlcXMdnaASJ8  2023-05-02 15:04:51  2023-05-02 15:11:18   10.0.52.31   
286  5fC4SAMFa7gO90g  2023-05-04 13:19:57  2023-05-04 13:40:05   10.0.52.44   

     identificacao_dado tipo_envio ano_referencia periodo_referencia  \
23                  NaN   ORIGINAL           2022           Novembro   
29                  NaN   ORIGINAL           2022           Novembro   
55                  NaN   ORIGINAL           2022        Consolidado   
74                  NaN   ORIGINAL           2022           Dezembro   
120                 NaN   ORIGINAL           2022        Consolidado   
142                 NaN   ORIGINAL           2023          Fevereiro   
148                 NaN   ORIGINAL           2022        Consolidado   
180                 NaN   ORIGINAL           2023            Janeiro   
278                 NaN   ORIGINAL           2023              Abril   
286                 NaN   ORIGINAL           2023              Abril   

     identificacao_estabelecimento                     municipio  \
23                             NaN    São Mateus, Espírito Santo   
29                             NaN    Vila Velha, Espírito Santo   
55                             NaN    Vila Velha, Espírito Santo   
74                             NaN       Vitória, Espírito Santo   
120                            NaN        Guaçuí, Espírito Santo   
142                            NaN      Linhares, Espírito Santo   
148                            NaN         Serra, Espírito Santo   
180                            NaN    Vila Velha, Espírito Santo   
278                            NaN  Nova Venécia, Espírito Santo   
286                            NaN     Cariacica, Espírito Santo   

                            razao_social_nome_fantasia  \
23   Secretaria de Estado da Saúde do Espírito Sant...   
29   Hemomed Medicina Transfusional Ltda - Hospital...   
55   Hemomed Medicina Transfusional Ltda - Hospital...   
74   Secretaria de Estado da Saúde do Espírito Sant...   
120               Santa Casa de Misericordia de Guaçuí   
142  Unimed Norte Capixaba Cooperativa de Trabalho ...   
148  Hemomed Medicina Transfusional Ltda - Hospital...   
180  Hemomed Medicina Transfusional Ltda - Centro M...   
278  Sociedade Beneficente São Camilo - Hospital Sã...   
286      Hemomed Medicina Transfusional Ltda - Hemomed   

    razao_social_nome_fantasia_outros          cnpj    tipo_estabelecimento  \
23                                NaN  


Amostra dos dados únicos (os mais recentes para cada chave):


id          data_envio  ultima_pagina idioma_inicial  semente  \
0  15 2022-11-28 11:00:00              4          pt-BR      NaN   
2  17 2022-11-28 11:09:00              4          pt-BR      NaN   
1  16 2022-11-28 11:20:00              4          pt-BR      NaN   
3  20 2022-11-30 13:53:00              4          pt-BR      NaN   
4  22 2022-12-01 09:57:00              4          pt-BR      NaN   
5  25 2022-12-01 12:21:00              4          pt-BR      NaN   
6  26 2022-12-02 06:59:00              4          pt-BR      NaN   
7  28 2022-12-05 10:19:00              4          pt-BR      NaN   
8  29 2022-12-06 09:36:00              4          pt-BR      NaN   
9  30 2022-12-06 11:49:00              4          pt-BR      NaN   

     codigo_acesso          data_inicio     data_ultima_acao           ip  \
0  vxvDL62C5ez3TbL  2022-11-28 10:49:00  2022-11-28 11:00:00  10.0.11.157   
2  vxvDL62C5ez3TbL  2022-11-28 11:04:00  2022-11-28 11:09:00   10.0.0.216   
1  Sgje9tqyifI28Jl  2022-11-28 10:54:00  2022-11-28 11:20:00   10.0.0.216   
3  z6fJe1OkT46z0Yn  2022-11-30 13:38:00  2022-11-30 13:53:00   10.0.7.253   
4  VSR5a1w4grp1UkS  2022-12-01 09:43:00  2022-12-01 09:57:00  10.0.11.127   
5  Wgven9W01gw8ZCo  2022-12-01 12:07:00  2022-12-01 12:21:00    10.0.8.14   
6  z6fJe1OkT46z0Yn  2022-12-02 06:47:00  2022-12-02 06:59:00  10.0.16.235   
7  ONRtlcXMdnaASJ8  2022-12-05 10:11:00  2022-12-05 10:19:00   10.0.0.168   
8  HnPdCX9rpCjmX01  2022-12-06 08:28:00  2022-12-06 09:36:00   10.0.0.148   
9  Sgje9tqyifI28Jl  2022-12-06 11:35:00  2022-12-06 11:49:00   10.0.0.168   

   identificacao_dado tipo_envio ano_referencia periodo_referencia  \
0                 NaN   ORIGINAL           2022            Outubro   
2                 NaN   ORIGINAL           2022            Outubro   
1                 NaN   ORIGINAL           2022            Outubro   
3                 NaN   ORIGINAL           2022            Outubro   
4                 NaN   ORIGINAL           2022           Novembro   
5                 NaN   ORIGINAL           2022           Novembro   
6                 NaN   ORIGINAL           2022           Novembro   
7                 NaN   ORIGINAL           2022           Novembro   
8                 NaN   ORIGINAL           2022           Novembro   
9                 NaN   ORIGINAL           2022            Outubro   

   identificacao_estabelecimento                                municipio  \
0                            NaN                    Serra, Espírito Santo   
2                            NaN                    Serra, Espírito Santo   
1                            NaN                  Vitória, Espírito Santo   
3                            NaN                 Colatina, Espírito Santo   
4                            NaN  Venda Nova do Imigrante, Espírito Santo   
5                            NaN                 Linhares, Espírito Santo   
6                            NaN                 Colatina, Espírito Santo   
7                            NaN             Nova Venécia, Espírito Santo   
8                            NaN                  Aracruz, Espírito Santo   
9                            NaN                  Vitória, Espírito Santo   

                          razao_social_nome_fantasia  \
0  Hemomed Medicina Transfusional Ltda - Hospital...   
2  Hemomed Medicina Transfusional Ltda - Hospital...   
1                     Pronto Socorro Milena Gottardi   
3                          Casa de Saúde Santa Maria   
4  Associação Social Filantrópica Hospital Padre ...   
5  Banco de Sangue Santa Teresa -  Hospital Linha...   
6                          Casa de Saúde Santa Maria   
7  Sociedade Beneficente São Camilo - Hospital Sã...   
8           Fundação Hospital Maternidade São Camilo   
9  Hospital Estadual Infantil Nossa Senhora da Gl...   

  razao_social_nome_fantasia_outros          cnpj    tipo_estabelecimento  \
0                               NaN  5.674518e+12  Agência Transfusional    
2               

In [70]:
hemoprod_es_deduplicado.to_excel('dados_processados/hemoprod_es.xlsx', index=False)

## Hemoprod Goiás

In [83]:
import os
import pandas as pd

dados_brutos_path = 'dados_brutos'

arquivo_dados_path = os.path.join(dados_brutos_path, 'Hemoprod_GO.xlsx')
nome_planilha = 'HEMOPROD - GOIAS'

dicionario_path_go = ('./dicionario_colunas_269.xlsx')
# dicionario_path_ap = ('./dicionario_colunas_270.xlsx')

dicionario_go = pd.read_excel(dicionario_path_go, sheet_name='Sheet1')

# --- 2. Carregue os dados e o dicionário ---
try:
    # Carrega o arquivo de dados
    hemoprod_go = pd.read_excel(arquivo_dados_path, sheet_name=nome_planilha)
    print("Arquivo de dados carregado com sucesso.")
    print(f"Número de colunas original: {len(hemoprod_go.columns)}")

    # Carrega o arquivo de dicionário
    dicionario = pd.read_excel(dicionario_path_go)
    print("Arquivo de dicionário carregado com sucesso.")

    # --- 3. Extraia a lista de novos nomes ---
    # Pega os valores da coluna 'nome_sql' e converte para uma lista
    novos_nomes = dicionario['nome_sql'].tolist()
    print(f"Número de novos nomes no dicionário: {len(novos_nomes)}")

    # --- 4. Verificação de segurança (MUITO IMPORTANTE) ---
    # Garante que o número de colunas é o mesmo antes de renomear
    if len(hemoprod_go.columns) == len(novos_nomes):
        print("\nO número de colunas corresponde. Renomeando...")
        
        # --- 5. Substitua os nomes das colunas ---
        # Esta é a linha principal que faz a substituição direta
        hemoprod_go.columns = novos_nomes
        
        print("Colunas renomeadas com sucesso!")
        
        # --- 6. Verifique o resultado ---
        print("\nInformações do DataFrame com as novas colunas:")
        hemoprod_go.info()
        
        print("\nAs 5 primeiras linhas com as novas colunas:")
        display(hemoprod_go.head())

    else:
        # Mensagem de erro se o número de colunas for diferente
        print("\n--- ERRO ---")
        print("A renomeação foi cancelada. O número de colunas no arquivo de dados não é igual ao número de nomes no dicionário.")
        print(f"Colunas no arquivo de dados: {len(hemoprod_go.columns)}")
        print(f"Nomes no dicionário: {len(novos_nomes)}")

except FileNotFoundError as e:
    print(f"\nErro de arquivo não encontrado: {e}")
except KeyError as e:
    print(f"\nErro de coluna não encontrada: {e}. Verifique se a coluna 'nome_sql' existe no seu arquivo de dicionário.")
except Exception as e:
    print(f"\nOcorreu um erro inesperado: {e}")



Arquivo de dados carregado com sucesso.
Número de colunas original: 257
Arquivo de dicionário carregado com sucesso.
Número de novos nomes no dicionário: 269

--- ERRO ---
A renomeação foi cancelada. O número de colunas no arquivo de dados não é igual ao número de nomes no dicionário.
Colunas no arquivo de dados: 257
Nomes no dicionário: 269


In [89]:
arquivo_dados_path = os.path.join(dados_brutos_path, 'Hemoprod_CE.xlsx')
nome_planilha = 'Planilha1'
hemoprod_ce1 = pd.read_excel(arquivo_dados_path, sheet_name=nome_planilha)

colunas_padrao = set(hemoprod_ce1.columns)
colunas_estado = set(hemoprod_go.columns)

colunas_faltantes = list(colunas_padrao - colunas_estado)

colunas_a_mais = list(colunas_estado - colunas_padrao)

print(f"Número de colunas faltantes: {len(colunas_faltantes)}")
print(f"Colunas faltantes (a serem adicionadas): {colunas_faltantes}")
print("-" * 30)
print(f"Número de colunas a mais: {len(colunas_a_mais)}")
print(f"Colunas a mais (a serem dropadas): {colunas_a_mais}")


Número de colunas faltantes: 0
Colunas faltantes (a serem adicionadas): []
------------------------------
Número de colunas a mais: 0
Colunas a mais (a serem dropadas): []


In [88]:
import os
import pandas as pd
import numpy as np # Adicionado para usar pd.NA

# --- Assumindo que você já carregou os DataFrames e calculou as listas ---
# hemoprod_ce1 (DataFrame Padrão)
# hemoprod_es (DataFrame do Estado)
# colunas_padrao, colunas_estado, colunas_faltantes, colunas_a_mais

# Nomes das colunas problemáticas
COLUNA_ERRADA = 'Ano de referência '  # A coluna que está 'a mais'
COLUNA_CORRETA = 'Ano de referência\xa0 ' # A coluna que está 'faltando'

# 1. TRATAMENTO DA COLUNA 'ANO DE REFERÊNCIA': RENOMEAR EM VEZ DE DROPAR/ADICIONAR

# if COLUNA_ERRADA in colunas_a_mais and COLUNA_CORRETA in colunas_faltantes:
#     # 1.1. Renomear a coluna no DataFrame do estado (preservando os dados)
#     hemoprod_go = hemoprod_go.rename(columns={COLUNA_ERRADA: COLUNA_CORRETA})
    
#     print(f"COLUNA RENOMEADA: '{COLUNA_ERRADA.strip()}' -> '{COLUNA_CORRETA.strip()}'")
    
#     # 1.2. Remover as colunas tratadas das listas de faltantes e a mais
#     colunas_a_mais.remove(COLUNA_ERRADA)
#     colunas_faltantes.remove(COLUNA_CORRETA)
    
#     print("A coluna de Ano de Referência foi removida das listas de ajuste.")
# else:
#     # Caso os nomes não correspondam ou a coluna não esteja nas listas (improvável, mas seguro)
#     print("A coluna de Ano de Referência não foi tratada por renomeação. Prosseguindo com drop/adição.")


# # 2. CONTINUAR com as colunas restantes: DROP e ADIÇÃO

print("\n--- INICIANDO DROP E ADIÇÃO ---")

# 2.1. DROP das colunas A MAIS restantes
if colunas_a_mais:
    # Observe que COLUNA_ERRADA não está mais aqui
    hemoprod_go = hemoprod_go.drop(columns=colunas_a_mais, errors='ignore')
    print(f"Colunas a mais (restantes) removidas: {colunas_a_mais}")
else:
    print("Nenhuma coluna a mais restante para remover.")


# 2.2. ADICIONAR as colunas FALTANTES restantes e preenchê-las com zero (0)
# A coluna COLUNA_CORRETA também não está mais aqui
colunas_de_texto_para_vazias = ['Os dados informados referem-se à um(a):'] # Adicione outras colunas de texto aqui, se houver

for coluna in colunas_faltantes:
    if coluna in colunas_de_texto_para_vazias:
        # Cria a nova coluna preenchida com valor ausente (pd.NA)
        hemoprod_go[coluna] = pd.NA
    else:
        # Cria a nova coluna preenchida com 0
        hemoprod_go[coluna] = 0

print(f"Colunas faltantes (restantes) adicionadas: {colunas_faltantes}")


# 3. REORDENAR as colunas do hemoprod_go na mesma ordem do padrão
ordem_padrao = hemoprod_ce1.columns.tolist()

# Reorganiza as colunas do hemoprod_go
hemoprod_go = hemoprod_go[ordem_padrao]

print("-" * 50)
print("Processo concluído:")
print(f"Total de colunas após o ajuste: {len(hemoprod_go.columns)}")
print("A ordem das colunas agora corresponde à ordem do hemoprod_ce1.")


--- INICIANDO DROP E ADIÇÃO ---
Nenhuma coluna a mais restante para remover.
Colunas faltantes (restantes) adicionadas: ['6. Produção Hemoterápica  6.1(a) Entradas\xa0  [Concentrado de Plaquetas de Aférese][Recebidas]', '6.1(b) Perdas  [Concentrado de Plaquetas de Aférese][Outros motivos]', '6. Produção Hemoterápica  6.1(a) Entradas\xa0  [Concentrado de Plaquetas de Aférese][Devolvidas]', '6.1(b) Perdas  [Concentrado de Plaquetas de Aférese][Validade]', '6.1(d) Distribuição para outros serviços  \xa0  [Concentrado de Plaquetas de Aférese][Total]', '6.1(c) Tranfusões  [Concentrado de Plaquetas de Aférese][Total]', '6.1(d) Distribuição para outros serviços  \xa0  [Concentrado de Plaquetas de Aférese][Com exame pré-transfusional ]', '6. Produção Hemoterápica  6.1(a) Entradas\xa0  [Concentrado de Plaquetas de Aférese][Produzidas]', '6.1(d) Distribuição para outros serviços  \xa0  [Concentrado de Plaquetas de Aférese][Sem exame pré-transfusional ]', '6.1(c) Tranfusões  [Concentrado de Plaq

In [90]:
# Mapeia as colunas, limpando espaços em branco no início e fim
# e substituindo o caractere \xa0 por um espaço normal.
novos_nomes = {col: col.strip().replace('\xa0', ' ') for col in hemoprod_go.columns}

# Aplica a renomeação
hemoprod_go = hemoprod_go.rename(columns=novos_nomes)

print("Nomes das colunas limpos e padronizados.")

Nomes das colunas limpos e padronizados.


In [91]:
print("--- Nomes das Colunas (um por linha) ---")
for coluna in hemoprod_go.columns:
    print(coluna + ",") 

--- Nomes das Colunas (um por linha) ---
ID da resposta,
Data de envio,
Última página,
Idioma inicial,
Semente,
Código de acesso,
Data de início,
Data da última ação,
Endereço IP,
IDENTIFICAÇÃO DO DADO,
Tipo de Informação  Antes de responder ao formulário, declare o tipo de informação que será inserida.,
Ano de referência,
Período de referência,
IDENTIFICAÇÃO DO ESTABELECIMENTO,
Município,
Razão Social - Nome Fantasia,
Razão Social - Nome Fantasia  [Outros],
CNPJ,
Tipo de estabelecimento,
Natureza do estabelecimento,
Os dados informados referem-se à um(a):,
Cite os estabelecimentos que compõem a rede  Informe o Tipo de Estabelecimento, o Nome Fantasia e o Município de localização de cada um.,
CNES - Cadastro Nacional de Estabelecimentos de Saúde,
Endereço,
2. Triagem Clínica  2.1 Total de candidatos quanto ao tipo de doação  [Espontânea][Aptos],
2. Triagem Clínica  2.1 Total de candidatos quanto ao tipo de doação  [Espontânea][Inaptos],
2. Triagem Clínica  2.1 Total de candidatos quant

In [92]:
hemoprod_go.head()

ID da resposta        Data de envio  Última página Idioma inicial  \
0               2  2023-04-06 10:24:01              4          pt-BR   
1               4  2023-04-10 16:13:24              4          pt-BR   
2               5  2023-04-11 16:26:17              4          pt-BR   
3               7  2023-04-22 20:12:00              4          pt-BR   
4               8  2023-05-09 09:11:08              4          pt-BR   

        Semente Código de acesso       Data de início  Data da última ação  \
0  8.032299e+08  7ViMrEUwxtMPA2q  2023-04-06 09:41:19  2023-04-06 10:24:01   
1  8.612602e+08  do26zwKaqbdfirs  2023-04-10 15:42:31  2023-04-10 16:13:24   
2  1.403820e+09  CIYBY7ylc1zXzre  2023-04-11 15:51:51  2023-04-11 16:26:17   
3           NaN  4GNr9cQ99c7Jrbk  2023-04-22 18:34:00  2023-04-22 20:12:00   
4  7.651788e+08  CIYBY7ylc1zXzre  2023-05-09 08:43:08  2023-05-09 09:11:08   

    Endereço IP  IDENTIFICAÇÃO DO DADO  \
0    10.0.0.186                    NaN   
1    10.0.0.186                    NaN   
2  10.0.113.219                    NaN   
3     10.0.1.33                    NaN   
4     10.0.0.47                    NaN   

  Tipo de Informação  Antes de responder ao formulário, declare o tipo de informação que será inserida.  \
0                                           ORIGINAL                                                      
1                                           ORIGINAL                                                      
2                                           ORIGINAL                                                      
3                                           ORIGINAL                                                      
4                                           ORIGINAL                                                      

   Ano de referência Período de referência  IDENTIFICAÇÃO DO ESTABELECIMENTO  \
0               2023                 Março                               NaN   
1               2023                 Março                               NaN   
2               2023                 Março                               NaN   
3               2023               Janeiro                               NaN   
4               2023                 Abril                               NaN   

        Município                       Razão Social - Nome Fantasia  \
0  Goiânia, Goiás  Associação de Combate ao Câncer em Goiás - Hos...   
1  Goiânia, Goiás  Instituto Goiano de Oncologia e Hemoterapia - ...   
2  Goiânia, Goiás  Santa Casa de Misericódia de Goiania - Santa C...   
3  Goiânia, Goiás  Instituto de Hemoterapia de Goiânia (IHG) - Ce...   
4  Goiânia, Goiás  Santa Casa de Misericódia de Goiania - Santa C...   

  Razão Social - Nome Fantasia  [Outros]          CNPJ  \
0                                    NaN  1.585595e+11   
1                                    NaN  1.277573e+12   
2                                    NaN  1.619790e+12   
3       CENTRO DE HEMOTERAPIA DE GOIÂNIA  3.341398e+12   
4                                    NaN  1.619790e+12   

          Tipo de estabelecimento Natureza do estabelecimento  \
0           Núcleo de Hemoterapia                     Público   
1  Unidade de Coleta e Transfusão                     Privado   
2  Unidade de Coleta e Transfusão                 Privado-SUS   
3  Unidade de Coleta e Transfusão                 Privado-SUS   
4  Unidade de Coleta e Transfusão                 Privado-SUS   

  Os dados informados referem-se à um(a):  \
0                           Único serviço   
1                           Único serviço   
2                           Único serviço   
3                           Único serviço   
4                           Único serviço   

  Cite os estabelecimentos que compõem a rede  Informe o Tipo de Estabelecimento, o Nome Fantasia e o Município de localização de cada um.  \
0                                                NaN                                                                                      

In [93]:
# Carrega o arquivo de dicionário
dicionario_path_go = ('./dicionario_colunas_269.xlsx')
dicionario = pd.read_excel(dicionario_path_go)
print("Arquivo de dicionário carregado com sucesso.")

# --- 3. Extraia a lista de novos nomes ---
# Pega os valores da coluna 'nome_sql' e converte para uma lista
novos_nomes = dicionario['nome_sql'].tolist()
print(f"Número de novos nomes no dicionário: {len(novos_nomes)}")

# --- 4. Verificação de segurança (MUITO IMPORTANTE) ---
# Garante que o número de colunas é o mesmo antes de renomear
if len(hemoprod_go.columns) == len(novos_nomes):
    print("\nO número de colunas corresponde. Renomeando...")
    
    # --- 5. Substitua os nomes das colunas ---
    # Esta é a linha principal que faz a substituição direta
    hemoprod_go.columns = novos_nomes
    
    print("Colunas renomeadas com sucesso!")
    
    # --- 6. Verifique o resultado ---
    print("\nInformações do DataFrame com as novas colunas:")
    hemoprod_go.info()
    
    print("\nAs 5 primeiras linhas com as novas colunas:")
    display(hemoprod_go.head())

else:
    # Mensagem de erro se o número de colunas for diferente
    print("\n--- ERRO ---")
    print("A renomeação foi cancelada. O número de colunas no arquivo de dados não é igual ao número de nomes no dicionário.")
    print(f"Colunas no arquivo de dados: {len(hemoprod_go.columns)}")
    print(f"Nomes no dicionário: {len(novos_nomes)}")


Arquivo de dicionário carregado com sucesso.
Número de novos nomes no dicionário: 269

O número de colunas corresponde. Renomeando...
Colunas renomeadas com sucesso!

Informações do DataFrame com as novas colunas:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 474 entries, 0 to 473
Columns: 269 entries, id to hemoprod_3_observacoes
dtypes: float64(92), int64(159), object(18)
memory usage: 996.3+ KB

As 5 primeiras linhas com as novas colunas:


id           data_envio  ultima_pagina idioma_inicial       semente  \
0   2  2023-04-06 10:24:01              4          pt-BR  8.032299e+08   
1   4  2023-04-10 16:13:24              4          pt-BR  8.612602e+08   
2   5  2023-04-11 16:26:17              4          pt-BR  1.403820e+09   
3   7  2023-04-22 20:12:00              4          pt-BR           NaN   
4   8  2023-05-09 09:11:08              4          pt-BR  7.651788e+08   

     codigo_acesso          data_inicio     data_ultima_acao            ip  \
0  7ViMrEUwxtMPA2q  2023-04-06 09:41:19  2023-04-06 10:24:01    10.0.0.186   
1  do26zwKaqbdfirs  2023-04-10 15:42:31  2023-04-10 16:13:24    10.0.0.186   
2  CIYBY7ylc1zXzre  2023-04-11 15:51:51  2023-04-11 16:26:17  10.0.113.219   
3  4GNr9cQ99c7Jrbk  2023-04-22 18:34:00  2023-04-22 20:12:00     10.0.1.33   
4  CIYBY7ylc1zXzre  2023-05-09 08:43:08  2023-05-09 09:11:08     10.0.0.47   

   identificacao_dado tipo_envio  ano_referencia periodo_referencia  \
0                 NaN   ORIGINAL            2023              Março   
1                 NaN   ORIGINAL            2023              Março   
2                 NaN   ORIGINAL            2023              Março   
3                 NaN   ORIGINAL            2023            Janeiro   
4                 NaN   ORIGINAL            2023              Abril   

   identificacao_estabelecimento       municipio  \
0                            NaN  Goiânia, Goiás   
1                            NaN  Goiânia, Goiás   
2                            NaN  Goiânia, Goiás   
3                            NaN  Goiânia, Goiás   
4                            NaN  Goiânia, Goiás   

                          razao_social_nome_fantasia  \
0  Associação de Combate ao Câncer em Goiás - Hos...   
1  Instituto Goiano de Oncologia e Hemoterapia - ...   
2  Santa Casa de Misericódia de Goiania - Santa C...   
3  Instituto de Hemoterapia de Goiânia (IHG) - Ce...   
4  Santa Casa de Misericódia de Goiania - Santa C...   

  razao_social_nome_fantasia_outros          cnpj  \
0                               NaN  1.585595e+11   
1                               NaN  1.277573e+12   
2                               NaN  1.619790e+12   
3  CENTRO DE HEMOTERAPIA DE GOIÂNIA  3.341398e+12   
4                               NaN  1.619790e+12   

             tipo_estabelecimento natureza_estabelecimento  \
0           Núcleo de Hemoterapia                  Público   
1  Unidade de Coleta e Transfusão                  Privado   
2  Unidade de Coleta e Transfusão              Privado-SUS   
3  Unidade de Coleta e Transfusão              Privado-SUS   
4  Unidade de Coleta e Transfusão              Privado-SUS   

  dados_informados_referem_se rede_estabelecimento  cnes  endereco  \
0               Único serviço                  NaN   NaN       NaN   
1               Único serviço                  NaN   NaN       NaN   
2               Único serviço                  NaN   NaN       NaN   
3               Único serviço                  NaN   NaN       NaN   
4               Único serviço                  NaN   NaN       NaN   

   triagem_clinica_total_doacao_espontanea_aptos  \
0                                          408.0   
1                                          362.0   
2                                          254.0   
3                                          189.0   
4                                          239.0   

   triagem_clinica_total_doacao_espontanea_inaptos  \
0                                             79.0   
1                                             22.0   
2                                            118.0   
3                                             16.0   
4                                            112.0   

   triagem_clinica_total_doacao_reposicao_aptos  \
0                                         363.0   
1                                         794.0   
2                                           0.0   
3                                         410.0   
4     

In [95]:
hemoprod_go.describe()

id  ultima_pagina       semente  identificacao_dado  \
count  474.000000          474.0  4.630000e+02                 0.0   
mean   292.487342            4.0  1.116554e+09                 NaN   
std    164.757561            0.0  6.098059e+08                 NaN   
min      2.000000            4.0  4.685700e+05                 NaN   
25%    154.250000            4.0  5.936350e+08                 NaN   
50%    286.000000            4.0  1.143310e+09                 NaN   
75%    437.750000            4.0  1.646603e+09                 NaN   
max    580.000000            4.0  2.141692e+09                 NaN   

       ano_referencia  identificacao_estabelecimento          cnpj  cnes  \
count      474.000000                            0.0  4.740000e+02   0.0   
mean      2023.921941                            NaN  7.126499e+12   NaN   
std          0.804469                            NaN  1.196518e+13   NaN   
min       2022.000000                            NaN  1.585595e+03   NaN   
25%       2023.000000                            NaN  2.529964e+12   NaN   
50%       2024.000000                            NaN  2.529964e+12   NaN   
75%       2025.000000                            NaN  2.529964e+12   NaN   
max       2025.000000                            NaN  4.945035e+13   NaN   

       endereco  triagem_clinica_total_doacao_espontanea_aptos  \
count       0.0                                     454.000000   
mean        NaN                                     437.460352   
std         NaN                                     597.295710   
min         NaN                                       0.000000   
25%         NaN                                     144.250000   
50%         NaN                                     254.500000   
75%         NaN                                     418.750000   
max         NaN                                    3040.000000   

       triagem_clinica_total_doacao_espontanea_inaptos  \
count                                       454.000000   
mean                                         63.162996   
std                                         105.918457   
min                                           0.000000   
25%                                          12.000000   
50%                                          30.000000   
75%                                          60.000000   
max                                         598.000000   

       triagem_clinica_total_doacao_reposicao_aptos  \
count                                    454.000000   
mean                                     181.024229   
std                                      273.361944   
min                                        0.000000   
25%                                        2.000000   
50%                                       19.000000   
75%                                      293.750000   
max                                     1226.000000   

       triagem_clinica_total_doacao_reposicao_inaptos  \
count                                      454.000000   
mean                                        20.248899   
std                                         31.746612   
min                                          0.000000   
25%                                          0.000000   
50%                                          2.000000   
75%                                         32.000000   
max                                        221.000000   

       triagem_clinica_total_doacao_autologa_aptos  \
count                                   454.000000   
mean                                      0.555066   
std                                       2.505677   
min                                       0.000000   
25%                                       0.000000   
50%                                       0.000000   
75%                                       0.000000   
max                                      23.000000   

       triagem_clinica_total_doacao_autologa_inaptos  \
count                       

In [96]:
# --- 2. Defina as colunas para a chave e para ordenação ---
registros_antes = len(hemoprod_go)
print(f"Total de registros ANTES da remoção de duplicatas: {registros_antes}")
    

colunas_chave = [
        'cnpj', 
        'ano_referencia', 
        'periodo_referencia', 
        'razao_social_nome_fantasia'
    ]

coluna_data = 'data_envio'

# --- 3. Verifique se as colunas necessárias existem ---
colunas_necessarias = colunas_chave + [coluna_data]

if not all(col in hemoprod_go.columns for col in colunas_necessarias):
    print("\n--- ERRO ---")
    print("Uma ou mais colunas necessárias para a deduplicação não foram encontradas.")
    colunas_faltantes = [col for col in colunas_necessarias if col not in hemoprod_go.columns]
    print(f"Colunas necessárias: {colunas_necessarias}")
    print(f"Colunas faltantes no DataFrame: {colunas_faltantes}")
else:
    # --- 4. Prepare a coluna de data e ordene os dados ---
    # Converte a coluna 'data_envio' para datetime para garantir a ordenação correta.
    # 'errors='coerce'' transformará datas inválidas em NaT (Not a Time), que são tratadas como nulas.
    hemoprod_go[coluna_data] = pd.to_datetime(hemoprod_go[coluna_data], errors='coerce')

    # Ordena o DataFrame. Os registros com data de envio mais recente ficarão por último.
    print(f"\nOrdenando os dados por '{coluna_data}'...")
    hemoprod_go_ordenado = hemoprod_go.sort_values(by=coluna_data, ascending=True)

    # --- 5. Identifique e separe os registros duplicados e únicos ---
    # Em vez de usar drop_duplicates() diretamente, vamos usar duplicated()
    # para criar uma máscara booleana.
    # 'keep='last'' marca todas as ocorrências de uma chave como True, EXCETO a última (a mais recente).
    print(f"Identificando duplicatas com cese na chave: {colunas_chave}...")
    mascara_duplicatas = hemoprod_go_ordenado.duplicated(subset=colunas_chave, keep='last')

    # O DataFrame de removidos conterá todas as linhas marcadas como True
    hemoprod_removidos = hemoprod_go_ordenado[mascara_duplicatas]
    
    # O DataFrame deduplicado conterá o INVERSO (~) da máscara (linhas marcadas como False)
    hemoprod_go_deduplicado = hemoprod_go_ordenado[~mascara_duplicatas]
    
    # Agora podemos contar os registros diretamente dos novos DataFrames
    registros_depois = len(hemoprod_go_deduplicado)
    registros_removidos = len(hemoprod_removidos) 
    
    # --- 6. Exice o resultado ---
    print("\n--- Processo Concluído ---")
    print(f"Registros removidos: {registros_removidos}")
    print(f"Total de registros DEPOIS da remoção de duplicatas: {registros_depois}")

    # (Opcional) Exibe a amostra dos removidos
    print("\nAmostra dos dados REMOVIDOS (os mais antigos/duplicados):")
    display(hemoprod_removidos.head(10))

    # Você pode continuar a usar o DataFrame 'hemoprod_ce_deduplicado' para suas análises
    print("\nAmostra dos dados únicos (os mais recentes para cada chave):")
    display(hemoprod_go_deduplicado.head(10))
    
    # Agora você tem o DataFrame 'hemoprod_removidos' salvo

Total de registros ANTES da remoção de duplicatas: 474

Ordenando os dados por 'data_envio'...
Identificando duplicatas com cese na chave: ['cnpj', 'ano_referencia', 'periodo_referencia', 'razao_social_nome_fantasia']...

--- Processo Concluído ---
Registros removidos: 3
Total de registros DEPOIS da remoção de duplicatas: 471

Amostra dos dados REMOVIDOS (os mais antigos/duplicados):


id          data_envio  ultima_pagina idioma_inicial       semente  \
342  423 2025-02-11 10:29:48              4          pt-BR  2.018850e+09   
408  503 2025-06-11 14:35:08              4          pt-BR  1.463516e+09   
434  535 2025-08-12 09:11:35              4          pt-BR  2.003715e+09   

       codigo_acesso          data_inicio     data_ultima_acao  \
342  VHGGYmZQaVu2QZx  2025-02-11 10:20:27  2025-02-11 10:29:48   
408  VHGGYmZQaVu2QZx  2025-06-11 14:30:12  2025-06-11 14:35:08   
434  VHGGYmZQaVu2QZx  2025-08-12 09:00:19  2025-08-12 09:11:35   

                 ip  identificacao_dado tipo_envio  ano_referencia  \
342   177.107.46.75                 NaN   ORIGINAL            2025   
408   177.107.46.75                 NaN   ORIGINAL            2025   
434  201.55.104.209                 NaN   ORIGINAL            2025   

    periodo_referencia  identificacao_estabelecimento       municipio  \
342            Janeiro                            NaN    Iporá, Goiás   
408               Maio                            NaN    Jataí, Goiás   
434              Julho                            NaN  Catalão, Goiás   

                            razao_social_nome_fantasia  \
342  Fundo Municipal de Saúde - Unidade de Coleta e...   
408  Empresa Transfusional do Entorno Ltda - Hemoce...   
434  Fundo Municipal de Saúde - Hemocentro Regional...   

    razao_social_nome_fantasia_outros          cnpj  \
342                               NaN  2.529964e+12   
408                               NaN  2.529964e+12   
434                               NaN  2.529964e+12   

               tipo_estabelecimento natureza_estabelecimento  \
342  Unidade de Coleta e Transfusão                  Público   
408             Hemocentro Regional                  Público   
434             Hemocentro Regional                  Público   

    dados_informados_referem_se rede_estabelecimento  cnes  endereco  \
342               Único serviço                  NaN   NaN       NaN   
408               Único serviço                  NaN   NaN       NaN   
434               Único serviço                  NaN   NaN       NaN   

     triagem_clinica_total_doacao_espontanea_aptos  \
342                                          163.0   
408                                          381.0   
434                                          260.0   

     triagem_clinica_total_doacao_espontanea_inaptos  \
342                                             34.0   
408                                             65.0   
434                                             14.0   

     triagem_clinica_total_doacao_reposicao_aptos  \
342                                           1.0   
408                                          14.0   
434                                           1.0   

     triagem_clinica_total_doacao_reposicao_inaptos  \
342                                             0.0   
408                                             1.0   
434                                             0.0   

     triagem_clinica_total_doacao_autologa_aptos  \
342                                          0.0   
408                                          0.0   
434                                          0.0   

     triagem_clinica_total_doacao_autologa_inaptos  \
342                                            0.0   
408                                            0.0   
434                                            0.0   

     total_doador_primeira_vez_aptos  total_doador_primeira_vez_inaptos  \
342                             19.0                               12.0   
408                            124.0                               30.0   
434                             87.0                                6.0   

     total_doador_repeticao_aptos  total_doador_repeticao_inaptos  \
342                         127.0                            19.0   
408                         124.0                            11.0   
434                         115.0                   


Amostra dos dados únicos (os mais recentes para cada chave):


id          data_envio  ultima_pagina idioma_inicial       semente  \
0   2 2023-04-06 10:24:01              4          pt-BR  8.032299e+08   
1   4 2023-04-10 16:13:24              4          pt-BR  8.612602e+08   
2   5 2023-04-11 16:26:17              4          pt-BR  1.403820e+09   
3   7 2023-04-22 20:12:00              4          pt-BR           NaN   
4   8 2023-05-09 09:11:08              4          pt-BR  7.651788e+08   
5   9 2023-05-11 09:12:10              4          pt-BR  1.511861e+09   
6  11 2023-06-03 16:39:49              4          pt-BR  8.956875e+08   
7  14 2023-06-07 09:32:39              4          pt-BR  1.529775e+09   
8  15 2023-06-09 13:26:33              4          pt-BR  7.006197e+08   
9  16 2023-06-12 06:59:13              4          pt-BR  1.313326e+09   

     codigo_acesso          data_inicio     data_ultima_acao            ip  \
0  7ViMrEUwxtMPA2q  2023-04-06 09:41:19  2023-04-06 10:24:01    10.0.0.186   
1  do26zwKaqbdfirs  2023-04-10 15:42:31  2023-04-10 16:13:24    10.0.0.186   
2  CIYBY7ylc1zXzre  2023-04-11 15:51:51  2023-04-11 16:26:17  10.0.113.219   
3  4GNr9cQ99c7Jrbk  2023-04-22 18:34:00  2023-04-22 20:12:00     10.0.1.33   
4  CIYBY7ylc1zXzre  2023-05-09 08:43:08  2023-05-09 09:11:08     10.0.0.47   
5  do26zwKaqbdfirs  2023-05-11 08:39:15  2023-05-11 09:12:10     10.0.0.30   
6  do26zwKaqbdfirs  2023-06-03 16:12:03  2023-06-03 16:39:49    10.0.0.173   
7  7ViMrEUwxtMPA2q  2023-06-07 07:33:57  2023-06-07 09:32:39     10.0.0.37   
8  7ViMrEUwxtMPA2q  2023-06-09 13:01:12  2023-06-09 13:26:33    10.0.4.217   
9  cNvbTtUu9qwibfp  2023-06-12 06:32:18  2023-06-12 06:59:13     10.0.0.68   

   identificacao_dado tipo_envio  ano_referencia periodo_referencia  \
0                 NaN   ORIGINAL            2023              Março   
1                 NaN   ORIGINAL            2023              Março   
2                 NaN   ORIGINAL            2023              Março   
3                 NaN   ORIGINAL            2023            Janeiro   
4                 NaN   ORIGINAL            2023              Abril   
5                 NaN   ORIGINAL            2023              Abril   
6                 NaN   ORIGINAL            2023               Maio   
7                 NaN   ORIGINAL            2023              Abril   
8                 NaN   ORIGINAL            2023               Maio   
9                 NaN   ORIGINAL            2023               Maio   

   identificacao_estabelecimento        municipio  \
0                            NaN   Goiânia, Goiás   
1                            NaN   Goiânia, Goiás   
2                            NaN   Goiânia, Goiás   
3                            NaN   Goiânia, Goiás   
4                            NaN   Goiânia, Goiás   
5                            NaN   Goiânia, Goiás   
6                            NaN   Goiânia, Goiás   
7                            NaN  Goianira, Goiás   
8                            NaN   Goiânia, Goiás   
9                            NaN   Goiânia, Goiás   

                          razao_social_nome_fantasia  \
0  Associação de Combate ao Câncer em Goiás - Hos...   
1  Instituto Goiano de Oncologia e Hemoterapia - ...   
2  Santa Casa de Misericódia de Goiania - Santa C...   
3  Instituto de Hemoterapia de Goiânia (IHG) - Ce...   
4  Santa Casa de Misericódia de Goiania - Santa C...   
5  Instituto Goiano de Oncologia e Hemoterapia - ...   
6  Instituto Goiano de Oncologia e Hemoterapia - ...   
7  Associação de Combate ao Câncer em Goiás - Hos...   
8  Associação de Combate ao Câncer em Goiás - Hos...   
9  Santa Casa de Misericódia de Goiania - Santa C...   

  razao_social_nome_fantasia_outros          cnpj  \
0                               NaN  1.585595e+11   
1                               NaN  1.277573e+12   
2                               NaN  1.619790e+12   
3  CENTRO DE HEMOTERAPIA DE GOIÂNIA  3.341398e+12   
4                               NaN  1.619790e+12   
5                               NaN  1.

In [97]:
hemoprod_go_deduplicado.to_excel('dados_processados/hemoprod_go.xlsx', index=False)

## Hemoprod Hemominas

In [98]:
import os
import pandas as pd

dados_brutos_path = 'dados_brutos'

arquivo_dados_path = os.path.join(dados_brutos_path, 'Hemoprod_Hemominas.xlsx')
nome_planilha = 'HEMOPROD - HEMOMINAS'

dicionario_path_hm = ('./dicionario_colunas_269.xlsx')
# dicionario_path_ap = ('./dicionario_colunas_270.xlsx')

dicionario_hm = pd.read_excel(dicionario_path_hm, sheet_name='Sheet1')

# --- 2. Carregue os dados e o dicionário ---
try:
    # Carrega o arquivo de dados
    hemoprod_hm = pd.read_excel(arquivo_dados_path, sheet_name=nome_planilha)
    print("Arquivo de dados carregado com sucesso.")
    print(f"Número de colunas original: {len(hemoprod_hm.columns)}")

    # Carrega o arquivo de dicionário
    dicionario = pd.read_excel(dicionario_path_hm)
    print("Arquivo de dicionário carregado com sucesso.")

    # --- 3. Extraia a lista de novos nomes ---
    # Pega os valores da coluna 'nome_sql' e converte para uma lista
    novos_nomes = dicionario['nome_sql'].tolist()
    print(f"Número de novos nomes no dicionário: {len(novos_nomes)}")

    # --- 4. Verificação de segurança (MUITO IMPORTANTE) ---
    # Garante que o número de colunas é o mesmo antes de renomear
    if len(hemoprod_hm.columns) == len(novos_nomes):
        print("\nO número de colunas corresponde. Renomeando...")
        
        # --- 5. Substitua os nomes das colunas ---
        # Esta é a linha principal que faz a substituição direta
        hemoprod_hm.columns = novos_nomes
        
        print("Colunas renomeadas com sucesso!")
        
        # --- 6. Verifique o resultado ---
        print("\nInformações do DataFrame com as novas colunas:")
        hemoprod_hm.info()
        
        print("\nAs 5 primeiras linhas com as novas colunas:")
        display(hemoprod_hm.head())

    else:
        # Mensagem de erro se o número de colunas for diferente
        print("\n--- ERRO ---")
        print("A renomeação foi cancelada. O número de colunas no arquivo de dados não é igual ao número de nomes no dicionário.")
        print(f"Colunas no arquivo de dados: {len(hemoprod_hm.columns)}")
        print(f"Nomes no dicionário: {len(novos_nomes)}")

except FileNotFoundError as e:
    print(f"\nErro de arquivo não encontrado: {e}")
except KeyError as e:
    print(f"\nErro de coluna não encontrada: {e}. Verifique se a coluna 'nome_sql' existe no seu arquivo de dicionário.")
except Exception as e:
    print(f"\nOcorreu um erro inesperado: {e}")



Arquivo de dados carregado com sucesso.
Número de colunas original: 270
Arquivo de dicionário carregado com sucesso.
Número de novos nomes no dicionário: 269

--- ERRO ---
A renomeação foi cancelada. O número de colunas no arquivo de dados não é igual ao número de nomes no dicionário.
Colunas no arquivo de dados: 270
Nomes no dicionário: 269


In [99]:
arquivo_dados_path = os.path.join(dados_brutos_path, 'Hemoprod_CE.xlsx')
nome_planilha = 'Planilha1'
hemoprod_ce1 = pd.read_excel(arquivo_dados_path, sheet_name=nome_planilha)

colunas_padrao = set(hemoprod_ce1.columns)
colunas_estado = set(hemoprod_hm.columns)

colunas_faltantes = list(colunas_padrao - colunas_estado)

colunas_a_mais = list(colunas_estado - colunas_padrao)

print(f"Número de colunas faltantes: {len(colunas_faltantes)}")
print(f"Colunas faltantes (a serem adicionadas): {colunas_faltantes}")
print("-" * 30)
print(f"Número de colunas a mais: {len(colunas_a_mais)}")
print(f"Colunas a mais (a serem dropadas): {colunas_a_mais}")

Número de colunas faltantes: 0
Colunas faltantes (a serem adicionadas): []
------------------------------
Número de colunas a mais: 1
Colunas a mais (a serem dropadas): ['Município [Outros]']


In [100]:

print("\n--- INICIANDO DROP E ADIÇÃO ---")

# 2.1. DROP das colunas A MAIS restantes
if colunas_a_mais:
    # Observe que COLUNA_ERRADA não está mais aqui
    hemoprod_hm = hemoprod_hm.drop(columns=colunas_a_mais, errors='ignore')
    print(f"Colunas a mais (restantes) removidas: {colunas_a_mais}")
else:
    print("Nenhuma coluna a mais restante para remover.")


# 2.2. ADICIONAR as colunas FALTANTES restantes e preenchê-las com zero (0)
# A coluna COLUNA_CORRETA também não está mais aqui
colunas_de_texto_para_vazias = ['Os dados informados referem-se à um(a):'] # Adicione outras colunas de texto aqui, se houver

for coluna in colunas_faltantes:
    if coluna in colunas_de_texto_para_vazias:
        # Cria a nova coluna preenchida com valor ausente (pd.NA)
        hemoprod_hm[coluna] = pd.NA
    else:
        # Cria a nova coluna preenchida com 0
        hemoprod_hm[coluna] = 0

print(f"Colunas faltantes (restantes) adicionadas: {colunas_faltantes}")


# 3. REORDENAR as colunas do hemoprod_hm na mesma ordem do padrão
ordem_padrao = hemoprod_ce1.columns.tolist()

# Reorganiza as colunas do hemoprod_hm
hemoprod_hm = hemoprod_hm[ordem_padrao]

print("-" * 50)
print("Processo concluído:")
print(f"Total de colunas após o ajuste: {len(hemoprod_hm.columns)}")
print("A ordem das colunas agora corresponde à ordem do hemoprod_ce1.")


--- INICIANDO DROP E ADIÇÃO ---
Colunas a mais (restantes) removidas: ['Município [Outros]']
Colunas faltantes (restantes) adicionadas: []
--------------------------------------------------
Processo concluído:
Total de colunas após o ajuste: 269
A ordem das colunas agora corresponde à ordem do hemoprod_ce1.


In [101]:
 # Carrega o arquivo de dicionário
dicionario = pd.read_excel(dicionario_path_hm)
print("Arquivo de dicionário carregado com sucesso.")

# --- 3. Extraia a lista de novos nomes ---
# Pega os valores da coluna 'nome_sql' e converte para uma lista
novos_nomes = dicionario['nome_sql'].tolist()
print(f"Número de novos nomes no dicionário: {len(novos_nomes)}")

# --- 4. Verificação de segurança (MUITO IMPORTANTE) ---
# Garante que o número de colunas é o mesmo antes de renomear
if len(hemoprod_hm.columns) == len(novos_nomes):
    print("\nO número de colunas corresponde. Renomeando...")
    
    # --- 5. Substitua os nomes das colunas ---
    # Esta é a linha principal que faz a substituição direta
    hemoprod_hm.columns = novos_nomes
    
    print("Colunas renomeadas com sucesso!")
    
    # --- 6. Verifique o resultado ---
    print("\nInformações do DataFrame com as novas colunas:")
    hemoprod_hm.info()
    
    print("\nAs 5 primeiras linhas com as novas colunas:")
    display(hemoprod_hm.head())

else:
    # Mensagem de erro se o número de colunas for diferente
    print("\n--- ERRO ---")
    print("A renomeação foi cancelada. O número de colunas no arquivo de dados não é igual ao número de nomes no dicionário.")
    print(f"Colunas no arquivo de dados: {len(hemoprod_hm.columns)}")
    print(f"Nomes no dicionário: {len(novos_nomes)}")

Arquivo de dicionário carregado com sucesso.
Número de novos nomes no dicionário: 269

O número de colunas corresponde. Renomeando...
Colunas renomeadas com sucesso!

Informações do DataFrame com as novas colunas:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 930 entries, 0 to 929
Columns: 269 entries, id to hemoprod_3_observacoes
dtypes: float64(26), int64(231), object(12)
memory usage: 1.9+ MB

As 5 primeiras linhas com as novas colunas:


id  data_envio  ultima_pagina  idioma_inicial  semente  codigo_acesso  \
0 NaN         NaN            NaN             NaN      NaN            NaN   
1 NaN         NaN            NaN             NaN      NaN            NaN   
2 NaN         NaN            NaN             NaN      NaN            NaN   
3 NaN         NaN            NaN             NaN      NaN            NaN   
4 NaN         NaN            NaN             NaN      NaN            NaN   

   data_inicio  data_ultima_acao  ip  identificacao_dado  tipo_envio  \
0          NaN               NaN NaN                 NaN         NaN   
1          NaN               NaN NaN                 NaN         NaN   
2          NaN               NaN NaN                 NaN         NaN   
3          NaN               NaN NaN                 NaN         NaN   
4          NaN               NaN NaN                 NaN         NaN   

   ano_referencia periodo_referencia identificacao_estabelecimento  \
0            2022            Janeiro                      B3013      
1            2022            Janeiro                      B3192      
2            2022            Janeiro                      B3193      
3            2022            Janeiro                      B3194      
4            2022            Janeiro                      B3195      

                            municipio  \
0  BELO HORIZONTE, MG                   
1  PATOS DE MINAS, MG                   
2  DIAMANTINA, MG                       
3  POUSO ALEGRE, MG                     
4  MONTES CLAROS, MG                    

                          razao_social_nome_fantasia  \
0  HEMOCENTRO DE BELO HORIZONTE                  ...   
1  HEMOMINAS PATOS DE MINAS                      ...   
2  HEMONUCLEO DE DIAMANTINA                      ...   
3  HEMOMINAS POUSO ALEGRE                        ...   
4  HEMOMINAS MONTES CLAROS                       ...   

                   razao_social_nome_fantasia_outros                cnpj  \
0  'HEMOCENTRO DE BELO HORIZONTE'                ...                       
1  'HEMOCENTRO DE BELO HORIZONTE'                ...  19.904.440/0001-00   
2  'HEMOCENTRO DE BELO HORIZONTE'                ...  03.129.874/0001-31   
3  'HEMOCENTRO DE BELO HORIZONTE'                ...                       
4  'HEMOCENTRO DE BELO HORIZONTE'                ...  17.217.985/0034-72   

     tipo_estabelecimento natureza_estabelecimento  \
0  Hemocentro Coordenador                  Público   
1   Núcleo de Hemoterapia                  Público   
2   Núcleo de Hemoterapia                  Público   
3     Hemocentro Regional                  Público   
4     Hemocentro Regional                  Público   

  dados_informados_referem_se rede_estabelecimento     cnes  \
0               Único serviço                  NaN  4034325   
1               Único serviço                  NaN  2191415   
2               Único serviço                  NaN  2761327   
3               Único serviço                  NaN  2761416   
4               Único serviço                  NaN  2218933   

                                            endereco  \
0  ALAMEDA EZEQUIEL DIAS, 321 - SANTA EFIGENIA   ...   
1  RUA MAJOR GOTE, 1255 - CENTRO                 ...   
2  RUA RUA DA GLORIA, 469, FUNDOS - CENTRO       ...   
3  RUA COMENDADOR JOSE GARCIA, 825 - CENTRO      ...   
4  RUA URBINO VIANA, 640 - VILA GUILHERMINA      ...   

   triagem_clinica_total_doacao_espontanea_aptos  \
0                                           1676   
1                                            380   
2                                             79   
3                                            350   
4                                            442   

   triagem_clinica_total_doacao_espontanea_inaptos  \
0                                              384   
1                                               76   
2                                               25   
3                                              115   
4                          

In [102]:
# --- 2. Defina as colunas para a chave e para ordenação ---
registros_antes = len(hemoprod_hm)
print(f"Total de registros ANTES da remoção de duplicatas: {registros_antes}")
    

colunas_chave = [
        'cnpj', 
        'ano_referencia', 
        'periodo_referencia', 
        'razao_social_nome_fantasia'
    ]

coluna_data = 'data_envio'

# --- 3. Verifique se as colunas necessárias existem ---
colunas_necessarias = colunas_chave + [coluna_data]

if not all(col in hemoprod_hm.columns for col in colunas_necessarias):
    print("\n--- ERRO ---")
    print("Uma ou mais colunas necessárias para a deduplicação não foram encontradas.")
    colunas_faltantes = [col for col in colunas_necessarias if col not in hemoprod_hm.columns]
    print(f"Colunas necessárias: {colunas_necessarias}")
    print(f"Colunas faltantes no DataFrame: {colunas_faltantes}")
else:
    # --- 4. Prepare a coluna de data e ordene os dados ---
    # Converte a coluna 'data_envio' para datetime para garantir a ordenação correta.
    # 'errors='coerce'' transformará datas inválidas em NaT (Not a Time), que são tratadas como nulas.
    hemoprod_hm[coluna_data] = pd.to_datetime(hemoprod_hm[coluna_data], errors='coerce')

    # Ordena o DataFrame. Os registros com data de envio mais recente ficarão por último.
    print(f"\nOrdenando os dados por '{coluna_data}'...")
    hemoprod_hm_ordenado = hemoprod_hm.sort_values(by=coluna_data, ascending=True)

    # --- 5. Identifique e separe os registros duplicados e únicos ---
    # Em vez de usar drop_duplicates() diretamente, vamos usar duplicated()
    # para criar uma máscara booleana.
    # 'keep='last'' marca todas as ocorrências de uma chave como True, EXCETO a última (a mais recente).
    print(f"Identificando duplicatas com cese na chave: {colunas_chave}...")
    mascara_duplicatas = hemoprod_hm_ordenado.duplicated(subset=colunas_chave, keep='last')

    # O DataFrame de removidos conterá todas as linhas marcadas como True
    hemoprod_removidos = hemoprod_hm_ordenado[mascara_duplicatas]
    
    # O DataFrame deduplicado conterá o INVERSO (~) da máscara (linhas marcadas como False)
    hemoprod_hm_deduplicado = hemoprod_hm_ordenado[~mascara_duplicatas]
    
    # Agora podemos contar os registros diretamente dos novos DataFrames
    registros_depois = len(hemoprod_hm_deduplicado)
    registros_removidos = len(hemoprod_removidos) 
    
    # --- 6. Exice o resultado ---
    print("\n--- Processo Concluído ---")
    print(f"Registros removidos: {registros_removidos}")
    print(f"Total de registros DEPOIS da remoção de duplicatas: {registros_depois}")

    # (Opcional) Exibe a amostra dos removidos
    print("\nAmostra dos dados REMOVIDOS (os mais antigos/duplicados):")
    display(hemoprod_removidos.head(10))

    # Você pode continuar a usar o DataFrame 'hemoprod_ce_deduplicado' para suas análises
    print("\nAmostra dos dados únicos (os mais recentes para cada chave):")
    display(hemoprod_hm_deduplicado.head(10))
    
    # Agora você tem o DataFrame 'hemoprod_removidos' salvo

Total de registros ANTES da remoção de duplicatas: 930

Ordenando os dados por 'data_envio'...
Identificando duplicatas com cese na chave: ['cnpj', 'ano_referencia', 'periodo_referencia', 'razao_social_nome_fantasia']...

--- Processo Concluído ---
Registros removidos: 0
Total de registros DEPOIS da remoção de duplicatas: 930

Amostra dos dados REMOVIDOS (os mais antigos/duplicados):


Empty DataFrame
Columns: [id, data_envio, ultima_pagina, idioma_inicial, semente, codigo_acesso, data_inicio, data_ultima_acao, ip, identificacao_dado, tipo_envio, ano_referencia, periodo_referencia, identificacao_estabelecimento, municipio, razao_social_nome_fantasia, razao_social_nome_fantasia_outros, cnpj, tipo_estabelecimento, natureza_estabelecimento, dados_informados_referem_se, rede_estabelecimento, cnes, endereco, triagem_clinica_total_doacao_espontanea_aptos, triagem_clinica_total_doacao_espontanea_inaptos, triagem_clinica_total_doacao_reposicao_aptos, triagem_clinica_total_doacao_reposicao_inaptos, triagem_clinica_total_doacao_autologa_aptos, triagem_clinica_total_doacao_autologa_inaptos, total_doador_primeira_vez_aptos, total_doador_primeira_vez_inaptos, total_doador_repeticao_aptos, total_doador_repeticao_inaptos, total_doador_esporadico_aptos, total_doador_esporadico_inaptos, total_doador_masculino_aptos, total_doador_masculino_inaptos, total_doador_feminino_aptos, total_doador_feminino_inaptos, total_doador_menor_de_18_anos_aptos, total_doador_menor_de_18_anos_inaptos, total_doador_18_ate_29_anos_aptos, total_doador_18_ate_29_anos_inaptos, total_doador_acima_de_29_anos_aptos, total_doador_acima_de_29_anos_inaptos, total_candidatos_inaptos_anemia_masculino, total_candidatos_inaptos_anemia_feminino, total_candidatos_inaptos_anemia_total, total_candidatos_inaptos_hipertensao_masculino, total_candidatos_inaptos_hipertensao_feminino, total_candidatos_inaptos_hipertensao_total, total_candidatos_inaptos_hipotensao_masculino, total_candidatos_inaptos_hipotensao_feminino, total_candidatos_inaptos_hipotensao_total, total_candidatos_inaptos_alcoolismo_masculino, total_candidatos_inaptos_alcoolismo_feminino, total_candidatos_inaptos_alcoolismo_total, total_candidatos_inaptos_comportamento_risco_dst_masculino, total_candidatos_inaptos_comportamento_risco_dst_feminino, total_candidatos_inaptos_comportamento_risco_dst_total, total_candidatos_inaptos_uso_drogas_masculino, total_candidatos_inaptos_uso_drogas_feminino, total_candidatos_inaptos_uso_drogas_total, total_candidatos_inaptos_hepatite_masculino, total_candidatos_inaptos_hepatite_feminino, total_candidatos_inaptos_hepatite_total, total_candidatos_inaptos_doenca_chagas_masculino, total_candidatos_inaptos_doenca_chagas_feminino, total_candidatos_inaptos_doenca_chagas_total, total_candidatos_inaptos_malaria_masculino, total_candidatos_inaptos_malaria_feminino, total_candidatos_inaptos_malaria_total, total_candidatos_inaptos_outras_masculino, total_candidatos_inaptos_outras_feminino, total_candidatos_inaptos_outras_total, coleta_total_candidatos_desistentes, total_interrupcoes_coleta_dificuldade_puncao_venosa, total_interrupcoes_coleta_reacao_vagal, total_interrupcoes_coleta_outros_motivos, total_coletas_sangue_total, total_coletas_aferese, hemoprod_1_observacoes, exames_triagem_doenca_doenca_chagas_amostras_testadas, exames_triagem_doenca_doenca_chagas_amostras_reagentes, exames_triagem_doenca_hiv_amostras_testadas, exames_triagem_doenca_hiv_amostras_reagentes, exames_triagem_doenca_sifilis_amostras_testadas, `exames_triagem_doenca_sifilis_amostras_reagentes, exames_triagem_doenca_hepatite_b_hbs_ag_amostras_testadas, exames_triagem_doenca_hepatite_b_hbs_ag_amostras_reagentes, exames_triagem_doenca_hepatite_b_anti_hbc_amostras_testadas, exames_triagem_doenca_hepatite_b_anti_hbc_amostras_reagentes, exames_triagem_doenca_hepatite_c_amostras_testadas, exames_triagem_doenca_hepatite_c_amostras_reagentes, exames_triagem_doenca_htlv_i_ii_amostras_testadas, exames_triagem_doenca_htlv_i_ii_amostras_reagentes, exames_triagem_doenca_malaria_amostras_testadas, exames_triagem_doenca_malaria_amostras_reagentes, exames_triagem_doenca_hbv_teste_nat_amostras_testadas, ...]
Index: []


Amostra dos dados únicos (os mais recentes para cada chave):


id data_envio  ultima_pagina  idioma_inicial  semente  codigo_acesso  \
0 NaN        NaT            NaN             NaN      NaN            NaN   
1 NaN        NaT            NaN             NaN      NaN            NaN   
2 NaN        NaT            NaN             NaN      NaN            NaN   
3 NaN        NaT            NaN             NaN      NaN            NaN   
4 NaN        NaT            NaN             NaN      NaN            NaN   
5 NaN        NaT            NaN             NaN      NaN            NaN   
6 NaN        NaT            NaN             NaN      NaN            NaN   
7 NaN        NaT            NaN             NaN      NaN            NaN   
8 NaN        NaT            NaN             NaN      NaN            NaN   
9 NaN        NaT            NaN             NaN      NaN            NaN   

   data_inicio  data_ultima_acao  ip  identificacao_dado  tipo_envio  \
0          NaN               NaN NaN                 NaN         NaN   
1          NaN               NaN NaN                 NaN         NaN   
2          NaN               NaN NaN                 NaN         NaN   
3          NaN               NaN NaN                 NaN         NaN   
4          NaN               NaN NaN                 NaN         NaN   
5          NaN               NaN NaN                 NaN         NaN   
6          NaN               NaN NaN                 NaN         NaN   
7          NaN               NaN NaN                 NaN         NaN   
8          NaN               NaN NaN                 NaN         NaN   
9          NaN               NaN NaN                 NaN         NaN   

   ano_referencia periodo_referencia identificacao_estabelecimento  \
0            2022            Janeiro                      B3013      
1            2022            Janeiro                      B3192      
2            2022            Janeiro                      B3193      
3            2022            Janeiro                      B3194      
4            2022            Janeiro                      B3195      
5            2022            Janeiro                      B3196      
6            2022            Janeiro                      B3197      
7            2022            Janeiro                      B3198      
8            2022            Janeiro                      B3199      
9            2022            Janeiro                      B3200      

                            municipio  \
0  BELO HORIZONTE, MG                   
1  PATOS DE MINAS, MG                   
2  DIAMANTINA, MG                       
3  POUSO ALEGRE, MG                     
4  MONTES CLAROS, MG                    
5  PONTE NOVA, MG                       
6  GOVERNADOR VALADARES, MG             
7  UBERABA, MG                          
8  SETE LAGOAS, MG                      
9  DIVINOPOLIS, MG                      

                          razao_social_nome_fantasia  \
0  HEMOCENTRO DE BELO HORIZONTE                  ...   
1  HEMOMINAS PATOS DE MINAS                      ...   
2  HEMONUCLEO DE DIAMANTINA                      ...   
3  HEMOMINAS POUSO ALEGRE                        ...   
4  HEMOMINAS MONTES CLAROS                       ...   
5  HEMOMINAS PONTE NOVA                          ...   
6  HEMOMINAS GOVERNADOR VALADARES                ...   
7  HEMOMINAS UBERABA                             ...   
8  HEMOMINAS SETE LAGOAS                         ...   
9  HEMOMINAS DIVINOPOLIS                         ...   

                   razao_social_nome_fantasia_outros                cnpj  \
0  'HEMOCENTRO DE BELO HORIZONTE'                ...                       
1  'HEMOCENTRO DE BELO HORIZONTE'                ...  19.904.440/0001-00   
2  'HEMOCENTRO DE BELO HORIZONTE'                ...  03.129.874/0001-31   
3  'HEMOCENTRO DE BELO HORIZONTE'                ...                       
4  'HEMOCENTRO DE BELO HORIZONTE'                ...  17.217.985/0034-72   
5  'HEMOCENTRO DE BELO HORIZONTE'                ...                       
6  'HEMOCENT

In [103]:
hemoprod_hm_deduplicado.to_excel('dados_processados/hemoprod_hm.xlsx', index=False)

## Hemoprod Maranhão

In [106]:
import os
import pandas as pd

dados_brutos_path = 'dados_brutos'

arquivo_dados_path = os.path.join(dados_brutos_path, 'Hemoprod_MA.xlsx')
nome_planilha = 'HEMOPROD - MARANHAO'

dicionario_path_ma = ('./dicionario_colunas_269.xlsx')
# dicionario_path_ap = ('./dicionario_colunas_270.xlsx')

dicionario_ma = pd.read_excel(dicionario_path_ma, sheet_name='Sheet1')

# --- 2. Carregue os dados e o dicionário ---
try:
    # Carrega o arquivo de dados
    hemoprod_ma = pd.read_excel(arquivo_dados_path, sheet_name=nome_planilha)
    print("Arquivo de dados carregado com sucesso.")
    print(f"Número de colunas original: {len(hemoprod_ma.columns)}")

    # Carrega o arquivo de dicionário
    dicionario = pd.read_excel(dicionario_path_ma)
    print("Arquivo de dicionário carregado com sucesso.")

    # --- 3. Extraia a lista de novos nomes ---
    # Pega os valores da coluna 'nome_sql' e converte para uma lista
    novos_nomes = dicionario['nome_sql'].tolist()
    print(f"Número de novos nomes no dicionário: {len(novos_nomes)}")

    # --- 4. Verificação de segurança (MUITO IMPORTANTE) ---
    # Garante que o número de colunas é o mesmo antes de renomear
    if len(hemoprod_ma.columns) == len(novos_nomes):
        print("\nO número de colunas corresponde. Renomeando...")
        
        # --- 5. Substitua os nomes das colunas ---
        # Esta é a linha principal que faz a substituição direta
        hemoprod_ma.columns = novos_nomes
        
        print("Colunas renomeadas com sucesso!")
        
        # --- 6. Verifique o resultado ---
        print("\nInformações do DataFrame com as novas colunas:")
        hemoprod_ma.info()
        
        print("\nAs 5 primeiras linhas com as novas colunas:")
        display(hemoprod_ma.head())

    else:
        # Mensagem de erro se o número de colunas for diferente
        print("\n--- ERRO ---")
        print("A renomeação foi cancelada. O número de colunas no arquivo de dados não é igual ao número de nomes no dicionário.")
        print(f"Colunas no arquivo de dados: {len(hemoprod_ma.columns)}")
        print(f"Nomes no dicionário: {len(novos_nomes)}")

except FileNotFoundError as e:
    print(f"\nErro de arquivo não encontrado: {e}")
except KeyError as e:
    print(f"\nErro de coluna não encontrada: {e}. Verifique se a coluna 'nome_sql' existe no seu arquivo de dicionário.")
except Exception as e:
    print(f"\nOcorreu um erro inesperado: {e}")



Arquivo de dados carregado com sucesso.
Número de colunas original: 269
Arquivo de dicionário carregado com sucesso.
Número de novos nomes no dicionário: 269

O número de colunas corresponde. Renomeando...
Colunas renomeadas com sucesso!

Informações do DataFrame com as novas colunas:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 45 entries, 0 to 44
Columns: 269 entries, id to hemoprod_3_observacoes
dtypes: float64(95), int64(160), object(14)
memory usage: 94.7+ KB

As 5 primeiras linhas com as novas colunas:


id           data_envio  ultima_pagina idioma_inicial  semente  \
0   7  2023-04-06 16:19:00              4          pt-BR      NaN   
1   8  2023-04-12 15:54:00              4          pt-BR      NaN   
2   9  2023-04-12 16:10:00              4          pt-BR      NaN   
3  10  2023-05-08 11:57:00              4          pt-BR      NaN   
4  11  2023-06-05 12:01:00              4          pt-BR      NaN   

     codigo_acesso          data_inicio     data_ultima_acao           ip  \
0  2zW7HEkDmwFPz8b  2023-04-06 16:06:00  2023-04-06 16:19:00    10.0.1.35   
1  2zW7HEkDmwFPz8b  2023-04-12 15:41:00  2023-04-12 15:54:00   10.0.0.186   
2  2zW7HEkDmwFPz8b  2023-04-12 15:58:00  2023-04-12 16:10:00  10.0.35.138   
3  2zW7HEkDmwFPz8b  2023-05-08 11:49:00  2023-05-08 11:57:00  10.0.51.163   
4  2zW7HEkDmwFPz8b  2023-06-05 11:50:00  2023-06-05 12:01:00   10.0.0.182   

   identificacao_dado tipo_envio  ano_referencia periodo_referencia  \
0                 NaN   ORIGINAL            2023              Março   
1                 NaN   ORIGINAL            2023            Janeiro   
2                 NaN   ORIGINAL            2023          Fevereiro   
3                 NaN   ORIGINAL            2023              Abril   
4                 NaN   ORIGINAL            2023               Maio   

   identificacao_estabelecimento           municipio  \
0                            NaN  São Luís, Maranhão   
1                            NaN  São Luís, Maranhão   
2                            NaN  São Luís, Maranhão   
3                            NaN  São Luís, Maranhão   
4                            NaN  São Luís, Maranhão   

                          razao_social_nome_fantasia  \
0  Fujisan Centro de Hemoterapia e Hematologia do...   
1  Fujisan Centro de Hemoterapia e Hematologia do...   
2  Fujisan Centro de Hemoterapia e Hematologia do...   
3  Fujisan Centro de Hemoterapia e Hematologia do...   
4  Fujisan Centro de Hemoterapia e Hematologia do...   

                   razao_social_nome_fantasia_outros           cnpj  \
0  FUJISAN CENTRO DE HEMOTERAPIA E HEMATOLOGIA DO...  7871676000957   
1  FUJISAN CENTRO DE HEMOTERAPIA E HEMATOLOGIA DO...  7871676000957   
2  FUJISAN CENTRO DE HEMOTERAPIA E HEMATOLOGIA DO...  7871676000957   
3  FUJISAN CENTRO DE HEMOTERAPIA E HEMATOLOGIA DO...  7871676000957   
4  FUJISAN CENTRO DE HEMOTERAPIA E HEMATOLOGIA DO...  7871676000957   

     tipo_estabelecimento natureza_estabelecimento  \
0  Agência Transfusional                   Privado   
1  Agência Transfusional                   Privado   
2  Agência Transfusional                   Privado   
3  Agência Transfusional                   Privado   
4  Agência Transfusional                   Privado   

  dados_informados_referem_se  rede_estabelecimento  cnes  endereco  \
0               Único serviço                   NaN   NaN       NaN   
1               Único serviço                   NaN   NaN       NaN   
2               Único serviço                   NaN   NaN       NaN   
3               Único serviço                   NaN   NaN       NaN   
4               Único serviço                   NaN   NaN       NaN   

   triagem_clinica_total_doacao_espontanea_aptos  \
0                                            NaN   
1                                            NaN   
2                                            NaN   
3                                            NaN   
4                                            NaN   

   triagem_clinica_total_doacao_espontanea_inaptos  \
0                                              NaN   
1                                              NaN   
2                                              NaN   
3                                              NaN   
4                                              NaN   

   triagem_clinica_total_doacao_reposicao_aptos  \
0                                           NaN   
1                                           NaN   
2                                           NaN   
3  

In [107]:
# --- 2. Defina as colunas para a chave e para ordenação ---
registros_antes = len(hemoprod_ma)
print(f"Total de registros ANTES da remoção de duplicatas: {registros_antes}")
    

colunas_chave = [
        'cnpj', 
        'ano_referencia', 
        'periodo_referencia', 
        'razao_social_nome_fantasia'
    ]

coluna_data = 'data_envio'

# --- 3. Verifique se as colunas necessárias existem ---
colunas_necessarias = colunas_chave + [coluna_data]

if not all(col in hemoprod_ma.columns for col in colunas_necessarias):
    print("\n--- ERRO ---")
    print("Uma ou mais colunas necessárias para a deduplicação não foram encontradas.")
    colunas_faltantes = [col for col in colunas_necessarias if col not in hemoprod_ma.columns]
    print(f"Colunas necessárias: {colunas_necessarias}")
    print(f"Colunas faltantes no DataFrame: {colunas_faltantes}")
else:
    # --- 4. Prepare a coluna de data e ordene os dados ---
    # Converte a coluna 'data_envio' para datetime para garantir a ordenação correta.
    # 'errors='coerce'' transformará datas inválidas em NaT (Not a Time), que são tratadas como nulas.
    hemoprod_ma[coluna_data] = pd.to_datetime(hemoprod_ma[coluna_data], errors='coerce')

    # Ordena o DataFrame. Os registros com data de envio mais recente ficarão por último.
    print(f"\nOrdenando os dados por '{coluna_data}'...")
    hemoprod_ma_ordenado = hemoprod_ma.sort_values(by=coluna_data, ascending=True)

    # --- 5. Identifique e separe os registros duplicados e únicos ---
    # Em vez de usar drop_duplicates() diretamente, vamos usar duplicated()
    # para criar uma máscara booleana.
    # 'keep='last'' marca todas as ocorrências de uma chave como True, EXCETO a última (a mais recente).
    print(f"Identificando duplicatas com cese na chave: {colunas_chave}...")
    mascara_duplicatas = hemoprod_ma_ordenado.duplicated(subset=colunas_chave, keep='last')

    # O DataFrame de removidos conterá todas as linhas marcadas como True
    hemoprod_removidos = hemoprod_ma_ordenado[mascara_duplicatas]
    
    # O DataFrame deduplicado conterá o INVERSO (~) da máscara (linhas marcadas como False)
    hemoprod_ma_deduplicado = hemoprod_ma_ordenado[~mascara_duplicatas]
    
    # Agora podemos contar os registros diretamente dos novos DataFrames
    registros_depois = len(hemoprod_ma_deduplicado)
    registros_removidos = len(hemoprod_removidos) 
    
    # --- 6. Exice o resultado ---
    print("\n--- Processo Concluído ---")
    print(f"Registros removidos: {registros_removidos}")
    print(f"Total de registros DEPOIS da remoção de duplicatas: {registros_depois}")

    # (Opcional) Exibe a amostra dos removidos
    print("\nAmostra dos dados REMOVIDOS (os mais antigos/duplicados):")
    display(hemoprod_removidos.head(10))

    # Você pode continuar a usar o DataFrame 'hemoprod_ce_deduplicado' para suas análises
    print("\nAmostra dos dados únicos (os mais recentes para cada chave):")
    display(hemoprod_ma_deduplicado.head(10))
    
    # Agora você tem o DataFrame 'hemoprod_removidos' salvo

Total de registros ANTES da remoção de duplicatas: 45

Ordenando os dados por 'data_envio'...
Identificando duplicatas com cese na chave: ['cnpj', 'ano_referencia', 'periodo_referencia', 'razao_social_nome_fantasia']...

--- Processo Concluído ---
Registros removidos: 1
Total de registros DEPOIS da remoção de duplicatas: 44

Amostra dos dados REMOVIDOS (os mais antigos/duplicados):


id          data_envio  ultima_pagina idioma_inicial       semente  \
28  36 2024-06-10 11:01:54              4          pt-BR  1.577533e+09   

      codigo_acesso          data_inicio     data_ultima_acao              ip  \
28  2zW7HEkDmwFPz8b  2024-06-10 10:49:44  2024-06-10 11:01:54  177.184.128.17   

    identificacao_dado tipo_envio  ano_referencia periodo_referencia  \
28                 NaN   ORIGINAL            2024              Junho   

    identificacao_estabelecimento           municipio  \
28                            NaN  São Luís, Maranhão   

                           razao_social_nome_fantasia  \
28  Fujisan Centro de Hemoterapia e Hematologia do...   

   razao_social_nome_fantasia_outros           cnpj    tipo_estabelecimento  \
28                               NaN  7871676000957  Agência Transfusional    

   natureza_estabelecimento dados_informados_referem_se  rede_estabelecimento  \
28                  Privado               Único serviço                   NaN   

    cnes  endereco  triagem_clinica_total_doacao_espontanea_aptos  \
28   NaN       NaN                                            NaN   

    triagem_clinica_total_doacao_espontanea_inaptos  \
28                                              NaN   

    triagem_clinica_total_doacao_reposicao_aptos  \
28                                           NaN   

    triagem_clinica_total_doacao_reposicao_inaptos  \
28                                             NaN   

    triagem_clinica_total_doacao_autologa_aptos  \
28                                          NaN   

    triagem_clinica_total_doacao_autologa_inaptos  \
28                                            NaN   

    total_doador_primeira_vez_aptos  total_doador_primeira_vez_inaptos  \
28                              NaN                                NaN   

    total_doador_repeticao_aptos  total_doador_repeticao_inaptos  \
28                           NaN                             NaN   

    total_doador_esporadico_aptos  total_doador_esporadico_inaptos  \
28                            NaN                              NaN   

    total_doador_masculino_aptos  total_doador_masculino_inaptos  \
28                           NaN                             NaN   

    total_doador_feminino_aptos  total_doador_feminino_inaptos  \
28                          NaN                            NaN   

    total_doador_menor_de_18_anos_aptos  \
28                                  NaN   

    total_doador_menor_de_18_anos_inaptos  total_doador_18_ate_29_anos_aptos  \
28                                    NaN                                NaN   

    total_doador_18_ate_29_anos_inaptos  total_doador_acima_de_29_anos_aptos  \
28                                  NaN                                  NaN   

    total_doador_acima_de_29_anos_inaptos  \
28                                    NaN   

    total_candidatos_inaptos_anemia_masculino  \
28                                        NaN   

    total_candidatos_inaptos_anemia_feminino  \
28                                       NaN   

    total_candidatos_inaptos_anemia_total  \
28                                    NaN   

    total_candidatos_inaptos_hipertensao_masculino  \
28                                             NaN   

    total_candidatos_inaptos_hipertensao_feminino  \
28                                            NaN   

    total_candidatos_inaptos_hipertensao_total  \
28                                         NaN   

    total_candidatos_inaptos_hipotensao_masculino  \
28                                            NaN   

    total_candidatos_inaptos_hipotensao_feminino  \
28                                           NaN   

    total_candidatos_inaptos_hipotensao_total  \
28                                        NaN   

    total_candidatos_inaptos_alcoolismo_masculino  \
28                                            NaN   

    total_candidatos_inaptos_alcoolismo_feminino  \
28                                           NaN  


Amostra dos dados únicos (os mais recentes para cada chave):


id          data_envio  ultima_pagina idioma_inicial       semente  \
0   7 2023-04-06 16:19:00              4          pt-BR           NaN   
1   8 2023-04-12 15:54:00              4          pt-BR           NaN   
2   9 2023-04-12 16:10:00              4          pt-BR           NaN   
3  10 2023-05-08 11:57:00              4          pt-BR           NaN   
4  11 2023-06-05 12:01:00              4          pt-BR           NaN   
5  12 2023-07-06 11:13:18              4          pt-BR  1.958977e+09   
6  13 2023-08-07 14:28:00              4          pt-BR           NaN   
7  14 2023-08-24 11:59:59              4          pt-BR  1.404320e+09   
8  15 2023-08-24 14:13:44              4          pt-BR  1.370605e+09   
9  16 2023-08-24 14:32:08              4          pt-BR  1.837154e+09   

     codigo_acesso          data_inicio     data_ultima_acao           ip  \
0  2zW7HEkDmwFPz8b  2023-04-06 16:06:00  2023-04-06 16:19:00    10.0.1.35   
1  2zW7HEkDmwFPz8b  2023-04-12 15:41:00  2023-04-12 15:54:00   10.0.0.186   
2  2zW7HEkDmwFPz8b  2023-04-12 15:58:00  2023-04-12 16:10:00  10.0.35.138   
3  2zW7HEkDmwFPz8b  2023-05-08 11:49:00  2023-05-08 11:57:00  10.0.51.163   
4  2zW7HEkDmwFPz8b  2023-06-05 11:50:00  2023-06-05 12:01:00   10.0.0.182   
5  2zW7HEkDmwFPz8b  2023-07-06 11:04:36  2023-07-06 11:13:18   10.0.0.205   
6  2zW7HEkDmwFPz8b  2023-08-07 14:14:00  2023-08-07 14:28:00   10.0.1.139   
7  2zW7HEkDmwFPz8b  2023-08-24 11:45:24  2023-08-24 11:59:59   10.0.0.224   
8  2zW7HEkDmwFPz8b  2023-08-24 14:03:45  2023-08-24 14:13:44   10.0.0.224   
9  2zW7HEkDmwFPz8b  2023-08-24 14:18:33  2023-08-24 14:32:08   10.0.0.205   

   identificacao_dado tipo_envio  ano_referencia periodo_referencia  \
0                 NaN   ORIGINAL            2023              Março   
1                 NaN   ORIGINAL            2023            Janeiro   
2                 NaN   ORIGINAL            2023          Fevereiro   
3                 NaN   ORIGINAL            2023              Abril   
4                 NaN   ORIGINAL            2023               Maio   
5                 NaN   ORIGINAL            2023              Junho   
6                 NaN   ORIGINAL            2023              Julho   
7                 NaN   ORIGINAL            2022            Janeiro   
8                 NaN   ORIGINAL            2022          Fevereiro   
9                 NaN   ORIGINAL            2022              Março   

   identificacao_estabelecimento           municipio  \
0                            NaN  São Luís, Maranhão   
1                            NaN  São Luís, Maranhão   
2                            NaN  São Luís, Maranhão   
3                            NaN  São Luís, Maranhão   
4                            NaN  São Luís, Maranhão   
5                            NaN  São Luís, Maranhão   
6                            NaN  São Luís, Maranhão   
7                            NaN  São Luís, Maranhão   
8                            NaN  São Luís, Maranhão   
9                            NaN  São Luís, Maranhão   

                          razao_social_nome_fantasia  \
0  Fujisan Centro de Hemoterapia e Hematologia do...   
1  Fujisan Centro de Hemoterapia e Hematologia do...   
2  Fujisan Centro de Hemoterapia e Hematologia do...   
3  Fujisan Centro de Hemoterapia e Hematologia do...   
4  Fujisan Centro de Hemoterapia e Hematologia do...   
5  Fujisan Centro de Hemoterapia e Hematologia do...   
6  Fujisan Centro de Hemoterapia e Hematologia do...   
7  Fujisan Centro de Hemoterapia e Hematologia do...   
8  Fujisan Centro de Hemoterapia e Hematologia do...   
9  Fujisan Centro de Hemoterapia e Hematologia do...   

                   razao_social_nome_fantasia_outros           cnpj  \
0  FUJISAN CENTRO DE HEMOTERAPIA E HEMATOLOGIA DO...  7871676000957   
1  FUJISAN CENTRO DE HEMOTERAPIA E HEMATOLOGIA DO...  7871676000957   
2  FUJISAN CENTRO DE HEMOTERAPIA E HEMATOLOGIA DO...  7871676000957   
3  FUJISAN CENTRO DE HEMOTERAPIA E HEMATOLOGIA DO..

In [108]:
hemoprod_ma_deduplicado.to_excel('dados_processados/hemoprod_ma.xlsx', index=False)

## Hemoprod Minas Gerais

In [109]:
import os
import pandas as pd

dados_brutos_path = 'dados_brutos'

arquivo_dados_path = os.path.join(dados_brutos_path, 'Hemoprod_MG.xlsx')
nome_planilha = 'HEMOPROD - MINASGERAIS'

dicionario_path_mg = ('./dicionario_colunas_269.xlsx')
# dicionario_path_ap = ('./dicionario_colunas_270.xlsx')

dicionario_mg = pd.read_excel(dicionario_path_mg, sheet_name='Sheet1')

# --- 2. Carregue os dados e o dicionário ---
try:
    # Carrega o arquivo de dados
    hemoprod_mg = pd.read_excel(arquivo_dados_path, sheet_name=nome_planilha)
    print("Arquivo de dados carregado com sucesso.")
    print(f"Número de colunas original: {len(hemoprod_mg.columns)}")

    # Carrega o arquivo de dicionário
    dicionario = pd.read_excel(dicionario_path_mg)
    print("Arquivo de dicionário carregado com sucesso.")

    # --- 3. Extraia a lista de novos nomes ---
    # Pega os valores da coluna 'nome_sql' e converte para uma lista
    novos_nomes = dicionario['nome_sql'].tolist()
    print(f"Número de novos nomes no dicionário: {len(novos_nomes)}")

    # --- 4. Verificação de segurança (MUITO IMPORTANTE) ---
    # Garante que o número de colunas é o mesmo antes de renomear
    if len(hemoprod_mg.columns) == len(novos_nomes):
        print("\nO número de colunas corresponde. Renomeando...")
        
        # --- 5. Substitua os nomes das colunas ---
        # Esta é a linha principal que faz a substituição direta
        hemoprod_mg.columns = novos_nomes
        
        print("Colunas renomeadas com sucesso!")
        
        # --- 6. Verifique o resultado ---
        print("\nInformações do DataFrame com as novas colunas:")
        hemoprod_mg.info()
        
        print("\nAs 5 primeiras linhas com as novas colunas:")
        display(hemoprod_mg.head())

    else:
        # Mensagem de erro se o número de colunas for diferente
        print("\n--- ERRO ---")
        print("A renomeação foi cancelada. O número de colunas no arquivo de dados não é igual ao número de nomes no dicionário.")
        print(f"Colunas no arquivo de dados: {len(hemoprod_mg.columns)}")
        print(f"Nomes no dicionário: {len(novos_nomes)}")

except FileNotFoundError as e:
    print(f"\nErro de arquivo não encontrado: {e}")
except KeyError as e:
    print(f"\nErro de coluna não encontrada: {e}. Verifique se a coluna 'nome_sql' existe no seu arquivo de dicionário.")
except Exception as e:
    print(f"\nOcorreu um erro inesperado: {e}")



Arquivo de dados carregado com sucesso.
Número de colunas original: 270
Arquivo de dicionário carregado com sucesso.
Número de novos nomes no dicionário: 269

--- ERRO ---
A renomeação foi cancelada. O número de colunas no arquivo de dados não é igual ao número de nomes no dicionário.
Colunas no arquivo de dados: 270
Nomes no dicionário: 269


In [110]:
arquivo_dados_path = os.path.join(dados_brutos_path, 'Hemoprod_CE.xlsx')
nome_planilha = 'Planilha1'
hemoprod_ce1 = pd.read_excel(arquivo_dados_path, sheet_name=nome_planilha)

colunas_padrao = set(hemoprod_ce1.columns)
colunas_estado = set(hemoprod_mg.columns)

colunas_faltantes = list(colunas_padrao - colunas_estado)

colunas_a_mais = list(colunas_estado - colunas_padrao)

print(f"Número de colunas faltantes: {len(colunas_faltantes)}")
print(f"Colunas faltantes (a serem adicionadas): {colunas_faltantes}")
print("-" * 30)
print(f"Número de colunas a mais: {len(colunas_a_mais)}")
print(f"Colunas a mais (a serem dropadas): {colunas_a_mais}")

Número de colunas faltantes: 0
Colunas faltantes (a serem adicionadas): []
------------------------------
Número de colunas a mais: 1
Colunas a mais (a serem dropadas): ['Município [Outros]']


In [111]:

print("\n--- INICIANDO DROP E ADIÇÃO ---")

# 2.1. DROP das colunas A MAIS restantes
if colunas_a_mais:
    # Observe que COLUNA_ERRADA não está mais aqui
    hemoprod_mg = hemoprod_mg.drop(columns=colunas_a_mais, errors='ignore')
    print(f"Colunas a mais (restantes) removidas: {colunas_a_mais}")
else:
    print("Nenhuma coluna a mais restante para remover.")


# 2.2. ADICIONAR as colunas FALTANTES restantes e preenchê-las com zero (0)
# A coluna COLUNA_CORRETA também não está mais aqui
colunas_de_texto_para_vazias = ['Os dados informados referem-se à um(a):'] # Adicione outras colunas de texto aqui, se houver

for coluna in colunas_faltantes:
    if coluna in colunas_de_texto_para_vazias:
        # Cria a nova coluna preenchida com valor ausente (pd.NA)
        hemoprod_mg[coluna] = pd.NA
    else:
        # Cria a nova coluna preenchida com 0
        hemoprod_mg[coluna] = 0

print(f"Colunas faltantes (restantes) adicionadas: {colunas_faltantes}")


# 3. REORDENAR as colunas do hemoprod_mg na mesma ordem do padrão
ordem_padrao = hemoprod_ce1.columns.tolist()

# Reorganiza as colunas do hemoprod_mg
hemoprod_mg = hemoprod_mg[ordem_padrao]

print("-" * 50)
print("Processo concluído:")
print(f"Total de colunas após o ajuste: {len(hemoprod_mg.columns)}")
print("A ordem das colunas agora corresponde à ordem do hemoprod_ce1.")


--- INICIANDO DROP E ADIÇÃO ---
Colunas a mais (restantes) removidas: ['Município [Outros]']
Colunas faltantes (restantes) adicionadas: []
--------------------------------------------------
Processo concluído:
Total de colunas após o ajuste: 269
A ordem das colunas agora corresponde à ordem do hemoprod_ce1.


In [112]:
 # Carrega o arquivo de dicionário
dicionario = pd.read_excel(dicionario_path_mg)
print("Arquivo de dicionário carregado com sucesso.")

# --- 3. Extraia a lista de novos nomes ---
# Pega os valores da coluna 'nome_sql' e converte para uma lista
novos_nomes = dicionario['nome_sql'].tolist()
print(f"Número de novos nomes no dicionário: {len(novos_nomes)}")

# --- 4. Verificação de segurança (MUITO IMPORTANTE) ---
# Garante que o número de colunas é o mesmo antes de renomear
if len(hemoprod_mg.columns) == len(novos_nomes):
    print("\nO número de colunas corresponde. Renomeando...")
    
    # --- 5. Substitua os nomes das colunas ---
    # Esta é a linha principal que faz a substituição direta
    hemoprod_mg.columns = novos_nomes
    
    print("Colunas renomeadas com sucesso!")
    
    # --- 6. Verifique o resultado ---
    print("\nInformações do DataFrame com as novas colunas:")
    hemoprod_mg.info()
    
    print("\nAs 5 primeiras linhas com as novas colunas:")
    display(hemoprod_mg.head())

else:
    # Mensagem de erro se o número de colunas for diferente
    print("\n--- ERRO ---")
    print("A renomeação foi cancelada. O número de colunas no arquivo de dados não é igual ao número de nomes no dicionário.")
    print(f"Colunas no arquivo de dados: {len(hemoprod_mg.columns)}")
    print(f"Nomes no dicionário: {len(novos_nomes)}")

Arquivo de dicionário carregado com sucesso.
Número de novos nomes no dicionário: 269

O número de colunas corresponde. Renomeando...
Colunas renomeadas com sucesso!

Informações do DataFrame com as novas colunas:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 271 entries, 0 to 270
Columns: 269 entries, id to hemoprod_3_observacoes
dtypes: float64(92), int64(160), object(17)
memory usage: 569.7+ KB

As 5 primeiras linhas com as novas colunas:


id           data_envio  ultima_pagina idioma_inicial       semente  \
0   5  2023-04-14 16:05:33              4          pt-BR  3.992492e+08   
1  10  2023-04-18 12:22:00              4          pt-BR           NaN   
2  12  2023-04-18 12:52:00              4          pt-BR           NaN   
3  17  2023-04-26 12:27:00              4          pt-BR           NaN   
4  18  2023-04-26 13:02:01              4          pt-BR  1.780040e+09   

     codigo_acesso          data_inicio     data_ultima_acao            ip  \
0  IvycpvVQH6KQqkP  2023-04-14 15:05:11  2023-04-14 16:05:33  10.0.113.219   
1  MfTu2yewsNxvB7k  2023-04-18 11:29:00  2023-04-18 12:22:00     10.0.1.35   
2  MfTu2yewsNxvB7k  2023-04-18 12:26:00  2023-04-18 12:52:00    10.0.0.186   
3  MfTu2yewsNxvB7k  2023-04-26 11:49:00  2023-04-26 12:27:00    10.0.52.44   
4  MfTu2yewsNxvB7k  2023-04-26 12:32:51  2023-04-26 13:02:01    10.0.52.19   

   identificacao_dado tipo_envio  ano_referencia periodo_referencia  \
0                 NaN   ORIGINAL            2023              Março   
1                 NaN   ORIGINAL            2022            Janeiro   
2                 NaN   ORIGINAL            2022          Fevereiro   
3                 NaN   ORIGINAL            2023            Janeiro   
4                 NaN   ORIGINAL            2023          Fevereiro   

   identificacao_estabelecimento                     municipio  \
0                            NaN  Belo Horizonte, Minas Gerais   
1                            NaN         Alfenas, Minas Gerais   
2                            NaN         Alfenas, Minas Gerais   
3                            NaN         Alfenas, Minas Gerais   
4                            NaN         Alfenas, Minas Gerais   

                          razao_social_nome_fantasia  \
0          Vita Hemoterapia Ltda - Vita Hemoterapia    
1  Fundação de Ensino e Tecnologia de Alfenas - H...   
2  Fundação de Ensino e Tecnologia de Alfenas - H...   
3  Fundação de Ensino e Tecnologia de Alfenas - H...   
4  Fundação de Ensino e Tecnologia de Alfenas - H...   

                   razao_social_nome_fantasia_outros            cnpj  \
0                                                NaN  25463423000179   
1  Hospital Universitário Alzira Velano-Banco de ...  17878554001241   
2               Hospital Universitário Alzira Velano  17878554001241   
3               Hospital Universitário Alzira Velano  17878554001241   
4                                                NaN  17878554001241   

             tipo_estabelecimento natureza_estabelecimento  \
0  Unidade de Coleta e Transfusão                  Privado   
1           Núcleo de Hemoterapia              Privado-SUS   
2           Núcleo de Hemoterapia              Privado-SUS   
3           Núcleo de Hemoterapia              Privado-SUS   
4           Núcleo de Hemoterapia              Privado-SUS   

  dados_informados_referem_se rede_estabelecimento  cnes  endereco  \
0               Único serviço                  NaN   NaN       NaN   
1               Único serviço                  NaN   NaN       NaN   
2               Único serviço                  NaN   NaN       NaN   
3               Único serviço                  NaN   NaN       NaN   
4               Único serviço                  NaN   NaN       NaN   

   triagem_clinica_total_doacao_espontanea_aptos  \
0                                          266.0   
1                                           49.0   
2                                           50.0   
3                                           48.0   
4                                           44.0   

   triagem_clinica_total_doacao_espontanea_inaptos  \
0                                             29.0   
1                                             10.0   
2                                             13.0   
3                                             11.0   
4                                              7.0   

   triagem_clinica_total_doacao_reposicao_aptos  \
0           

In [113]:
    # --- 2. Defina as colunas para a chave e para ordenação ---
registros_antes = len(hemoprod_mg)
print(f"Total de registros ANTES da remoção de duplicatas: {registros_antes}")
    

colunas_chave = [
        'cnpj', 
        'ano_referencia', 
        'periodo_referencia', 
        'razao_social_nome_fantasia'
    ]

coluna_data = 'data_envio'

# --- 3. Verifique se as colunas necessárias existem ---
colunas_necessarias = colunas_chave + [coluna_data]

if not all(col in hemoprod_mg.columns for col in colunas_necessarias):
    print("\n--- ERRO ---")
    print("Uma ou mais colunas necessárias para a deduplicação não foram encontradas.")
    colunas_faltantes = [col for col in colunas_necessarias if col not in hemoprod_mg.columns]
    print(f"Colunas necessárias: {colunas_necessarias}")
    print(f"Colunas faltantes no DataFrame: {colunas_faltantes}")
else:
    # --- 4. Prepare a coluna de data e ordene os dados ---
    # Converte a coluna 'data_envio' para datetime para garantir a ordenação correta.
    # 'errors='coerce'' transformará datas inválidas em NaT (Not a Time), que são tratadas como nulas.
    hemoprod_mg[coluna_data] = pd.to_datetime(hemoprod_mg[coluna_data], errors='coerce')

    # Ordena o DataFrame. Os registros com data de envio mais recente ficarão por último.
    print(f"\nOrdenando os dados por '{coluna_data}'...")
    hemoprod_mg_ordenado = hemoprod_mg.sort_values(by=coluna_data, ascending=True)

    # --- 5. Identifique e separe os registros duplicados e únicos ---
    # Em vez de usar drop_duplicates() diretamente, vamos usar duplicated()
    # para criar uma máscara booleana.
    # 'keep='last'' marca todas as ocorrências de uma chave como True, EXCETO a última (a mais recente).
    print(f"Identificando duplicatas com cese na chave: {colunas_chave}...")
    mascara_duplicatas = hemoprod_mg_ordenado.duplicated(subset=colunas_chave, keep='last')

    # O DataFrame de removidos conterá todas as linhas marcadas como True
    hemoprod_removidos = hemoprod_mg_ordenado[mascara_duplicatas]
    
    # O DataFrame deduplicado conterá o INVERSO (~) da máscara (linhas marcadas como False)
    hemoprod_mg_deduplicado = hemoprod_mg_ordenado[~mascara_duplicatas]
    
    # Agora podemos contar os registros diretamente dos novos DataFrames
    registros_depois = len(hemoprod_mg_deduplicado)
    registros_removidos = len(hemoprod_removidos) 
    
    # --- 6. Exice o resultado ---
    print("\n--- Processo Concluído ---")
    print(f"Registros removidos: {registros_removidos}")
    print(f"Total de registros DEPOIS da remoção de duplicatas: {registros_depois}")

    # (Opcional) Exibe a amostra dos removidos
    print("\nAmostra dos dados REMOVIDOS (os mais antigos/duplicados):")
    display(hemoprod_removidos.head(10))

    # Você pode continuar a usar o DataFrame 'hemoprod_ce_deduplicado' para suas análises
    print("\nAmostra dos dados únicos (os mais recentes para cada chave):")
    display(hemoprod_mg_deduplicado.head(10))
    
    # Agora você tem o DataFrame 'hemoprod_removidos' salvo

Total de registros ANTES da remoção de duplicatas: 271

Ordenando os dados por 'data_envio'...
Identificando duplicatas com cese na chave: ['cnpj', 'ano_referencia', 'periodo_referencia', 'razao_social_nome_fantasia']...

--- Processo Concluído ---
Registros removidos: 8
Total de registros DEPOIS da remoção de duplicatas: 263

Amostra dos dados REMOVIDOS (os mais antigos/duplicados):


id          data_envio  ultima_pagina idioma_inicial       semente  \
85   184 2023-11-20 12:45:37              4          pt-BR  1.974213e+09   
138  266 2024-04-08 10:15:29              4          pt-BR  1.448841e+09   
141  271 2024-04-19 10:30:35              4          pt-BR  1.650070e+09   
157  293 2024-06-08 12:16:00              4          pt-BR           NaN   
166  305 2024-07-08 09:59:32              4          pt-BR  1.814253e+08   
215  369 2025-01-20 16:00:29              4          pt-BR  1.209934e+09   
237  394 2025-05-22 10:29:17              4          pt-BR  3.127244e+08   
244  401 2025-07-03 11:22:11              4          pt-BR  1.269800e+09   

       codigo_acesso          data_inicio     data_ultima_acao  \
85   GKfOabdaZZsYIgO  2023-11-20 11:59:35  2023-11-20 12:45:37   
138  43HpQpDjnc0LmIu  2024-04-08 09:50:22  2024-04-08 10:15:29   
141  mJUrRJria3Szapo  2024-04-19 09:42:46  2024-04-19 10:30:35   
157  MfTu2yewsNxvB7k  2024-06-08 11:45:00  2024-06-08 12:16:00   
166  MfTu2yewsNxvB7k  2024-07-08 09:24:27  2024-07-08 09:59:32   
215  VZuYtMoaMM5Nvea  2025-01-20 15:41:01  2025-01-20 16:00:29   
237  VZuYtMoaMM5Nvea  2025-05-22 10:17:59  2025-05-22 10:29:17   
244  MfTu2yewsNxvB7k  2025-07-03 11:03:03  2025-07-03 11:22:11   

                  ip  identificacao_dado tipo_envio  ano_referencia  \
85      189.17.52.98                 NaN   ORIGINAL            2023   
138   177.207.187.35                 NaN   ORIGINAL            2024   
141  186.248.197.178                 NaN   ORIGINAL            2024   
157     189.45.16.78                 NaN   ORIGINAL            2024   
166     189.45.16.78                 NaN   ORIGINAL            2024   
215    192.140.91.31                 NaN   ORIGINAL            2024   
237    177.22.125.93                 NaN   ORIGINAL            2025   
244     189.45.16.78                 NaN   ORIGINAL            2025   

    periodo_referencia  identificacao_estabelecimento  \
85               Julho                            NaN   
138              Março                            NaN   
141              Março                            NaN   
157               Maio                            NaN   
166              Junho                            NaN   
215           Dezembro                            NaN   
237              Abril                            NaN   
244              Junho                            NaN   

                       municipio  \
85   Teófilo Otoni, Minas Gerais   
138       Ipatinga, Minas Gerais   
141      Nova Lima, Minas Gerais   
157        Alfenas, Minas Gerais   
166        Alfenas, Minas Gerais   
215        Alfenas, Minas Gerais   
237        Alfenas, Minas Gerais   
244        Alfenas, Minas Gerais   

                            razao_social_nome_fantasia  \
85   Associação Hospitalar Santa Rosália - Hospital...   
138  Fundação São Francisco Xavier - Hospital Márci...   
141  Biocor Hospital de Doenças Cardiovasculares Lt...   
157  Fundação de Ensino e Tecnologia de Alfenas - H...   
166  Fundação de Ensino e Tecnologia de Alfenas - H...   
215  Casa de Caridade de Alfenas Nossa Senhora do P...   
237  Casa de Caridade de Alfenas Nossa Senhora do P...   
244  Fundação de Ensino e Tecnologia de Alfenas - H...   

                     razao_social_nome_fantasia_outros            cnpj  \
85                                                 NaN   2510490200107   
138                                                NaN  19878404000100   
141                                                NaN  20294088000109   
157  Nucleo Hemoterapico Hospital Universitario Alz...  17878554001241   
166                                                NaN  17878554001241   
215                                                NaN  16650756000116   
237                                                NaN  16650756000116   
244                                                NaN  17878554001241   

      tipo_estabelecimento natureza_estabelecimento  \
85


Amostra dos dados únicos (os mais recentes para cada chave):


id          data_envio  ultima_pagina idioma_inicial       semente  \
0   5 2023-04-14 16:05:33              4          pt-BR  3.992492e+08   
1  10 2023-04-18 12:22:00              4          pt-BR           NaN   
2  12 2023-04-18 12:52:00              4          pt-BR           NaN   
3  17 2023-04-26 12:27:00              4          pt-BR           NaN   
4  18 2023-04-26 13:02:01              4          pt-BR  1.780040e+09   
5  19 2023-04-26 17:05:53              4          pt-BR  1.061017e+09   
6  20 2023-04-27 12:48:29              4          pt-BR  3.356946e+08   
7  23 2023-05-05 15:13:37              4          pt-BR  1.756985e+09   
8  24 2023-05-05 15:41:16              4          pt-BR  2.073804e+09   
9  30 2023-05-09 12:17:46              4          pt-BR  2.073407e+09   

     codigo_acesso          data_inicio     data_ultima_acao            ip  \
0  IvycpvVQH6KQqkP  2023-04-14 15:05:11  2023-04-14 16:05:33  10.0.113.219   
1  MfTu2yewsNxvB7k  2023-04-18 11:29:00  2023-04-18 12:22:00     10.0.1.35   
2  MfTu2yewsNxvB7k  2023-04-18 12:26:00  2023-04-18 12:52:00    10.0.0.186   
3  MfTu2yewsNxvB7k  2023-04-26 11:49:00  2023-04-26 12:27:00    10.0.52.44   
4  MfTu2yewsNxvB7k  2023-04-26 12:32:51  2023-04-26 13:02:01    10.0.52.19   
5  mJUrRJria3Szapo  2023-04-26 15:44:37  2023-04-26 17:05:53     10.0.0.30   
6  MfTu2yewsNxvB7k  2023-04-27 12:25:21  2023-04-27 12:48:29     10.0.0.14   
7  IvycpvVQH6KQqkP  2023-05-05 14:45:07  2023-05-05 15:13:37   10.0.51.218   
8  IvycpvVQH6KQqkP  2023-05-05 15:21:15  2023-05-05 15:41:16   10.0.51.170   
9  MfTu2yewsNxvB7k  2023-05-09 10:47:53  2023-05-09 12:17:46    10.0.52.44   

   identificacao_dado tipo_envio  ano_referencia periodo_referencia  \
0                 NaN   ORIGINAL            2023              Março   
1                 NaN   ORIGINAL            2022            Janeiro   
2                 NaN   ORIGINAL            2022          Fevereiro   
3                 NaN   ORIGINAL            2023            Janeiro   
4                 NaN   ORIGINAL            2023          Fevereiro   
5                 NaN   ORIGINAL            2023              Março   
6                 NaN   ORIGINAL            2023              Março   
7                 NaN   ORIGINAL            2023            Janeiro   
8                 NaN   ORIGINAL            2023          Fevereiro   
9                 NaN   ORIGINAL            2023              Abril   

   identificacao_estabelecimento                     municipio  \
0                            NaN  Belo Horizonte, Minas Gerais   
1                            NaN         Alfenas, Minas Gerais   
2                            NaN         Alfenas, Minas Gerais   
3                            NaN         Alfenas, Minas Gerais   
4                            NaN         Alfenas, Minas Gerais   
5                            NaN       Nova Lima, Minas Gerais   
6                            NaN         Alfenas, Minas Gerais   
7                            NaN  Belo Horizonte, Minas Gerais   
8                            NaN  Belo Horizonte, Minas Gerais   
9                            NaN         Alfenas, Minas Gerais   

                          razao_social_nome_fantasia  \
0          Vita Hemoterapia Ltda - Vita Hemoterapia    
1  Fundação de Ensino e Tecnologia de Alfenas - H...   
2  Fundação de Ensino e Tecnologia de Alfenas - H...   
3  Fundação de Ensino e Tecnologia de Alfenas - H...   
4  Fundação de Ensino e Tecnologia de Alfenas - H...   
5  Biocor Hospital de Doenças Cardiovasculares Lt...   
6  Fundação de Ensino e Tecnologia de Alfenas - H...   
7          Vita Hemoterapia Ltda - Vita Hemoterapia    
8          Vita Hemoterapia Ltda - Vita Hemoterapia    
9  Fundação de Ensino e Tecnologia de Alfenas - H...   

                   razao_social_nome_fantasia_outros            cnpj  \
0                                                NaN  25463423000179   
1  Hospital Universitário Alzira Velano-Banco de ...  17878554001241  

In [114]:
hemoprod_mg_deduplicado.to_excel('dados_processados/hemoprod_mg.xlsx', index=False)

## Hemoprod Mato Grosso do Sul

In [ ]:
import os
import pandas as pd

dados_brutos_path = 'dados_brutos'

arquivo_dados_path = os.path.join(dados_brutos_path, 'Hemoprod_MS.xlsx')
nome_planilha = 'HEMOPROD - MATOGROSSODOSUL'

dicionario_path_ms = ('./dicionario_colunas_270.xlsx')
# dicionario_path_ap = ('./dicionario_colunas_270.xlsx')

dicionario_ms = pd.read_excel(dicionario_path_ms, sheet_name='Sheet1')

# --- 2. Carregue os dados e o dicionário ---
try:
    # Carrega o arquivo de dados
    hemoprod_ms = pd.read_excel(arquivo_dados_path, sheet_name=nome_planilha)
    print("Arquivo de dados carregado com sucesso.")
    print(f"Número de colunas original: {len(hemoprod_ms.columns)}")

    # Carrega o arquivo de dicionário
    dicionario = pd.read_excel(dicionario_path_ms)
    print("Arquivo de dicionário carregado com sucesso.")

    # --- 3. Extraia a lista de novos nomes ---
    # Pega os valores da coluna 'nome_sql' e converte para uma lista
    novos_nomes = dicionario['nome_sql'].tolist()
    print(f"Número de novos nomes no dicionário: {len(novos_nomes)}")

    # --- 4. Verificação de segurança (MUITO IMPORTANTE) ---
    # Garante que o número de colunas é o mesmo antes de renomear
    if len(hemoprod_ms.columns) == len(novos_nomes):
        print("\nO número de colunas corresponde. Renomeando...")
        
        # --- 5. Substitua os nomes das colunas ---
        # Esta é a linha principal que faz a substituição direta
        hemoprod_ms.columns = novos_nomes
        
        print("Colunas renomeadas com sucesso!")
        
        # --- 6. Verifique o resultado ---
        print("\nInformações do DataFrame com as novas colunas:")
        hemoprod_ms.info()
        
        print("\nAs 5 primeiras linhas com as novas colunas:")
        display(hemoprod_ms.head())

    else:
        # Mensagem de erro se o número de colunas for diferente
        print("\n--- ERRO ---")
        print("A renomeação foi cancelada. O número de colunas no arquivo de dados não é igual ao número de nomes no dicionário.")
        print(f"Colunas no arquivo de dados: {len(hemoprod_ms.columns)}")
        print(f"Nomes no dicionário: {len(novos_nomes)}")

except FileNotFoundError as e:
    print(f"\nErro de arquivo não encontrado: {e}")
except KeyError as e:
    print(f"\nErro de coluna não encontrada: {e}. Verifique se a coluna 'nome_sql' existe no seu arquivo de dicionário.")
except Exception as e:
    print(f"\nOcorreu um erro inesperado: {e}")



Arquivo de dados carregado com sucesso.
Número de colunas original: 269
Arquivo de dicionário carregado com sucesso.
Número de novos nomes no dicionário: 270

--- ERRO ---
A renomeação foi cancelada. O número de colunas no arquivo de dados não é igual ao número de nomes no dicionário.
Colunas no arquivo de dados: 269
Nomes no dicionário: 270


In [6]:

arquivo_dados_path = os.path.join(dados_brutos_path, 'Hemoprod_AM.xlsx')
nome_planilha = 'HEMOPROD - AMAZONAS'
hemoprod_ce1 = pd.read_excel(arquivo_dados_path, sheet_name=nome_planilha)

colunas_padrao = set(hemoprod_ce1.columns)
colunas_estado = set(hemoprod_ms.columns)

colunas_faltantes = list(colunas_padrao - colunas_estado)

colunas_a_mais = list(colunas_estado - colunas_padrao)

print(f"Número de colunas faltantes: {len(colunas_faltantes)}")
print(f"Colunas faltantes (a serem adicionadas): {colunas_faltantes}")
print("-" * 30)
print(f"Número de colunas a mais: {len(colunas_a_mais)}")
print(f"Colunas a mais (a serem dropadas): {colunas_a_mais}")

Número de colunas faltantes: 3
Colunas faltantes (a serem adicionadas): ['Os dados informados referem-se à um(a): ', 'Cite os estabelecimentos que compõem a rede  Informe o Tipo de Estabelecimento, o Nome Fantasia\xa0e o Município de localização de cada um. ', 'Ano de referência ']
------------------------------
Número de colunas a mais: 2
Colunas a mais (a serem dropadas): ['Município [Outros]', 'Período de referência [Outros]']


## Analisando o auto exclusao


In [1]:
import pandas as pd
import os

# 1. Definir o caminho do arquivo
parquet_path = "dados_processados/base_nacional.parquet"
coluna_alvo = "descarte_bolsas_total_bolsas_descartadas_auto_exclusao"

# 2. Verificar se o arquivo existe antes de tentar carregar
if not os.path.exists(parquet_path):
    print(f"Erro: Arquivo não encontrado no caminho: {parquet_path}")
else:
    try:
        # 3. Carregar o DataFrame do arquivo Parquet
        # O pandas usa o pyarrow ou fastparquet internamente para ler o .parquet
        df = pd.read_parquet(parquet_path)
        print(f"DataFrame carregado com sucesso. Total de linhas: {len(df)}")
        
        # 4. Verificar se a coluna existe no DataFrame
        if coluna_alvo in df.columns:
            # 5. Calcular a soma da coluna
            total_descarte = df[coluna_alvo].sum()
            
            # 6. Exibir o resultado formatado
            # O f-string com ":," formata o número com separador de milhar
            print("\n--- Resultado ---")
            print(f"Soma total de '{coluna_alvo}':")
            print(f"-> {int(total_descarte):,}")
            
        else:
            print(f"\nErro: A coluna '{coluna_alvo}' não foi encontrada no arquivo Parquet.")
            print(f"Colunas disponíveis: {df.columns.tolist()}")

    except Exception as e:
        print(f"Ocorreu um erro ao carregar o arquivo Parquet: {e}")

DataFrame carregado com sucesso. Total de linhas: 15865

--- Resultado ---
Soma total de 'descarte_bolsas_total_bolsas_descartadas_auto_exclusao':
-> 20,579


In [2]:
import pandas as pd
import os

# 1. Defina o caminho do arquivo Parquet
# Certifique-se de que este caminho está correto em relação ao seu notebook.
parquet_path = "dados_processados/base_nacional.parquet"
coluna_municipio = "municipio"
coluna_descarte = "descarte_bolsas_total_bolsas_descartadas_auto_exclusao"

# 2. Verificar se o arquivo existe e carregar
if not os.path.exists(parquet_path):
    print(f"ERRO: Arquivo não encontrado no caminho: {parquet_path}")
    print("Verifique se o caminho está correto ou se o arquivo foi gerado.")
else:
    try:
        # Carregar o DataFrame
        df = pd.read_parquet(parquet_path)
        print(f"DataFrame carregado com sucesso. Total de linhas: {len(df):,}")

        # 3. Verificar a existência das colunas
        if coluna_municipio in df.columns and coluna_descarte in df.columns:
            
            # 4. Agrupar por Município e somar o total de descartes
            # O .fillna(0) garante que valores nulos não atrapalhem a soma.
            df_analise = (
                df.groupby(coluna_municipio)[coluna_descarte]
                .sum()
                .fillna(0) 
                .sort_values(ascending=False)
            )

            # 5. Selecionar o Top 50
            top_50_municipios = df_analise.head(50)

            # 6. Exibir o resultado
            print("\n--- TOP 50 Municípios por Total de Bolsas Descartadas ---")
            
            # Usando to_frame() e reset_index() para uma exibição formatada
            df_resultado = top_50_municipios.to_frame().reset_index()
            
            # Renomear coluna para clareza
            df_resultado.columns = ["Município", "Total Bolsas Descartadas"]
            
            # Formatação opcional para melhor visualização no notebook
            pd.options.display.float_format = '{:,.0f}'.format
            
            # Exibe a tabela no Jupyter/Pandas
            display(df_resultado)

        else:
            print("\nERRO: Uma ou ambas as colunas necessárias não foram encontradas no DataFrame.")
            print(f"Esperadas: '{coluna_municipio}' e '{coluna_descarte}'")
            
    except Exception as e:
        print(f"Ocorreu um erro ao carregar ou processar o arquivo Parquet: {e}")

DataFrame carregado com sucesso. Total de linhas: 15,865

--- TOP 50 Municípios por Total de Bolsas Descartadas ---


Município  Total Bolsas Descartadas
0       Não se aplica                     10083
1            Curitiba                      1472
2        Campo Grande                      1003
3             Goiânia                       578
4               Natal                       536
5             Vitória                       491
6         João Pessoa                       445
7              Manaus                       363
8             Maringá                       321
9               Belém                       312
10          Fortaleza                       299
11  Cornélio Procópio                       280
12      Florianópolis                       240
13          Boa Vista                       239
14             Macapá                       216
15             Palmas                       196
16          Tramandaí                       191
17        Porto Velho                       168
18            Lajeado                       168
19          Joinville                       141
20            Pelotas                       135
21            Chapecó                       119
22      Foz do Iguaçu                       115
23           Cascavel                       114
24           Parnaíba                       113
25           Londrina                       110
26       Porto Alegre                       106
27          Apucarana                       103
28             Marabá                        97
29           Blumenau                        96
30           Salvador                        96
31        Três Lagoas                        92
32            Mossoró                        85
33             Cuiabá                        77
34             Gurupi                        75
35          Rio Verde                        69
36       Ponta Grossa                        66
37              Caicó                        64
38            Camaquã                        62
39     Porto Nacional                        56
40           Capanema                        56
41              Lages                        47
42              Juína                        45
43          Castanhal                        45
44            Alfenas                        42
45        Passo Fundo                        38
46           Dourados                        37
47      Caxias do Sul                        30
48     Augustinópolis                        30
49             Recife                        30

In [6]:
import pandas as pd
import os

# 1. Defina o caminho do arquivo Parquet
# Certifique-se de que este caminho está correto em relação ao seu notebook.
parquet_path = "dados_processados/base_nacional.parquet"

# 2. Definir as colunas de análise
coluna_municipio = "municipio"
colunas_de_soma = [
    "total_coletas_sangue_total",
]

# 3. Verificar se o arquivo existe e carregar
if not os.path.exists(parquet_path):
    print(f"ERRO: Arquivo não encontrado no caminho: {parquet_path}")
    print("Verifique se o caminho está correto ou se o arquivo foi gerado.")
else:
    try:
        # Carregar o DataFrame
        # O argumento columns= otimiza a leitura lendo apenas as colunas necessárias + a coluna de agrupamento
        cols_to_load = [coluna_municipio] + colunas_de_soma
        df = pd.read_parquet(parquet_path, columns=cols_to_load)
        print(f"DataFrame carregado com sucesso. Total de linhas: {len(df):,}")

        # 4. Agrupar por Município e somar as colunas
        agg_functions = {col: "sum" for col in colunas_de_soma}
        
        municipio_stats = (
            df.groupby(coluna_municipio)
            .agg(agg_functions)
            .fillna(0) # Trata possíveis valores nulos nas colunas de soma
            .reset_index()
        )

        # 5. Calcular a coluna "Total Coletas" (como no seu código Streamlit)
        municipio_stats["Total Coletas"] = (
            municipio_stats["total_coletas_sangue_total"]
        )
        
        # 6. Ordenar e selecionar o Top 50
        municipio_stats = municipio_stats.sort_values("Total Coletas", ascending=False)
        top_50_municipios = municipio_stats.head(5)

        # 7. Exibir o resultado
        print("\n--- TOP 50 Municípios por Total de Coletas (Sangue Total + Aférese) ---")
        
        # Formatação opcional para melhor visualização dos números no notebook
        pd.options.display.float_format = '{:,.0f}'.format
        
        # Exibe a tabela no Jupyter/Pandas
        display(top_50_municipios)

    except Exception as e:
        print(f"Ocorreu um erro ao carregar ou processar o arquivo Parquet: {e}")

DataFrame carregado com sucesso. Total de linhas: 15,865

--- TOP 50 Municípios por Total de Coletas (Sangue Total + Aférese) ---


municipio  total_coletas_sangue_total  Total Coletas
234  Não se aplica                     2832656        2832656
112       Curitiba                      427623         427623
140      Fortaleza                      339609         339609
294         Recife                      281227         281227
398        Vitória                      246585         246585